In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
from sklearn.preprocessing import StandardScaler

from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import StratifiedKFold
from pycaret.regression import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from sklearn.impute import KNNImputer

In [2]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

# Data

In [111]:
train_data = pd.read_csv("./train.csv")
train_data

PRODUCT_ID  Y_Class  Y_Quality         TIMESTAMP     LINE PRODUCT_CODE  \
0    TRAIN_000        1   0.533433   2022-06-13 5:14  T050304         A_31   
1    TRAIN_001        2   0.541819   2022-06-13 5:22  T050307         A_31   
2    TRAIN_002        1   0.531267   2022-06-13 5:30  T050304         A_31   
3    TRAIN_003        2   0.537325   2022-06-13 5:39  T050307         A_31   
4    TRAIN_004        1   0.531590   2022-06-13 5:47  T050304         A_31   
..         ...      ...        ...               ...      ...          ...   
593  TRAIN_593        1   0.526546  2022-09-08 14:30  T100306         T_31   
594  TRAIN_594        0   0.524022  2022-09-08 22:38  T050304         A_31   
595  TRAIN_595        0   0.521289  2022-09-08 22:47  T050304         A_31   
596  TRAIN_596        1   0.531375  2022-09-08 14:38  T100304         O_31   
597  TRAIN_597        1   0.533702  2022-09-08 14:46  T100306         O_31   

      X_1   X_2  X_3   X_4  ...  X_2866  X_2867  X_2868  X_2869  X_2870  \
0     NaN   NaN  NaN   NaN  ...   39.34   40.89   32.56   34.09   77.77   
1     NaN   NaN  NaN   NaN  ...   38.89   42.82   43.92   35.34   72.55   
2     NaN   NaN  NaN   NaN  ...   39.19   36.65   42.47   36.53   78.35   
3     NaN   NaN  NaN   NaN  ...   37.74   39.17   52.17   30.58   71.78   
4     NaN   NaN  NaN   NaN  ...   38.70   41.89   46.93   33.09   76.97   
..    ...   ...  ...   ...  ...     ...     ...     ...     ...     ...   
593   2.0  95.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   
594   NaN   NaN  NaN   NaN  ...   49.47   53.07   50.89   55.10   66.49   
595   NaN   NaN  NaN   NaN  ...     NaN     NaN     NaN     NaN     NaN   
596  40.0  94.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   
597  21.0  87.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   

     X_2871  X_2872  X_2873  X_2874  X_2875  
0       NaN     NaN     NaN     NaN     NaN  
1       NaN     NaN     NaN     NaN     NaN  
2       NaN     NaN     NaN     NaN     NaN  
3       NaN     NaN     NaN     NaN     NaN  
4       NaN     NaN     NaN     NaN     NaN  
..      ...     ...     ...     ...     ...  
593     NaN     NaN     NaN     NaN     NaN  
594     1.0     NaN     NaN     NaN     NaN  
595     1.0     NaN     NaN     NaN     NaN  
596     NaN     NaN     NaN     NaN     NaN  
597     NaN     NaN     NaN     NaN     NaN  

[598 rows x 2881 columns]

In [112]:
train_data['YEAR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.year
train_data['MONTH'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.month
train_data['DAY'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day
train_data['HOUR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.hour
train_data['MINUTE'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.minute
train_data['DAY_OF_WEEK'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day_name()

In [113]:
train_data = train_data.drop(['MONTH', 'DAY', 'YEAR'], axis = 1)

In [114]:
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T010305'),'LINE_AND_CODE'] = 0
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T010306'),'LINE_AND_CODE'] = 1
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T050304'),'LINE_AND_CODE'] = 2
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T050307'),'LINE_AND_CODE'] = 3
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T100304'),'LINE_AND_CODE'] = 4
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T100306'),'LINE_AND_CODE'] = 5

train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T010305'),'LINE_AND_CODE'] = 6
train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T010306'),'LINE_AND_CODE'] = 7
train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T050304'),'LINE_AND_CODE'] = 8
train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T050307'),'LINE_AND_CODE'] = 9
train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T100304'),'LINE_AND_CODE'] = 10
train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T100306'),'LINE_AND_CODE'] = 11

train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T010305'),'LINE_AND_CODE'] = 12
train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T010306'),'LINE_AND_CODE'] = 13
train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T050304'),'LINE_AND_CODE'] = 14
train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T050307'),'LINE_AND_CODE'] = 15
train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T100304'),'LINE_AND_CODE'] = 16
train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T100306'),'LINE_AND_CODE'] = 17
train_data

PRODUCT_ID  Y_Class  Y_Quality         TIMESTAMP     LINE PRODUCT_CODE  \
0    TRAIN_000        1   0.533433   2022-06-13 5:14  T050304         A_31   
1    TRAIN_001        2   0.541819   2022-06-13 5:22  T050307         A_31   
2    TRAIN_002        1   0.531267   2022-06-13 5:30  T050304         A_31   
3    TRAIN_003        2   0.537325   2022-06-13 5:39  T050307         A_31   
4    TRAIN_004        1   0.531590   2022-06-13 5:47  T050304         A_31   
..         ...      ...        ...               ...      ...          ...   
593  TRAIN_593        1   0.526546  2022-09-08 14:30  T100306         T_31   
594  TRAIN_594        0   0.524022  2022-09-08 22:38  T050304         A_31   
595  TRAIN_595        0   0.521289  2022-09-08 22:47  T050304         A_31   
596  TRAIN_596        1   0.531375  2022-09-08 14:38  T100304         O_31   
597  TRAIN_597        1   0.533702  2022-09-08 14:46  T100306         O_31   

      X_1   X_2  X_3   X_4  ...  X_2870  X_2871  X_2872  X_2873  X_2874  \
0     NaN   NaN  NaN   NaN  ...   77.77     NaN     NaN     NaN     NaN   
1     NaN   NaN  NaN   NaN  ...   72.55     NaN     NaN     NaN     NaN   
2     NaN   NaN  NaN   NaN  ...   78.35     NaN     NaN     NaN     NaN   
3     NaN   NaN  NaN   NaN  ...   71.78     NaN     NaN     NaN     NaN   
4     NaN   NaN  NaN   NaN  ...   76.97     NaN     NaN     NaN     NaN   
..    ...   ...  ...   ...  ...     ...     ...     ...     ...     ...   
593   2.0  95.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   
594   NaN   NaN  NaN   NaN  ...   66.49     1.0     NaN     NaN     NaN   
595   NaN   NaN  NaN   NaN  ...     NaN     1.0     NaN     NaN     NaN   
596  40.0  94.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   
597  21.0  87.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   

     X_2875  HOUR  MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0       NaN     5      14       Monday            2.0  
1       NaN     5      22       Monday            3.0  
2       NaN     5      30       Monday            2.0  
3       NaN     5      39       Monday            3.0  
4       NaN     5      47       Monday            2.0  
..      ...   ...     ...          ...            ...  
593     NaN    14      30     Thursday           11.0  
594     NaN    22      38     Thursday            2.0  
595     NaN    22      47     Thursday            2.0  
596     NaN    14      38     Thursday           16.0  
597     NaN    14      46     Thursday           17.0  

[598 rows x 2885 columns]

In [115]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

82


In [116]:
train_data.drop(colls, inplace = True, axis = 1)

In [117]:
train_data.loc[train_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
train_data.loc[train_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
train_data.loc[train_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

train_data.drop(['PRODUCT_ID', 'TIMESTAMP', 'PRODUCT_CODE'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality     LINE   X_1   X_2  X_3   X_4   X_5  X_6   X_7  ...  \
0          1   0.533433  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
1          2   0.541819  T050307   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
2          1   0.531267  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
3          2   0.537325  T050307   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
4          1   0.531590  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
..       ...        ...      ...   ...   ...  ...   ...   ...  ...   ...  ...   
593        1   0.526546  T100306   2.0  95.0  0.0  45.0  10.0  0.0  50.0  ...   
594        0   0.524022  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
595        0   0.521289  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
596        1   0.531375  T100304  40.0  94.0  0.0  45.0  11.0  0.0  45.0  ...   
597        1   0.533702  T100306  21.0  87.0  0.0  45.0  10.0  0.0  61.0  ...   

     X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  MINUTE  \
0     39.34   40.89   32.56   34.09   77.77     NaN     5      14   
1     38.89   42.82   43.92   35.34   72.55     NaN     5      22   
2     39.19   36.65   42.47   36.53   78.35     NaN     5      30   
3     37.74   39.17   52.17   30.58   71.78     NaN     5      39   
4     38.70   41.89   46.93   33.09   76.97     NaN     5      47   
..      ...     ...     ...     ...     ...     ...   ...     ...   
593     NaN     NaN     NaN     NaN     NaN     NaN    14      30   
594   49.47   53.07   50.89   55.10   66.49     1.0    22      38   
595     NaN     NaN     NaN     NaN     NaN     1.0    22      47   
596     NaN     NaN     NaN     NaN     NaN     NaN    14      38   
597     NaN     NaN     NaN     NaN     NaN     NaN    14      46   

     DAY_OF_WEEK  LINE_AND_CODE  
0              1            2.0  
1              1            3.0  
2              1            2.0  
3              1            3.0  
4              1            2.0  
..           ...            ...  
593            4           11.0  
594            4            2.0  
595            4            2.0  
596            4           16.0  
597            4           17.0  

[598 rows x 2800 columns]

In [118]:
T050304 = train_data[train_data['LINE'] == 'T050304']
T050307 = train_data[train_data['LINE'] == 'T050307']
T010305 = train_data[train_data['LINE'] == 'T010305']
T010306 = train_data[train_data['LINE'] == 'T010306']
T100304 = train_data[train_data['LINE'] == 'T100304']
T100306 = train_data[train_data['LINE'] == 'T100306']

In [119]:
T050304.drop(['LINE'], axis = 1, inplace = True)
T050307.drop(['LINE'], axis = 1, inplace = True)
T010305.drop(['LINE'], axis = 1, inplace = True)
T010306.drop(['LINE'], axis = 1, inplace = True)
T100304.drop(['LINE'], axis = 1, inplace = True)
T100306.drop(['LINE'], axis = 1, inplace = True)

In [120]:
T050304_col = []
for col in T050304 :
    if 'X' in col and T050304[col].isna().sum() == len(T050304) :
        T050304_col.append(col)
print(len(T050304_col))

T050304.drop(T050304_col, inplace = True, axis = 1)

825


In [121]:
T050307_col = []
for col in T050307 :
    if 'X' in col and T050307[col].isna().sum() == len(T050307) :
        T050307_col.append(col)
print(len(T050307_col))

T050307.drop(T050307_col, inplace = True, axis = 1)

818


In [122]:
T010305_col = []
for col in T010305 :
    if 'X' in col and T010305[col].isna().sum() == len(T010305) :
        T010305_col.append(col)
print(len(T010305_col))

T010305.drop(T010305_col, inplace = True, axis = 1)

1907


In [123]:
T010306_col = []
for col in T010306 :
    if 'X' in col and T010306[col].isna().sum() == len(T010306) :
        T010306_col.append(col)
print(len(T010306_col))

T010306.drop(T010306_col, inplace = True, axis = 1)

1907


In [124]:
T100304_col = []
for col in T100304 :
    if 'X' in col and T100304[col].isna().sum() == len(T100304) :
        T100304_col.append(col)
print(len(T100304_col))

T100304.drop(T100304_col, inplace = True, axis = 1)

2122


In [125]:
T100306_col = []
for col in T100306 :
    if 'X' in col and T100306[col].isna().sum() == len(T100306) :
        T100306_col.append(col)
print(len(T100306_col))

T100306.drop(T100306_col, inplace = True, axis = 1)

2122


In [126]:
T051 = list(set(T050307_col)-set(T050304_col))
T052 = list(set(T050304_col)-set(T050307_col))
T5drop = T051 + T052

T011 = list(set(T010305_col)-set(T010306_col))
T012 = list(set(T010306_col)-set(T010305_col))
T0drop = T011 + T012

T101 = list(set(T100304_col)-set(T100306_col))
T102 = list(set(T100306_col)-set(T100304_col))
T1drop = T101 + T102

In [127]:
T05 = pd.concat([T050304, T050307])
T01 = pd.concat([T010305, T010306])
T10 = pd.concat([T100304, T100306])

In [128]:
T05.drop(T5drop, inplace = True, axis = 1)
T01.drop(T0drop, inplace = True, axis = 1)
T10.drop(T1drop, inplace = True, axis = 1)

In [129]:
T05 = T05.fillna(0)
T01 = T01.fillna(0)
T10 = T10.fillna(0)

# T05

In [130]:
T05_class = T05['Y_Class']
T05_target = T05['Y_Quality']
T05_data = T05.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [47]:
T_05c = T05_data.columns
T_05scaler = MinMaxScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)
T05_data

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
0      0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.554348   
1      0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.570652   
2      0.5    0.0    0.0    0.0  0.232779  0.232779  0.228944  0.559783   
3      0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.563406   
4      0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.561594   
..     ...    ...    ...    ...       ...       ...       ...       ...   
115    0.5    0.0    0.5    0.0  0.058195  0.058195  0.058126  0.217391   
116    0.5    0.0    0.5    0.0  0.059382  0.059382  0.059312  0.217391   
117    0.5    0.0    0.5    0.0  0.061758  0.061758  0.061684  0.219203   
118    0.5    0.0    0.5    0.0  0.061758  0.061758  0.061684  0.222826   
119    0.5    0.0    0.5    0.0  0.065321  0.065321  0.065243  0.206522   

        X_140     X_141  X_142  X_143     X_144  X_145     X_146  X_147  \
0    0.520906  0.639640    0.0    0.0  0.666667    0.0  0.892914    0.0   
1    0.529617  0.711712    0.0    0.0  1.000000    0.0  0.980288    0.0   
2    0.524390  0.621622    0.0    0.0  0.666667    0.0  0.839638    0.0   
3    0.524390  0.338481    0.0    0.0  0.333333    0.0  0.258924    0.0   
4    0.522648  0.698842    0.0    0.0  1.000000    0.0  0.972829    0.0   
..        ...       ...    ...    ...       ...    ...       ...    ...   
115  0.202091  0.411840    0.0    0.0  1.000000    0.0  0.950986    0.0   
116  0.198606  0.404118    0.0    0.0  0.666667    0.0  0.917954    0.0   
117  0.200348  0.462033    0.0    0.0  1.000000    0.0  0.988812    0.0   
118  0.203833  0.406692    0.0    0.0  1.000000    0.0  0.917954    0.0   
119  0.203833  0.321750    0.0    0.0  0.666667    0.0  0.758657    0.0   

        X_148     X_149     X_150  X_151  X_152  X_153  X_154  X_155  X_156  \
0    0.414634  0.365854  0.452381    0.0    0.5    1.0    0.0    1.0    0.5   
1    0.390244  0.341463  0.428571    0.0    0.5    0.5    0.0    1.0    0.5   
2    0.414634  0.341463  0.452381    1.0    0.5    0.5    0.0    1.0    1.0   
3    0.414634  0.341463  0.428571    1.0    1.0    1.0    0.0    0.0    0.5   
4    0.414634  0.341463  0.452381    1.0    0.5    1.0    0.0    1.0    0.5   
..        ...       ...       ...    ...    ...    ...    ...    ...    ...   
115  0.756098  0.731707  0.761905    0.0    0.5    0.0    0.0    1.0    0.5   
116  0.756098  0.731707  0.761905    1.0    0.5    1.0    0.0    1.0    0.5   
117  0.756098  0.731707  0.761905    0.0    0.5    0.5    0.0    0.0    0.5   
118  0.756098  0.731707  0.761905    0.0    0.0    0.5    0.0    1.0    0.5   
119  0.780488  0.756098  0.761905    1.0    0.5    1.0    0.0    0.0    0.5   

     X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  \
0      0.5    0.0    0.0    0.0    0.5    0.0    0.0    0.0    0.0    0.0   
1      0.5    0.0    1.0    0.0    0.5    0.0    0.0    0.0    0.0    0.0   
2      1.0    0.0    0.0    0.0    0.5    0.0    1.0    1.0    1.0    0.0   
3      0.5    0.0    1.0    0.0    0.5    0.0    1.0    0.0    0.0    0.0   
4      0.5    0.0    1.0    0.0    0.5    0.0    1.0    1.0    1.0    0.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
115    0.5    0.0    0.0    0.0    0.5    0.0    0.0    0.0    0.0    0.0   
116    0.5    0.0    1.0    0.0    0.5    0.0    1.0    1.0    1.0    0.0   
117    0.5    0.0    0.0    0.0    0.5    0.0    1.0    0.0    1.0    0.0   
118    0.0    0.0    0.0    1.0    0.5    0.0    0.0    0.0    0.0    0.0   
119    0.5    0.0    1.0    1.0    0.5    0.0    1.0    0.0    1.0    0.0   

     X_167  X_168  X_169  X_170  X_171  X_172  X_173  X_174  X_175  X_176  \
0      0.0    0.5    1.0    0.0    1.0    0.0    0.5    0.0    0.0    0.0   
1      0.0    0.5    1.0    0.0    0.0    0.0    0.5    0.0    0.0    0.0   
2      0.0    0.5    1.0    0.0    0.0    0.0    0.5    0.0    0.0    0.0   
3      1.0    0.5    

In [48]:
T05_y_class = pd.DataFrame(T05_target, columns = ['Y_Quality'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_data = pd.concat([T05_data, T05_y_class], axis = 1)
T05_data = T05_data.set_index('index')
T05_data.drop(['Y_Quality'], axis = 1, inplace = True)
T05_data

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
index                                                                       
0        0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.554348   
2        0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.570652   
4        0.5    0.0    0.0    0.0  0.232779  0.232779  0.228944  0.559783   
6        0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.563406   
8        0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.561594   
...      ...    ...    ...    ...       ...       ...       ...       ...   
549      0.5    0.0    0.5    0.0  0.058195  0.058195  0.058126  0.217391   
550      0.5    0.0    0.5    0.0  0.059382  0.059382  0.059312  0.217391   
551      0.5    0.0    0.5    0.0  0.061758  0.061758  0.061684  0.219203   
552      0.5    0.0    0.5    0.0  0.061758  0.061758  0.061684  0.222826   
555      0.5    0.0    0.5    0.0  0.065321  0.065321  0.065243  0.206522   

          X_140     X_141  X_142  X_143     X_144  X_145     X_146  X_147  \
index                                                                       
0      0.520906  0.639640    0.0    0.0  0.666667    0.0  0.892914    0.0   
2      0.529617  0.711712    0.0    0.0  1.000000    0.0  0.980288    0.0   
4      0.524390  0.621622    0.0    0.0  0.666667    0.0  0.839638    0.0   
6      0.524390  0.338481    0.0    0.0  0.333333    0.0  0.258924    0.0   
8      0.522648  0.698842    0.0    0.0  1.000000    0.0  0.972829    0.0   
...         ...       ...    ...    ...       ...    ...       ...    ...   
549    0.202091  0.411840    0.0    0.0  1.000000    0.0  0.950986    0.0   
550    0.198606  0.404118    0.0    0.0  0.666667    0.0  0.917954    0.0   
551    0.200348  0.462033    0.0    0.0  1.000000    0.0  0.988812    0.0   
552    0.203833  0.406692    0.0    0.0  1.000000    0.0  0.917954    0.0   
555    0.203833  0.321750    0.0    0.0  0.666667    0.0  0.758657    0.0   

          X_148     X_149     X_150  X_151  X_152  X_153  X_154  X_155  X_156  \
index                                                                           
0      0.414634  0.365854  0.452381    0.0    0.5    1.0    0.0    1.0    0.5   
2      0.390244  0.341463  0.428571    0.0    0.5    0.5    0.0    1.0    0.5   
4      0.414634  0.341463  0.452381    1.0    0.5    0.5    0.0    1.0    1.0   
6      0.414634  0.341463  0.428571    1.0    1.0    1.0    0.0    0.0    0.5   
8      0.414634  0.341463  0.452381    1.0    0.5    1.0    0.0    1.0    0.5   
...         ...       ...       ...    ...    ...    ...    ...    ...    ...   
549    0.756098  0.731707  0.761905    0.0    0.5    0.0    0.0    1.0    0.5   
550    0.756098  0.731707  0.761905    1.0    0.5    1.0    0.0    1.0    0.5   
551    0.756098  0.731707  0.761905    0.0    0.5    0.5    0.0    0.0    0.5   
552    0.756098  0.731707  0.761905    0.0    0.0    0.5    0.0    1.0    0.5   
555    0.780488  0.756098  0.761905    1.0    0.5    1.0    0.0    0.0    0.5   

       X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  \
index                                                                         
0        0.5    0.0    0.0    0.0    0.5    0.0    0.0    0.0    0.0    0.0   
2        0.5    0.0    1.0    0.0    0.5    0.0    0.0    0.0    0.0    0.0   
4        1.0    0.0    0.0    0.0    0.5    0.0    1.0    1.0    1.0    0.0   
6        0.5    0.0    1.0    0.0    0.5    0.0    1.0    0.0    0.0    0.0   
8        0.5    0.0    1.0    0.0    0.5    0.0    1.0    1.0    1.0    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
549      0.5    0.0    0.0    0.0    0.5    0.0    0.0    0.0    0.0    0.0   
550      0.5    0.0    1.0    0.0    0.5    0.0    1.0    1.0    1.0    0.0   
551      0.5    0.0    0.0    0.0    0.5    0.0    1.0    0.0    1.0    0.0   
552      0.0    0.0    0.0    1.0    0.5    0.0    0.0    0.0    0.0    0.0   
5

In [49]:
#13
setup_rgs = setup(data = T05_data, target = T05_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [50]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbr = create_model('gbr', fold = 5)
T05_total_models.append(T05_model_gbr)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [51]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbr = tune_model(T05_model_gbr, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [52]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbr, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]
T05_tuned_models

[LGBMRegressor(random_state=414),
 RandomForestRegressor(n_jobs=-1, random_state=414),
 GradientBoostingRegressor(random_state=414),
 ExtraTreesRegressor(n_jobs=-1, random_state=414),
 XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, predictor='auto', random_state=414,
              reg_alpha=0, reg_lambda=1, ...),
 AdaBoostRegressor(learning_rate=0.05, n_estimators=290, random_state=414)]

In [53]:
for model in T05_tuned_models:
    display(predict_model(model))

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     1.0    1.0    1.0    0.0  0.560570  0.554632  0.559905  0.684783   
85     1.0    1.0    0.5    0.0  0.729216  0.729216  0.728351  0.536232   
86     0.5    0.0    0.5    0.0  0.232779  0.232779  0.232503  0.568841   
87     0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.027174   
88     1.0    1.0    1.0    0.0  0.615202  0.615202  0.614472  0.625000   
89     0.5    1.0    0.5    0.0  0.925178  0.925178  0.924081  0.869565   
90     1.0    1.0    1.0    0.0  0.875297  0.875297  0.874259  0.811594   
91     1.0    1.0    1.0    0.0  0.640143  0.640143  0.639383  0.653986   
92     1.0    1.0    1.0    0.0  1.000000  1.000000  1.000000  0.914855   
93     1.0    1.0    1.0    0.0  0.813539  0.813539  0.813760  0.771739   
94     0.5    0.0    0.0    0.0  0.262470  0.262470  0.258600  0.565217   
95     1.0    1.0    1.0    0.0  0.793349  0.793349  0.792408  0.733696   
96     0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.570652   
97     0.5    0.0    0.5    0.0  0.166271  0.166271  0.166074  0.490942   
98     1.0    1.0    1.0    0.0  0.495249  0.497625  0.497034  0.501812   
99     1.0    1.0    1.0    0.0  0.944181  0.944181  0.944247  0.811594   
100    1.0    1.0    1.0    0.0  0.173397  0.175772  0.175563  0.275362   
101    1.0    1.0    1.0    0.0  0.514252  0.514252  0.513642  0.556159   
102    0.5    1.0    0.5    0.0  0.021378  0.023753  0.023725  0.143116   
103    0.5    0.0    0.5    0.0  0.059382  0.059382  0.059312  0.217391   
104    1.0    1.0    1.0    0.0  0.108076  0.108076  0.107948  0.344203   
105    0.5    0.0    0.5    0.0  0.065321  0.065321  0.065243  0.206522   
106    0.5    0.0    0.5    0.0  0.235154  0.235154  0.234875  0.574275   
107    1.0    1.0    1.0    0.0  0.453682  0.453682  0.453144  0.670290   
108    1.0    1.0    0.5    0.0  0.505938  0.505938  0.505338  0.525362   
109    1.0    1.0    1.0    0.0  0.166271  0.166271  0.166074  0.360507   
110    1.0    1.0    1.0    0.0  0.089074  0.089074  0.088968  0.402174   
111    0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.019928   
112    1.0    1.0    1.0    0.0  0.813539  0.813539  0.812574  0.773551   
113    1.0    1.0    0.5    0.0  0.461995  0.461995  0.461447  0.509058   
114    1.0    1.0    1.0    0.0  0.695962  0.688836  0.695136  0.782609   
115    1.0    1.0    0.5    0.0  0.587886  0.587886  0.584816  0.784420   
116    0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.548913   
117    0.5    0.0    0.5    0.0  0.323040  0.323040  0.322657  0.663043   
118    1.0    1.0    1.0    0.0  0.877672  0.877672  0.876631  0.806159   
119    1.0    1.0    1.0    0.0  0.713777  0.713777  0.712930  0.583333   

        X_140     X_141  ...    X_2868    X_2869    X_2870  X_2871      HOUR  \
84   0.752613  0.463320  ...  0.979970  0.991490  0.879749     1.0  1.000000   
85   0.550523  0.330759  ...  0.984440  0.982646  0.818433     1.0  1.000000   
86   0.543554  0.689833  ...  0.876842  0.939763  0.836238     1.0  0.260870   
87   0.026132  0.000000  ...  0.828836  0.953279  0.805893     1.0  0.434783   
88   0.614983  0.643501  ...  0.831319  0.926581  0.838370     1.0  0.260870   
89   0.878049  0.722008  ...  0.841748  0.923244  0.825956     1.0  0.608696   
90   0.810105  0.863578  ...  0.980301  0.954280  0.786583     1.0  0.043478   
91   0.644599  0.740026  ...  0.902500  0.941432  0.838244     1.0  0.521739   
92   0.905923  0.903475  ...  0.000000  0.000000  0.000000     1.0  0.173913   
93   0.770035  0.749035  ...  0.672074  0.944268  0.816552     1.0  0.608696   
94   0.540070  0.388674  ...  0.000000  0.000000  0.000000     1.0  0.217391   
95   0.735192  0.786358  ...  0.933289  0.943935  0.805016     1.0  0.000000   
96   0.529617  0.711712  ...  0.703029  0.609544  0.982445     0.0  0.217391   
97   0.456446  0.649936  ...  0.881311  0.946438  0.804640     1.0  0.043478   
98   0.479094  0.608752  ... 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     1.0    1.0    1.0    0.0  0.560570  0.554632  0.559905  0.684783   
85     1.0    1.0    0.5    0.0  0.729216  0.729216  0.728351  0.536232   
86     0.5    0.0    0.5    0.0  0.232779  0.232779  0.232503  0.568841   
87     0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.027174   
88     1.0    1.0    1.0    0.0  0.615202  0.615202  0.614472  0.625000   
89     0.5    1.0    0.5    0.0  0.925178  0.925178  0.924081  0.869565   
90     1.0    1.0    1.0    0.0  0.875297  0.875297  0.874259  0.811594   
91     1.0    1.0    1.0    0.0  0.640143  0.640143  0.639383  0.653986   
92     1.0    1.0    1.0    0.0  1.000000  1.000000  1.000000  0.914855   
93     1.0    1.0    1.0    0.0  0.813539  0.813539  0.813760  0.771739   
94     0.5    0.0    0.0    0.0  0.262470  0.262470  0.258600  0.565217   
95     1.0    1.0    1.0    0.0  0.793349  0.793349  0.792408  0.733696   
96     0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.570652   
97     0.5    0.0    0.5    0.0  0.166271  0.166271  0.166074  0.490942   
98     1.0    1.0    1.0    0.0  0.495249  0.497625  0.497034  0.501812   
99     1.0    1.0    1.0    0.0  0.944181  0.944181  0.944247  0.811594   
100    1.0    1.0    1.0    0.0  0.173397  0.175772  0.175563  0.275362   
101    1.0    1.0    1.0    0.0  0.514252  0.514252  0.513642  0.556159   
102    0.5    1.0    0.5    0.0  0.021378  0.023753  0.023725  0.143116   
103    0.5    0.0    0.5    0.0  0.059382  0.059382  0.059312  0.217391   
104    1.0    1.0    1.0    0.0  0.108076  0.108076  0.107948  0.344203   
105    0.5    0.0    0.5    0.0  0.065321  0.065321  0.065243  0.206522   
106    0.5    0.0    0.5    0.0  0.235154  0.235154  0.234875  0.574275   
107    1.0    1.0    1.0    0.0  0.453682  0.453682  0.453144  0.670290   
108    1.0    1.0    0.5    0.0  0.505938  0.505938  0.505338  0.525362   
109    1.0    1.0    1.0    0.0  0.166271  0.166271  0.166074  0.360507   
110    1.0    1.0    1.0    0.0  0.089074  0.089074  0.088968  0.402174   
111    0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.019928   
112    1.0    1.0    1.0    0.0  0.813539  0.813539  0.812574  0.773551   
113    1.0    1.0    0.5    0.0  0.461995  0.461995  0.461447  0.509058   
114    1.0    1.0    1.0    0.0  0.695962  0.688836  0.695136  0.782609   
115    1.0    1.0    0.5    0.0  0.587886  0.587886  0.584816  0.784420   
116    0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.548913   
117    0.5    0.0    0.5    0.0  0.323040  0.323040  0.322657  0.663043   
118    1.0    1.0    1.0    0.0  0.877672  0.877672  0.876631  0.806159   
119    1.0    1.0    1.0    0.0  0.713777  0.713777  0.712930  0.583333   

        X_140     X_141  ...    X_2868    X_2869    X_2870  X_2871      HOUR  \
84   0.752613  0.463320  ...  0.979970  0.991490  0.879749     1.0  1.000000   
85   0.550523  0.330759  ...  0.984440  0.982646  0.818433     1.0  1.000000   
86   0.543554  0.689833  ...  0.876842  0.939763  0.836238     1.0  0.260870   
87   0.026132  0.000000  ...  0.828836  0.953279  0.805893     1.0  0.434783   
88   0.614983  0.643501  ...  0.831319  0.926581  0.838370     1.0  0.260870   
89   0.878049  0.722008  ...  0.841748  0.923244  0.825956     1.0  0.608696   
90   0.810105  0.863578  ...  0.980301  0.954280  0.786583     1.0  0.043478   
91   0.644599  0.740026  ...  0.902500  0.941432  0.838244     1.0  0.521739   
92   0.905923  0.903475  ...  0.000000  0.000000  0.000000     1.0  0.173913   
93   0.770035  0.749035  ...  0.672074  0.944268  0.816552     1.0  0.608696   
94   0.540070  0.388674  ...  0.000000  0.000000  0.000000     1.0  0.217391   
95   0.735192  0.786358  ...  0.933289  0.943935  0.805016     1.0  0.000000   
96   0.529617  0.711712  ...  0.703029  0.609544  0.982445     0.0  0.217391   
97   0.456446  0.649936  ...  0.881311  0.946438  0.804640     1.0  0.043478   
98   0.479094  0.608752  ... 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     1.0    1.0    1.0    0.0  0.560570  0.554632  0.559905  0.684783   
85     1.0    1.0    0.5    0.0  0.729216  0.729216  0.728351  0.536232   
86     0.5    0.0    0.5    0.0  0.232779  0.232779  0.232503  0.568841   
87     0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.027174   
88     1.0    1.0    1.0    0.0  0.615202  0.615202  0.614472  0.625000   
89     0.5    1.0    0.5    0.0  0.925178  0.925178  0.924081  0.869565   
90     1.0    1.0    1.0    0.0  0.875297  0.875297  0.874259  0.811594   
91     1.0    1.0    1.0    0.0  0.640143  0.640143  0.639383  0.653986   
92     1.0    1.0    1.0    0.0  1.000000  1.000000  1.000000  0.914855   
93     1.0    1.0    1.0    0.0  0.813539  0.813539  0.813760  0.771739   
94     0.5    0.0    0.0    0.0  0.262470  0.262470  0.258600  0.565217   
95     1.0    1.0    1.0    0.0  0.793349  0.793349  0.792408  0.733696   
96     0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.570652   
97     0.5    0.0    0.5    0.0  0.166271  0.166271  0.166074  0.490942   
98     1.0    1.0    1.0    0.0  0.495249  0.497625  0.497034  0.501812   
99     1.0    1.0    1.0    0.0  0.944181  0.944181  0.944247  0.811594   
100    1.0    1.0    1.0    0.0  0.173397  0.175772  0.175563  0.275362   
101    1.0    1.0    1.0    0.0  0.514252  0.514252  0.513642  0.556159   
102    0.5    1.0    0.5    0.0  0.021378  0.023753  0.023725  0.143116   
103    0.5    0.0    0.5    0.0  0.059382  0.059382  0.059312  0.217391   
104    1.0    1.0    1.0    0.0  0.108076  0.108076  0.107948  0.344203   
105    0.5    0.0    0.5    0.0  0.065321  0.065321  0.065243  0.206522   
106    0.5    0.0    0.5    0.0  0.235154  0.235154  0.234875  0.574275   
107    1.0    1.0    1.0    0.0  0.453682  0.453682  0.453144  0.670290   
108    1.0    1.0    0.5    0.0  0.505938  0.505938  0.505338  0.525362   
109    1.0    1.0    1.0    0.0  0.166271  0.166271  0.166074  0.360507   
110    1.0    1.0    1.0    0.0  0.089074  0.089074  0.088968  0.402174   
111    0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.019928   
112    1.0    1.0    1.0    0.0  0.813539  0.813539  0.812574  0.773551   
113    1.0    1.0    0.5    0.0  0.461995  0.461995  0.461447  0.509058   
114    1.0    1.0    1.0    0.0  0.695962  0.688836  0.695136  0.782609   
115    1.0    1.0    0.5    0.0  0.587886  0.587886  0.584816  0.784420   
116    0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.548913   
117    0.5    0.0    0.5    0.0  0.323040  0.323040  0.322657  0.663043   
118    1.0    1.0    1.0    0.0  0.877672  0.877672  0.876631  0.806159   
119    1.0    1.0    1.0    0.0  0.713777  0.713777  0.712930  0.583333   

        X_140     X_141  ...    X_2868    X_2869    X_2870  X_2871      HOUR  \
84   0.752613  0.463320  ...  0.979970  0.991490  0.879749     1.0  1.000000   
85   0.550523  0.330759  ...  0.984440  0.982646  0.818433     1.0  1.000000   
86   0.543554  0.689833  ...  0.876842  0.939763  0.836238     1.0  0.260870   
87   0.026132  0.000000  ...  0.828836  0.953279  0.805893     1.0  0.434783   
88   0.614983  0.643501  ...  0.831319  0.926581  0.838370     1.0  0.260870   
89   0.878049  0.722008  ...  0.841748  0.923244  0.825956     1.0  0.608696   
90   0.810105  0.863578  ...  0.980301  0.954280  0.786583     1.0  0.043478   
91   0.644599  0.740026  ...  0.902500  0.941432  0.838244     1.0  0.521739   
92   0.905923  0.903475  ...  0.000000  0.000000  0.000000     1.0  0.173913   
93   0.770035  0.749035  ...  0.672074  0.944268  0.816552     1.0  0.608696   
94   0.540070  0.388674  ...  0.000000  0.000000  0.000000     1.0  0.217391   
95   0.735192  0.786358  ...  0.933289  0.943935  0.805016     1.0  0.000000   
96   0.529617  0.711712  ...  0.703029  0.609544  0.982445     0.0  0.217391   
97   0.456446  0.649936  ...  0.881311  0.946438  0.804640     1.0  0.043478   
98   0.479094  0.608752  ... 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     1.0    1.0    1.0    0.0  0.560570  0.554632  0.559905  0.684783   
85     1.0    1.0    0.5    0.0  0.729216  0.729216  0.728351  0.536232   
86     0.5    0.0    0.5    0.0  0.232779  0.232779  0.232503  0.568841   
87     0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.027174   
88     1.0    1.0    1.0    0.0  0.615202  0.615202  0.614472  0.625000   
89     0.5    1.0    0.5    0.0  0.925178  0.925178  0.924081  0.869565   
90     1.0    1.0    1.0    0.0  0.875297  0.875297  0.874259  0.811594   
91     1.0    1.0    1.0    0.0  0.640143  0.640143  0.639383  0.653986   
92     1.0    1.0    1.0    0.0  1.000000  1.000000  1.000000  0.914855   
93     1.0    1.0    1.0    0.0  0.813539  0.813539  0.813760  0.771739   
94     0.5    0.0    0.0    0.0  0.262470  0.262470  0.258600  0.565217   
95     1.0    1.0    1.0    0.0  0.793349  0.793349  0.792408  0.733696   
96     0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.570652   
97     0.5    0.0    0.5    0.0  0.166271  0.166271  0.166074  0.490942   
98     1.0    1.0    1.0    0.0  0.495249  0.497625  0.497034  0.501812   
99     1.0    1.0    1.0    0.0  0.944181  0.944181  0.944247  0.811594   
100    1.0    1.0    1.0    0.0  0.173397  0.175772  0.175563  0.275362   
101    1.0    1.0    1.0    0.0  0.514252  0.514252  0.513642  0.556159   
102    0.5    1.0    0.5    0.0  0.021378  0.023753  0.023725  0.143116   
103    0.5    0.0    0.5    0.0  0.059382  0.059382  0.059312  0.217391   
104    1.0    1.0    1.0    0.0  0.108076  0.108076  0.107948  0.344203   
105    0.5    0.0    0.5    0.0  0.065321  0.065321  0.065243  0.206522   
106    0.5    0.0    0.5    0.0  0.235154  0.235154  0.234875  0.574275   
107    1.0    1.0    1.0    0.0  0.453682  0.453682  0.453144  0.670290   
108    1.0    1.0    0.5    0.0  0.505938  0.505938  0.505338  0.525362   
109    1.0    1.0    1.0    0.0  0.166271  0.166271  0.166074  0.360507   
110    1.0    1.0    1.0    0.0  0.089074  0.089074  0.088968  0.402174   
111    0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.019928   
112    1.0    1.0    1.0    0.0  0.813539  0.813539  0.812574  0.773551   
113    1.0    1.0    0.5    0.0  0.461995  0.461995  0.461447  0.509058   
114    1.0    1.0    1.0    0.0  0.695962  0.688836  0.695136  0.782609   
115    1.0    1.0    0.5    0.0  0.587886  0.587886  0.584816  0.784420   
116    0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.548913   
117    0.5    0.0    0.5    0.0  0.323040  0.323040  0.322657  0.663043   
118    1.0    1.0    1.0    0.0  0.877672  0.877672  0.876631  0.806159   
119    1.0    1.0    1.0    0.0  0.713777  0.713777  0.712930  0.583333   

        X_140     X_141  ...    X_2868    X_2869    X_2870  X_2871      HOUR  \
84   0.752613  0.463320  ...  0.979970  0.991490  0.879749     1.0  1.000000   
85   0.550523  0.330759  ...  0.984440  0.982646  0.818433     1.0  1.000000   
86   0.543554  0.689833  ...  0.876842  0.939763  0.836238     1.0  0.260870   
87   0.026132  0.000000  ...  0.828836  0.953279  0.805893     1.0  0.434783   
88   0.614983  0.643501  ...  0.831319  0.926581  0.838370     1.0  0.260870   
89   0.878049  0.722008  ...  0.841748  0.923244  0.825956     1.0  0.608696   
90   0.810105  0.863578  ...  0.980301  0.954280  0.786583     1.0  0.043478   
91   0.644599  0.740026  ...  0.902500  0.941432  0.838244     1.0  0.521739   
92   0.905923  0.903475  ...  0.000000  0.000000  0.000000     1.0  0.173913   
93   0.770035  0.749035  ...  0.672074  0.944268  0.816552     1.0  0.608696   
94   0.540070  0.388674  ...  0.000000  0.000000  0.000000     1.0  0.217391   
95   0.735192  0.786358  ...  0.933289  0.943935  0.805016     1.0  0.000000   
96   0.529617  0.711712  ...  0.703029  0.609544  0.982445     0.0  0.217391   
97   0.456446  0.649936  ...  0.881311  0.946438  0.804640     1.0  0.043478   
98   0.479094  0.608752  ... 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     1.0    1.0    1.0    0.0  0.560570  0.554632  0.559905  0.684783   
85     1.0    1.0    0.5    0.0  0.729216  0.729216  0.728351  0.536232   
86     0.5    0.0    0.5    0.0  0.232779  0.232779  0.232503  0.568841   
87     0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.027174   
88     1.0    1.0    1.0    0.0  0.615202  0.615202  0.614472  0.625000   
89     0.5    1.0    0.5    0.0  0.925178  0.925178  0.924081  0.869565   
90     1.0    1.0    1.0    0.0  0.875297  0.875297  0.874259  0.811594   
91     1.0    1.0    1.0    0.0  0.640143  0.640143  0.639383  0.653986   
92     1.0    1.0    1.0    0.0  1.000000  1.000000  1.000000  0.914855   
93     1.0    1.0    1.0    0.0  0.813539  0.813539  0.813760  0.771739   
94     0.5    0.0    0.0    0.0  0.262470  0.262470  0.258600  0.565217   
95     1.0    1.0    1.0    0.0  0.793349  0.793349  0.792408  0.733696   
96     0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.570652   
97     0.5    0.0    0.5    0.0  0.166271  0.166271  0.166074  0.490942   
98     1.0    1.0    1.0    0.0  0.495249  0.497625  0.497034  0.501812   
99     1.0    1.0    1.0    0.0  0.944181  0.944181  0.944247  0.811594   
100    1.0    1.0    1.0    0.0  0.173397  0.175772  0.175563  0.275362   
101    1.0    1.0    1.0    0.0  0.514252  0.514252  0.513642  0.556159   
102    0.5    1.0    0.5    0.0  0.021378  0.023753  0.023725  0.143116   
103    0.5    0.0    0.5    0.0  0.059382  0.059382  0.059312  0.217391   
104    1.0    1.0    1.0    0.0  0.108076  0.108076  0.107948  0.344203   
105    0.5    0.0    0.5    0.0  0.065321  0.065321  0.065243  0.206522   
106    0.5    0.0    0.5    0.0  0.235154  0.235154  0.234875  0.574275   
107    1.0    1.0    1.0    0.0  0.453682  0.453682  0.453144  0.670290   
108    1.0    1.0    0.5    0.0  0.505938  0.505938  0.505338  0.525362   
109    1.0    1.0    1.0    0.0  0.166271  0.166271  0.166074  0.360507   
110    1.0    1.0    1.0    0.0  0.089074  0.089074  0.088968  0.402174   
111    0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.019928   
112    1.0    1.0    1.0    0.0  0.813539  0.813539  0.812574  0.773551   
113    1.0    1.0    0.5    0.0  0.461995  0.461995  0.461447  0.509058   
114    1.0    1.0    1.0    0.0  0.695962  0.688836  0.695136  0.782609   
115    1.0    1.0    0.5    0.0  0.587886  0.587886  0.584816  0.784420   
116    0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.548913   
117    0.5    0.0    0.5    0.0  0.323040  0.323040  0.322657  0.663043   
118    1.0    1.0    1.0    0.0  0.877672  0.877672  0.876631  0.806159   
119    1.0    1.0    1.0    0.0  0.713777  0.713777  0.712930  0.583333   

        X_140     X_141  ...    X_2868    X_2869    X_2870  X_2871      HOUR  \
84   0.752613  0.463320  ...  0.979970  0.991490  0.879749     1.0  1.000000   
85   0.550523  0.330759  ...  0.984440  0.982646  0.818433     1.0  1.000000   
86   0.543554  0.689833  ...  0.876842  0.939763  0.836238     1.0  0.260870   
87   0.026132  0.000000  ...  0.828836  0.953279  0.805893     1.0  0.434783   
88   0.614983  0.643501  ...  0.831319  0.926581  0.838370     1.0  0.260870   
89   0.878049  0.722008  ...  0.841748  0.923244  0.825956     1.0  0.608696   
90   0.810105  0.863578  ...  0.980301  0.954280  0.786583     1.0  0.043478   
91   0.644599  0.740026  ...  0.902500  0.941432  0.838244     1.0  0.521739   
92   0.905923  0.903475  ...  0.000000  0.000000  0.000000     1.0  0.173913   
93   0.770035  0.749035  ...  0.672074  0.944268  0.816552     1.0  0.608696   
94   0.540070  0.388674  ...  0.000000  0.000000  0.000000     1.0  0.217391   
95   0.735192  0.786358  ...  0.933289  0.943935  0.805016     1.0  0.000000   
96   0.529617  0.711712  ...  0.703029  0.609544  0.982445     0.0  0.217391   
97   0.456446  0.649936  ...  0.881311  0.946438  0.804640     1.0  0.043478   
98   0.479094  0.608752  ... 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     1.0    1.0    1.0    0.0  0.560570  0.554632  0.559905  0.684783   
85     1.0    1.0    0.5    0.0  0.729216  0.729216  0.728351  0.536232   
86     0.5    0.0    0.5    0.0  0.232779  0.232779  0.232503  0.568841   
87     0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.027174   
88     1.0    1.0    1.0    0.0  0.615202  0.615202  0.614472  0.625000   
89     0.5    1.0    0.5    0.0  0.925178  0.925178  0.924081  0.869565   
90     1.0    1.0    1.0    0.0  0.875297  0.875297  0.874259  0.811594   
91     1.0    1.0    1.0    0.0  0.640143  0.640143  0.639383  0.653986   
92     1.0    1.0    1.0    0.0  1.000000  1.000000  1.000000  0.914855   
93     1.0    1.0    1.0    0.0  0.813539  0.813539  0.813760  0.771739   
94     0.5    0.0    0.0    0.0  0.262470  0.262470  0.258600  0.565217   
95     1.0    1.0    1.0    0.0  0.793349  0.793349  0.792408  0.733696   
96     0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.570652   
97     0.5    0.0    0.5    0.0  0.166271  0.166271  0.166074  0.490942   
98     1.0    1.0    1.0    0.0  0.495249  0.497625  0.497034  0.501812   
99     1.0    1.0    1.0    0.0  0.944181  0.944181  0.944247  0.811594   
100    1.0    1.0    1.0    0.0  0.173397  0.175772  0.175563  0.275362   
101    1.0    1.0    1.0    0.0  0.514252  0.514252  0.513642  0.556159   
102    0.5    1.0    0.5    0.0  0.021378  0.023753  0.023725  0.143116   
103    0.5    0.0    0.5    0.0  0.059382  0.059382  0.059312  0.217391   
104    1.0    1.0    1.0    0.0  0.108076  0.108076  0.107948  0.344203   
105    0.5    0.0    0.5    0.0  0.065321  0.065321  0.065243  0.206522   
106    0.5    0.0    0.5    0.0  0.235154  0.235154  0.234875  0.574275   
107    1.0    1.0    1.0    0.0  0.453682  0.453682  0.453144  0.670290   
108    1.0    1.0    0.5    0.0  0.505938  0.505938  0.505338  0.525362   
109    1.0    1.0    1.0    0.0  0.166271  0.166271  0.166074  0.360507   
110    1.0    1.0    1.0    0.0  0.089074  0.089074  0.088968  0.402174   
111    0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.019928   
112    1.0    1.0    1.0    0.0  0.813539  0.813539  0.812574  0.773551   
113    1.0    1.0    0.5    0.0  0.461995  0.461995  0.461447  0.509058   
114    1.0    1.0    1.0    0.0  0.695962  0.688836  0.695136  0.782609   
115    1.0    1.0    0.5    0.0  0.587886  0.587886  0.584816  0.784420   
116    0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.548913   
117    0.5    0.0    0.5    0.0  0.323040  0.323040  0.322657  0.663043   
118    1.0    1.0    1.0    0.0  0.877672  0.877672  0.876631  0.806159   
119    1.0    1.0    1.0    0.0  0.713777  0.713777  0.712930  0.583333   

        X_140     X_141  ...    X_2868    X_2869    X_2870  X_2871      HOUR  \
84   0.752613  0.463320  ...  0.979970  0.991490  0.879749     1.0  1.000000   
85   0.550523  0.330759  ...  0.984440  0.982646  0.818433     1.0  1.000000   
86   0.543554  0.689833  ...  0.876842  0.939763  0.836238     1.0  0.260870   
87   0.026132  0.000000  ...  0.828836  0.953279  0.805893     1.0  0.434783   
88   0.614983  0.643501  ...  0.831319  0.926581  0.838370     1.0  0.260870   
89   0.878049  0.722008  ...  0.841748  0.923244  0.825956     1.0  0.608696   
90   0.810105  0.863578  ...  0.980301  0.954280  0.786583     1.0  0.043478   
91   0.644599  0.740026  ...  0.902500  0.941432  0.838244     1.0  0.521739   
92   0.905923  0.903475  ...  0.000000  0.000000  0.000000     1.0  0.173913   
93   0.770035  0.749035  ...  0.672074  0.944268  0.816552     1.0  0.608696   
94   0.540070  0.388674  ...  0.000000  0.000000  0.000000     1.0  0.217391   
95   0.735192  0.786358  ...  0.933289  0.943935  0.805016     1.0  0.000000   
96   0.529617  0.711712  ...  0.703029  0.609544  0.982445     0.0  0.217391   
97   0.456446  0.649936  ...  0.881311  0.946438  0.804640     1.0  0.043478   
98   0.479094  0.608752  ... 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     1.0    1.0    1.0    0.0  0.560570  0.554632  0.559905  0.684783   
85     1.0    1.0    0.5    0.0  0.729216  0.729216  0.728351  0.536232   
86     0.5    0.0    0.5    0.0  0.232779  0.232779  0.232503  0.568841   
87     0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.027174   
88     1.0    1.0    1.0    0.0  0.615202  0.615202  0.614472  0.625000   
89     0.5    1.0    0.5    0.0  0.925178  0.925178  0.924081  0.869565   
90     1.0    1.0    1.0    0.0  0.875297  0.875297  0.874259  0.811594   
91     1.0    1.0    1.0    0.0  0.640143  0.640143  0.639383  0.653986   
92     1.0    1.0    1.0    0.0  1.000000  1.000000  1.000000  0.914855   
93     1.0    1.0    1.0    0.0  0.813539  0.813539  0.813760  0.771739   
94     0.5    0.0    0.0    0.0  0.262470  0.262470  0.258600  0.565217   
95     1.0    1.0    1.0    0.0  0.793349  0.793349  0.792408  0.733696   
96     0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.570652   
97     0.5    0.0    0.5    0.0  0.166271  0.166271  0.166074  0.490942   
98     1.0    1.0    1.0    0.0  0.495249  0.497625  0.497034  0.501812   
99     1.0    1.0    1.0    0.0  0.944181  0.944181  0.944247  0.811594   
100    1.0    1.0    1.0    0.0  0.173397  0.175772  0.175563  0.275362   
101    1.0    1.0    1.0    0.0  0.514252  0.514252  0.513642  0.556159   
102    0.5    1.0    0.5    0.0  0.021378  0.023753  0.023725  0.143116   
103    0.5    0.0    0.5    0.0  0.059382  0.059382  0.059312  0.217391   
104    1.0    1.0    1.0    0.0  0.108076  0.108076  0.107948  0.344203   
105    0.5    0.0    0.5    0.0  0.065321  0.065321  0.065243  0.206522   
106    0.5    0.0    0.5    0.0  0.235154  0.235154  0.234875  0.574275   
107    1.0    1.0    1.0    0.0  0.453682  0.453682  0.453144  0.670290   
108    1.0    1.0    0.5    0.0  0.505938  0.505938  0.505338  0.525362   
109    1.0    1.0    1.0    0.0  0.166271  0.166271  0.166074  0.360507   
110    1.0    1.0    1.0    0.0  0.089074  0.089074  0.088968  0.402174   
111    0.5    1.0    0.5    0.0  0.032067  0.032067  0.032028  0.019928   
112    1.0    1.0    1.0    0.0  0.813539  0.813539  0.812574  0.773551   
113    1.0    1.0    0.5    0.0  0.461995  0.461995  0.461447  0.509058   
114    1.0    1.0    1.0    0.0  0.695962  0.688836  0.695136  0.782609   
115    1.0    1.0    0.5    0.0  0.587886  0.587886  0.584816  0.784420   
116    0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.548913   
117    0.5    0.0    0.5    0.0  0.323040  0.323040  0.322657  0.663043   
118    1.0    1.0    1.0    0.0  0.877672  0.877672  0.876631  0.806159   
119    1.0    1.0    1.0    0.0  0.713777  0.713777  0.712930  0.583333   

        X_140     X_141  ...    X_2868    X_2869    X_2870  X_2871      HOUR  \
84   0.752613  0.463320  ...  0.979970  0.991490  0.879749     1.0  1.000000   
85   0.550523  0.330759  ...  0.984440  0.982646  0.818433     1.0  1.000000   
86   0.543554  0.689833  ...  0.876842  0.939763  0.836238     1.0  0.260870   
87   0.026132  0.000000  ...  0.828836  0.953279  0.805893     1.0  0.434783   
88   0.614983  0.643501  ...  0.831319  0.926581  0.838370     1.0  0.260870   
89   0.878049  0.722008  ...  0.841748  0.923244  0.825956     1.0  0.608696   
90   0.810105  0.863578  ...  0.980301  0.954280  0.786583     1.0  0.043478   
91   0.644599  0.740026  ...  0.902500  0.941432  0.838244     1.0  0.521739   
92   0.905923  0.903475  ...  0.000000  0.000000  0.000000     1.0  0.173913   
93   0.770035  0.749035  ...  0.672074  0.944268  0.816552     1.0  0.608696   
94   0.540070  0.388674  ...  0.000000  0.000000  0.000000     1.0  0.217391   
95   0.735192  0.786358  ...  0.933289  0.943935  0.805016     1.0  0.000000   
96   0.529617  0.711712  ...  0.703029  0.609544  0.982445     0.0  0.217391   
97   0.456446  0.649936  ...  0.881311  0.946438  0.804640     1.0  0.043478   
98   0.479094  0.608752  ... 

In [54]:
T05_final_regression_model = finalize_model(T05_model_et)

In [55]:
T05_prediction = predict_model(T05_final_regression_model, data=T05_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [56]:
T05_datas = T05_prediction['prediction_label']
T05_datas = pd.DataFrame(T05_datas.values, columns = ['Y_Quality'])
T05_datas

Y_Quality
0     0.533433
1     0.531267
2     0.531590
3     0.533665
4     0.531821
..         ...
115   0.533711
116   0.533695
117   0.525271
118   0.529806
119   0.521406

[120 rows x 1 columns]

In [57]:
T05y_idx= T05_class.index
T05y_idx = pd.DataFrame(T05y_idx, columns = ['index'])
T05_datas = pd.concat([T05y_idx, T05_datas], axis = 1)
T05_datas = T05_datas.set_index('index')
T05_datas

Y_Quality
index           
0       0.533433
2       0.531267
4       0.531590
6       0.533665
8       0.531821
...          ...
549     0.533711
550     0.533695
551     0.525271
552     0.529806
555     0.521406

[120 rows x 1 columns]

In [58]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T05_datas, 
                   target=T05_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [59]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbc = create_model('gbc', fold = 5)
T05_total_models.append(T05_model_gbc)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [60]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbc = tune_model(T05_model_gbc, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [61]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbc, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]
T05_tuned_models

[LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
                importance_type='split', learning_rate=0.1, max_depth=-1,
                min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
                n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
                random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
                subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                        criterion='gini', max_depth=None, max_features='auto',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.0, min_samples_leaf=1,
                        min_samples_split=2, min_weight_fraction_leaf=0.0,
                        n_estimators=100, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp

In [62]:
for model in T05_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0            0.9920
85    0.524781        0                 0            0.6880
86    0.527944        1                 1            0.9956
87    0.519451        0                 0            0.9920
88    0.550340        2                 2            0.9903
89    0.513751        0                 0            0.9920
90    0.527332        1                 1            0.9956
91    0.544129        2                 2            0.9903
92    0.527976        1                 1            0.9956
93    0.528186        1                 1            0.9956
94    0.525046        0                 0            0.6880
95    0.535405        2                 2            0.6814
96    0.531821        1                 1            0.9954
97    0.529681        1                 1            0.9956
98    0.559464        2                 2            0.9903
99    0.525494        1                 1            0.9946
100   0.527398        1                 1            0.9956
101   0.562770        2                 2            0.9903
102   0.539611        2                 2            0.9903
103   0.519406        0                 0            0.9920
104   0.531503        1                 1            0.9954
105   0.520856        0                 0            0.9920
106   0.547592        2                 2            0.9903
107   0.533665        1                 1            0.9917
108   0.521051        0                 0            0.9920
109   0.543957        2                 2            0.9903
110   0.560568        2                 2            0.9903
111   0.523383        0                 0            0.9920
112   0.520911        0                 0            0.9920
113   0.522460        0                 0            0.9920
114   0.524022        0                 0            0.9920
115   0.531267        1                 1            0.9956
116   0.534054        1                 1            0.9917
117   0.532170        1                 1            0.9950
118   0.531254        1                 1            0.9956
119   0.537560        2                 2            0.9903

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0              1.00
85    0.524781        0                 0              0.93
86    0.527944        1                 1              1.00
87    0.519451        0                 0              1.00
88    0.550340        2                 2              1.00
89    0.513751        0                 0              1.00
90    0.527332        1                 1              1.00
91    0.544129        2                 2              1.00
92    0.527976        1                 1              1.00
93    0.528186        1                 1              1.00
94    0.525046        0                 1              0.95
95    0.535405        2                 2              0.67
96    0.531821        1                 1              1.00
97    0.529681        1                 1              1.00
98    0.559464        2                 2              1.00
99    0.525494        1                 1              0.99
100   0.527398        1                 1              1.00
101   0.562770        2                 2              1.00
102   0.539611        2                 2              1.00
103   0.519406        0                 0              1.00
104   0.531503        1                 1              1.00
105   0.520856        0                 0              1.00
106   0.547592        2                 2              1.00
107   0.533665        1                 1              1.00
108   0.521051        0                 0              1.00
109   0.543957        2                 2              1.00
110   0.560568        2                 2              1.00
111   0.523383        0                 0              1.00
112   0.520911        0                 0              1.00
113   0.522460        0                 0              1.00
114   0.524022        0                 0              0.99
115   0.531267        1                 1              1.00
116   0.534054        1                 1              1.00
117   0.532170        1                 1              1.00
118   0.531254        1                 1              1.00
119   0.537560        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0            0.9942
85    0.524781        0                 0            0.9788
86    0.527944        1                 1            0.9917
87    0.519451        0                 0            0.9942
88    0.550340        2                 2            0.9918
89    0.513751        0                 0            0.9942
90    0.527332        1                 1            0.9917
91    0.544129        2                 2            0.9918
92    0.527976        1                 1            0.9917
93    0.528186        1                 1            0.9917
94    0.525046        0                 1            0.9595
95    0.535405        2                 1            0.5235
96    0.531821        1                 1            0.9917
97    0.529681        1                 1            0.9917
98    0.559464        2                 2            0.9918
99    0.525494        1                 1            0.9875
100   0.527398        1                 1            0.9917
101   0.562770        2                 2            0.9918
102   0.539611        2                 2            0.9918
103   0.519406        0                 0            0.9942
104   0.531503        1                 1            0.9917
105   0.520856        0                 0            0.9942
106   0.547592        2                 2            0.9918
107   0.533665        1                 1            0.9917
108   0.521051        0                 0            0.9942
109   0.543957        2                 2            0.9918
110   0.560568        2                 2            0.9918
111   0.523383        0                 0            0.9942
112   0.520911        0                 0            0.9942
113   0.522460        0                 0            0.9942
114   0.524022        0                 0            0.9923
115   0.531267        1                 1            0.9917
116   0.534054        1                 1            0.9917
117   0.532170        1                 1            0.9917
118   0.531254        1                 1            0.9917
119   0.537560        2                 2            0.9918

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0              1.00
85    0.524781        0                 0              0.62
86    0.527944        1                 1              1.00
87    0.519451        0                 0              1.00
88    0.550340        2                 2              1.00
89    0.513751        0                 0              1.00
90    0.527332        1                 1              1.00
91    0.544129        2                 2              1.00
92    0.527976        1                 1              1.00
93    0.528186        1                 1              1.00
94    0.525046        0                 1              0.94
95    0.535405        2                 1              0.56
96    0.531821        1                 1              1.00
97    0.529681        1                 1              1.00
98    0.559464        2                 2              1.00
99    0.525494        1                 1              1.00
100   0.527398        1                 1              1.00
101   0.562770        2                 2              1.00
102   0.539611        2                 2              1.00
103   0.519406        0                 0              1.00
104   0.531503        1                 1              1.00
105   0.520856        0                 0              1.00
106   0.547592        2                 2              1.00
107   0.533665        1                 1              1.00
108   0.521051        0                 0              1.00
109   0.543957        2                 2              1.00
110   0.560568        2                 2              1.00
111   0.523383        0                 0              1.00
112   0.520911        0                 0              1.00
113   0.522460        0                 0              1.00
114   0.524022        0                 0              1.00
115   0.531267        1                 1              1.00
116   0.534054        1                 1              1.00
117   0.532170        1                 1              1.00
118   0.531254        1                 1              1.00
119   0.537560        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0            0.9991
85    0.524781        0                 0            0.9746
86    0.527944        1                 1            0.9991
87    0.519451        0                 0            0.9991
88    0.550340        2                 2            0.9984
89    0.513751        0                 0            0.9983
90    0.527332        1                 1            0.9991
91    0.544129        2                 2            0.9987
92    0.527976        1                 1            0.9992
93    0.528186        1                 1            0.9992
94    0.525046        0                 1            0.9799
95    0.535405        2                 2            0.9784
96    0.531821        1                 1            0.9990
97    0.529681        1                 1            0.9992
98    0.559464        2                 2            0.9981
99    0.525494        1                 1            0.9975
100   0.527398        1                 1            0.9991
101   0.562770        2                 2            0.9981
102   0.539611        2                 2            0.9988
103   0.519406        0                 0            0.9991
104   0.531503        1                 1            0.9991
105   0.520856        0                 0            0.9991
106   0.547592        2                 2            0.9984
107   0.533665        1                 1            0.9962
108   0.521051        0                 0            0.9991
109   0.543957        2                 2            0.9987
110   0.560568        2                 2            0.9981
111   0.523383        0                 0            0.9989
112   0.520911        0                 0            0.9991
113   0.522460        0                 0            0.9990
114   0.524022        0                 0            0.9985
115   0.531267        1                 1            0.9991
116   0.534054        1                 1            0.9906
117   0.532170        1                 1            0.9989
118   0.531254        1                 1            0.9991
119   0.537560        2                 2            0.9975

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0            0.9840
85    0.524781        0                 0            0.9840
86    0.527944        1                 1            0.9824
87    0.519451        0                 0            0.9840
88    0.550340        2                 2            0.9803
89    0.513751        0                 0            0.9840
90    0.527332        1                 1            0.9817
91    0.544129        2                 2            0.9803
92    0.527976        1                 1            0.9824
93    0.528186        1                 1            0.9824
94    0.525046        0                 1            0.9773
95    0.535405        2                 2            0.9803
96    0.531821        1                 1            0.9810
97    0.529681        1                 1            0.9901
98    0.559464        2                 2            0.9803
99    0.525494        1                 1            0.9804
100   0.527398        1                 1            0.9817
101   0.562770        2                 2            0.9803
102   0.539611        2                 2            0.9803
103   0.519406        0                 0            0.9840
104   0.531503        1                 1            0.9810
105   0.520856        0                 0            0.9840
106   0.547592        2                 2            0.9803
107   0.533665        1                 1            0.9784
108   0.521051        0                 0            0.9840
109   0.543957        2                 2            0.9803
110   0.560568        2                 2            0.9803
111   0.523383        0                 0            0.9840
112   0.520911        0                 0            0.9840
113   0.522460        0                 0            0.9840
114   0.524022        0                 0            0.9840
115   0.531267        1                 1            0.9816
116   0.534054        1                 1            0.9784
117   0.532170        1                 1            0.9810
118   0.531254        1                 1            0.9816
119   0.537560        2                 2            0.9803

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0               1.0
85    0.524781        0                 0               1.0
86    0.527944        1                 1               1.0
87    0.519451        0                 0               1.0
88    0.550340        2                 2               1.0
89    0.513751        0                 0               1.0
90    0.527332        1                 1               1.0
91    0.544129        2                 2               1.0
92    0.527976        1                 1               1.0
93    0.528186        1                 1               1.0
94    0.525046        0                 1               1.0
95    0.535405        2                 2               1.0
96    0.531821        1                 1               1.0
97    0.529681        1                 1               1.0
98    0.559464        2                 2               1.0
99    0.525494        1                 1               1.0
100   0.527398        1                 1               1.0
101   0.562770        2                 2               1.0
102   0.539611        2                 2               1.0
103   0.519406        0                 0               1.0
104   0.531503        1                 1               1.0
105   0.520856        0                 0               1.0
106   0.547592        2                 2               1.0
107   0.533665        1                 1               1.0
108   0.521051        0                 0               1.0
109   0.543957        2                 2               1.0
110   0.560568        2                 2               1.0
111   0.523383        0                 0               1.0
112   0.520911        0                 0               1.0
113   0.522460        0                 0               1.0
114   0.524022        0                 0               1.0
115   0.531267        1                 1               1.0
116   0.534054        1                 1               1.0
117   0.532170        1                 1               1.0
118   0.531254        1                 1               1.0
119   0.537560        2                 2               1.0

In [63]:
T05_final_classification_model = finalize_model(T05_model_lightgbm)

In [64]:
T05_prediction = predict_model(T05_final_classification_model, data=T05_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [65]:
T05_y_class = pd.DataFrame(T05_class, columns = ['Y_Class'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_prediction = pd.concat([T05_prediction, T05_y_class], axis = 1)
T05_prediction = T05_prediction.set_index('index')
T05_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [66]:
T05_prediction

Y_Quality  prediction_label  prediction_score
index                                               
0       0.533433                 1            0.9990
2       0.531267                 1            0.9989
4       0.531590                 1            0.9990
6       0.533665                 1            0.9990
8       0.531821                 1            0.9990
...          ...               ...               ...
549     0.533711                 1            0.9990
550     0.533695                 1            0.9990
551     0.525271                 1            0.9978
552     0.529806                 1            0.9989
555     0.521406                 0            0.9983

[120 rows x 3 columns]

# T01

In [131]:
T01_class = T01['Y_Class']
T01_target = T01['Y_Quality']
T01_data = T01.drop(['Y_Class', 'Y_Quality'], axis = 1)
T01_data

X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  X_254  X_255  \
28     1.0   89.0    0.0   45.0   11.0   90.0   45.0   11.0   42.0    2.0   
33     1.0   95.0    0.0   45.0   11.0   98.0   45.0   11.0   42.0    2.0   
39     1.0   95.0    0.0   45.0   11.0  102.0   45.0   12.0   42.0    2.0   
40     1.0   95.0    0.0   45.0   11.0  105.0   45.0   11.0   42.0    2.0   
41     1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   42.0    2.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
479    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
501    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
523    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
531    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
585    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   

     ...  X_2860      X_2861  X_2862  X_2863      X_2864  X_2865  HOUR  \
28   ...   182.0  174.727586   160.5   446.0  429.716981   413.0    20   
33   ...   175.7  168.258621   158.3   446.0  429.301887   413.0     7   
39   ...   184.1  173.479310   165.8   447.0  427.867925   407.0     4   
40   ...   191.8  178.832143   168.6   446.0  428.403846   413.0    12   
41   ...   182.4  170.379310   162.9   446.0  429.094340   406.0    12   
..   ...     ...         ...     ...     ...         ...     ...   ...   
479  ...   183.3  169.553571   154.2   456.0  438.132075   413.0    15   
501  ...   187.6  182.142857   175.1   466.0  445.307692   425.0    15   
523  ...   189.2  181.700000   172.7   466.0  444.615385   423.0    10   
531  ...   192.6  185.207143   173.2   466.0  446.038461   427.0    15   
585  ...   192.2  187.396552   176.7   472.0  450.339623   432.0    11   

     MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
28       26            7            0.0  
33       14            2            0.0  
39       45            3            0.0  
40       26            3            0.0  
41       34            3            0.0  
..      ...          ...            ...  
479      28            2            1.0  
501      58            5            1.0  
523      39            7            1.0  
531      38            1            1.0  
585      17            1            1.0  

[129 rows x 882 columns]

In [68]:
T_01c = T01_data.columns
T_01scaler = MinMaxScaler()
T_01scaled = T_05scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)
T01_data

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
0      0.0  0.222222  0.000000    0.0    0.0  0.535714    0.0    0.0    0.0   
1      0.0  0.888889  0.000000    0.0    0.0  0.583333    0.0    0.0    0.0   
2      0.0  0.888889  0.000000    0.0    0.0  0.607143    0.0    1.0    0.0   
3      0.0  0.888889  0.000000    0.0    0.0  0.625000    0.0    0.0    0.0   
4      0.0  0.000000  0.000000    0.0    0.0  0.625000    0.0    0.0    0.0   
..     ...       ...       ...    ...    ...       ...    ...    ...    ...   
124    0.0  0.666667  0.629412    0.0    0.0  0.000000    0.0    1.0    1.0   
125    0.1  0.888889  0.729412    0.0    0.0  0.000000    0.0    1.0    1.0   
126    0.0  0.222222  0.800000    0.0    1.0  0.000000    0.0    1.0    1.0   
127    0.0  0.333333  0.835294    0.0    0.0  0.000000    0.0    1.0    1.0   
128    0.0  0.666667  0.370588    0.0    1.0  0.000000    0.0    1.0    1.0   

     X_255  ...    X_2860    X_2861    X_2862    X_2863    X_2864  X_2865  \
0      0.0  ...  0.526316  0.601597  0.503534  0.270270  0.345174   0.475   
1      0.0  ...  0.415789  0.478605  0.464664  0.270270  0.332216   0.475   
2      0.0  ...  0.563158  0.577864  0.597173  0.297297  0.287449   0.325   
3      0.0  ...  0.698246  0.679636  0.646643  0.270270  0.304180   0.475   
4      0.0  ...  0.533333  0.518925  0.545936  0.270270  0.325736   0.300   
..     ...  ...       ...       ...       ...       ...       ...     ...   
124    0.0  ...  0.549123  0.503225  0.392226  0.540541  0.607884   0.475   
125    0.0  ...  0.624561  0.742582  0.761484  0.810811  0.831899   0.775   
126    0.0  ...  0.652632  0.734162  0.719081  0.810811  0.810285   0.725   
127    0.0  ...  0.712281  0.800842  0.727915  0.810811  0.854712   0.825   
128    0.0  ...  0.705263  0.842469  0.789753  0.972973  0.988990   0.950   

         HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0    0.869565  0.440678     1.000000            0.0  
1    0.304348  0.237288     0.166667            0.0  
2    0.173913  0.762712     0.333333            0.0  
3    0.521739  0.440678     0.333333            0.0  
4    0.521739  0.576271     0.333333            0.0  
..        ...       ...          ...            ...  
124  0.652174  0.474576     0.166667            1.0  
125  0.652174  0.983051     0.666667            1.0  
126  0.434783  0.661017     1.000000            1.0  
127  0.652174  0.644068     0.000000            1.0  
128  0.478261  0.288136     0.000000            1.0  

[129 rows x 882 columns]

In [69]:
T01_y_class = pd.DataFrame(T01_target, columns = ['Y_Quality'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_data = pd.concat([T01_data, T01_y_class], axis = 1)
T01_data = T01_data.set_index('index')
T01_data.drop(['Y_Quality'], axis = 1, inplace = True)
T01_data

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
index                                                                           
28       0.0  0.222222  0.000000    0.0    0.0  0.535714    0.0    0.0    0.0   
33       0.0  0.888889  0.000000    0.0    0.0  0.583333    0.0    0.0    0.0   
39       0.0  0.888889  0.000000    0.0    0.0  0.607143    0.0    1.0    0.0   
40       0.0  0.888889  0.000000    0.0    0.0  0.625000    0.0    0.0    0.0   
41       0.0  0.000000  0.000000    0.0    0.0  0.625000    0.0    0.0    0.0   
...      ...       ...       ...    ...    ...       ...    ...    ...    ...   
479      0.0  0.666667  0.629412    0.0    0.0  0.000000    0.0    1.0    1.0   
501      0.1  0.888889  0.729412    0.0    0.0  0.000000    0.0    1.0    1.0   
523      0.0  0.222222  0.800000    0.0    1.0  0.000000    0.0    1.0    1.0   
531      0.0  0.333333  0.835294    0.0    0.0  0.000000    0.0    1.0    1.0   
585      0.0  0.666667  0.370588    0.0    1.0  0.000000    0.0    1.0    1.0   

       X_255  ...    X_2860    X_2861    X_2862    X_2863    X_2864  X_2865  \
index         ...                                                             
28       0.0  ...  0.526316  0.601597  0.503534  0.270270  0.345174   0.475   
33       0.0  ...  0.415789  0.478605  0.464664  0.270270  0.332216   0.475   
39       0.0  ...  0.563158  0.577864  0.597173  0.297297  0.287449   0.325   
40       0.0  ...  0.698246  0.679636  0.646643  0.270270  0.304180   0.475   
41       0.0  ...  0.533333  0.518925  0.545936  0.270270  0.325736   0.300   
...      ...  ...       ...       ...       ...       ...       ...     ...   
479      0.0  ...  0.549123  0.503225  0.392226  0.540541  0.607884   0.475   
501      0.0  ...  0.624561  0.742582  0.761484  0.810811  0.831899   0.775   
523      0.0  ...  0.652632  0.734162  0.719081  0.810811  0.810285   0.725   
531      0.0  ...  0.712281  0.800842  0.727915  0.810811  0.854712   0.825   
585      0.0  ...  0.705263  0.842469  0.789753  0.972973  0.988990   0.950   

           HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
index                                                  
28     0.869565  0.440678     1.000000            0.0  
33     0.304348  0.237288     0.166667            0.0  
39     0.173913  0.762712     0.333333            0.0  
40     0.521739  0.440678     0.333333            0.0  
41     0.521739  0.576271     0.333333            0.0  
...         ...       ...          ...            ...  
479    0.652174  0.474576     0.166667            1.0  
501    0.652174  0.983051     0.666667            1.0  
523    0.434783  0.661017     1.000000            1.0  
531    0.652174  0.644068     0.000000            1.0  
585    0.478261  0.288136     0.000000            1.0  

[129 rows x 882 columns]

In [70]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T01_data, target = T01_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [71]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbr = create_model('gbr', fold = 5)
T01_total_models.append(T01_model_gbr)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [72]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbr = tune_model(T01_model_gbr, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [73]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbr, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]
T01_tuned_models

[LGBMRegressor(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance_type='split', learning_rate=0.1, max_depth=-1,
               min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
               n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
               random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
               subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='squared_error',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       max_samples=None, min_impurity_decrease=0.0,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
                       oob_score=False, random_state=414, verbose=0,
                       warm_start=False),
 GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, c

In [74]:
for model in T01_tuned_models:
    display(predict_model(model))

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.1  0.444444  0.000000    0.0    0.0  0.226190    0.0    0.0    0.0   
91     0.0  0.888889  0.000000    0.0    0.0  0.166667    0.0    0.0    0.0   
92     0.1  0.000000  0.000000    0.0    0.0  0.750000    0.0    0.0    0.0   
93     0.0  0.888889  0.388235    0.0    0.0  0.000000    0.0    1.0    1.0   
94     0.0  0.444444  0.147059    0.0    1.0  0.000000    0.0    1.0    1.0   
95     0.0  0.222222  0.000000    0.0    0.0  0.726190    0.0    0.0    0.0   
96     0.0  0.222222  0.382353    0.0    1.0  0.000000    0.0    1.0    1.0   
97     0.0  0.000000  0.847059    0.0    1.0  0.000000    0.0    1.0    1.0   
98     0.0  0.666667  0.117647    0.0    1.0  0.000000    0.0    1.0    1.0   
99     0.0  0.666667  0.629412    0.0    0.0  0.000000    0.0    1.0    1.0   
100    0.0  0.666667  0.888235    0.0    1.0  0.000000    0.0    1.0    1.0   
101    0.1  0.444444  0.929412    0.0    0.0  0.000000    0.0    1.0    1.0   
102    0.0  0.666667  0.811765    0.0    0.0  0.000000    0.0    1.0    1.0   
103    0.0  0.222222  0.452941    0.0    1.0  0.000000    0.0    1.0    1.0   
104    0.1  0.444444  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
105    0.0  0.222222  0.041176    0.0    1.0  0.000000    0.0    1.0    1.0   
106    0.0  0.333333  0.835294    0.0    0.0  0.000000    0.0    1.0    1.0   
107    0.1  0.444444  0.476471    0.0    1.0  0.000000    0.0    1.0    1.0   
108    0.0  0.000000  0.000000    0.0    0.0  0.065476    0.0    0.0    0.0   
109    0.0  0.111111  0.070588    0.0    1.0  0.000000    0.0    1.0    1.0   
110    0.0  0.888889  0.000000    0.0    0.0  0.583333    0.0    0.0    0.0   
111    0.0  0.222222  0.000000    0.0    0.0  0.077381    0.0    1.0    0.0   
112    0.1  1.000000  0.205882    0.0    1.0  0.000000    0.0    1.0    1.0   
113    0.1  0.666667  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
114    0.0  0.333333  0.000000    0.0    0.0  0.208333    0.0    0.0    0.0   
115    0.0  0.111111  0.488235    0.0    1.0  0.000000    0.0    1.0    1.0   
116    0.1  0.444444  0.000000    0.0    0.0  0.398810    0.0    0.0    0.0   
117    0.1  0.111111  0.000000    0.0    0.0  0.535714    0.0    0.0    0.0   
118    0.0  0.888889  0.000000    0.0    0.0  0.130952    0.0    0.0    0.0   
119    0.0  0.111111  0.000000    0.0    0.0  0.571429    0.0    0.0    0.0   
120    0.1  0.111111  0.000000    0.0    0.0  0.505952    0.0    0.0    0.0   
121    0.0  0.888889  0.852941    0.0    0.0  0.000000    0.0    1.0    1.0   
122    0.0  0.111111  0.000000    0.0    0.0  0.994048    0.0    0.0    0.0   
123    0.0  0.222222  0.141176    0.0    1.0  0.000000    0.0    1.0    1.0   
124    0.0  0.222222  0.000000    0.0    0.0  0.767857    0.0    0.0    0.0   
125    0.0  0.222222  0.364706    0.0    0.0  0.000000    0.0    1.0    1.0   
126    0.0  0.222222  0.305882    0.0    1.0  0.000000    0.0    1.0    1.0   
127    0.1  0.111111  0.000000    0.0    0.0  0.250000    0.0    0.0    0.0   
128    0.0  0.666667  0.023529    0.0    0.0  0.000000    0.0    1.0    1.0   

     X_255  ...    X_2862    X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ...  0.332155  0.540541  0.652651   0.725  0.086957  0.576271   
91     0.0  ...  0.325088  0.540541  0.622972   0.700  0.652174  0.525424   
92     0.0  ...  0.761484  0.729730  0.693294   0.725  0.782609  0.881356   
93     0.0  ...  0.393993  0.540541  0.702821   0.700  0.739130  0.271186   
94     0.0  ...  0.623675  0.810811  0.848709   0.725  0.304348  0.559322   
95     0.0  ...  0.807420  0.783784  0.725634   0.725  0.478261  0.525424   
96     0.0  ...  0.416961  0.810811  0.944166   0.950  0.652174  0.542373   
97     0.0  ...  0.492933  0.270270  0.367818   0.475  0.869565  0.305085   
98     0.0  ...  0.690813  0.540541  0.667377   0.725  0.739130  0.118644   
99     0.0  ...  0.392226  0.540541  0.607884   0.475  0.652174  0.474576 

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.1  0.444444  0.000000    0.0    0.0  0.226190    0.0    0.0    0.0   
91     0.0  0.888889  0.000000    0.0    0.0  0.166667    0.0    0.0    0.0   
92     0.1  0.000000  0.000000    0.0    0.0  0.750000    0.0    0.0    0.0   
93     0.0  0.888889  0.388235    0.0    0.0  0.000000    0.0    1.0    1.0   
94     0.0  0.444444  0.147059    0.0    1.0  0.000000    0.0    1.0    1.0   
95     0.0  0.222222  0.000000    0.0    0.0  0.726190    0.0    0.0    0.0   
96     0.0  0.222222  0.382353    0.0    1.0  0.000000    0.0    1.0    1.0   
97     0.0  0.000000  0.847059    0.0    1.0  0.000000    0.0    1.0    1.0   
98     0.0  0.666667  0.117647    0.0    1.0  0.000000    0.0    1.0    1.0   
99     0.0  0.666667  0.629412    0.0    0.0  0.000000    0.0    1.0    1.0   
100    0.0  0.666667  0.888235    0.0    1.0  0.000000    0.0    1.0    1.0   
101    0.1  0.444444  0.929412    0.0    0.0  0.000000    0.0    1.0    1.0   
102    0.0  0.666667  0.811765    0.0    0.0  0.000000    0.0    1.0    1.0   
103    0.0  0.222222  0.452941    0.0    1.0  0.000000    0.0    1.0    1.0   
104    0.1  0.444444  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
105    0.0  0.222222  0.041176    0.0    1.0  0.000000    0.0    1.0    1.0   
106    0.0  0.333333  0.835294    0.0    0.0  0.000000    0.0    1.0    1.0   
107    0.1  0.444444  0.476471    0.0    1.0  0.000000    0.0    1.0    1.0   
108    0.0  0.000000  0.000000    0.0    0.0  0.065476    0.0    0.0    0.0   
109    0.0  0.111111  0.070588    0.0    1.0  0.000000    0.0    1.0    1.0   
110    0.0  0.888889  0.000000    0.0    0.0  0.583333    0.0    0.0    0.0   
111    0.0  0.222222  0.000000    0.0    0.0  0.077381    0.0    1.0    0.0   
112    0.1  1.000000  0.205882    0.0    1.0  0.000000    0.0    1.0    1.0   
113    0.1  0.666667  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
114    0.0  0.333333  0.000000    0.0    0.0  0.208333    0.0    0.0    0.0   
115    0.0  0.111111  0.488235    0.0    1.0  0.000000    0.0    1.0    1.0   
116    0.1  0.444444  0.000000    0.0    0.0  0.398810    0.0    0.0    0.0   
117    0.1  0.111111  0.000000    0.0    0.0  0.535714    0.0    0.0    0.0   
118    0.0  0.888889  0.000000    0.0    0.0  0.130952    0.0    0.0    0.0   
119    0.0  0.111111  0.000000    0.0    0.0  0.571429    0.0    0.0    0.0   
120    0.1  0.111111  0.000000    0.0    0.0  0.505952    0.0    0.0    0.0   
121    0.0  0.888889  0.852941    0.0    0.0  0.000000    0.0    1.0    1.0   
122    0.0  0.111111  0.000000    0.0    0.0  0.994048    0.0    0.0    0.0   
123    0.0  0.222222  0.141176    0.0    1.0  0.000000    0.0    1.0    1.0   
124    0.0  0.222222  0.000000    0.0    0.0  0.767857    0.0    0.0    0.0   
125    0.0  0.222222  0.364706    0.0    0.0  0.000000    0.0    1.0    1.0   
126    0.0  0.222222  0.305882    0.0    1.0  0.000000    0.0    1.0    1.0   
127    0.1  0.111111  0.000000    0.0    0.0  0.250000    0.0    0.0    0.0   
128    0.0  0.666667  0.023529    0.0    0.0  0.000000    0.0    1.0    1.0   

     X_255  ...    X_2862    X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ...  0.332155  0.540541  0.652651   0.725  0.086957  0.576271   
91     0.0  ...  0.325088  0.540541  0.622972   0.700  0.652174  0.525424   
92     0.0  ...  0.761484  0.729730  0.693294   0.725  0.782609  0.881356   
93     0.0  ...  0.393993  0.540541  0.702821   0.700  0.739130  0.271186   
94     0.0  ...  0.623675  0.810811  0.848709   0.725  0.304348  0.559322   
95     0.0  ...  0.807420  0.783784  0.725634   0.725  0.478261  0.525424   
96     0.0  ...  0.416961  0.810811  0.944166   0.950  0.652174  0.542373   
97     0.0  ...  0.492933  0.270270  0.367818   0.475  0.869565  0.305085   
98     0.0  ...  0.690813  0.540541  0.667377   0.725  0.739130  0.118644   
99     0.0  ...  0.392226  0.540541  0.607884   0.475  0.652174  0.474576 

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.1  0.444444  0.000000    0.0    0.0  0.226190    0.0    0.0    0.0   
91     0.0  0.888889  0.000000    0.0    0.0  0.166667    0.0    0.0    0.0   
92     0.1  0.000000  0.000000    0.0    0.0  0.750000    0.0    0.0    0.0   
93     0.0  0.888889  0.388235    0.0    0.0  0.000000    0.0    1.0    1.0   
94     0.0  0.444444  0.147059    0.0    1.0  0.000000    0.0    1.0    1.0   
95     0.0  0.222222  0.000000    0.0    0.0  0.726190    0.0    0.0    0.0   
96     0.0  0.222222  0.382353    0.0    1.0  0.000000    0.0    1.0    1.0   
97     0.0  0.000000  0.847059    0.0    1.0  0.000000    0.0    1.0    1.0   
98     0.0  0.666667  0.117647    0.0    1.0  0.000000    0.0    1.0    1.0   
99     0.0  0.666667  0.629412    0.0    0.0  0.000000    0.0    1.0    1.0   
100    0.0  0.666667  0.888235    0.0    1.0  0.000000    0.0    1.0    1.0   
101    0.1  0.444444  0.929412    0.0    0.0  0.000000    0.0    1.0    1.0   
102    0.0  0.666667  0.811765    0.0    0.0  0.000000    0.0    1.0    1.0   
103    0.0  0.222222  0.452941    0.0    1.0  0.000000    0.0    1.0    1.0   
104    0.1  0.444444  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
105    0.0  0.222222  0.041176    0.0    1.0  0.000000    0.0    1.0    1.0   
106    0.0  0.333333  0.835294    0.0    0.0  0.000000    0.0    1.0    1.0   
107    0.1  0.444444  0.476471    0.0    1.0  0.000000    0.0    1.0    1.0   
108    0.0  0.000000  0.000000    0.0    0.0  0.065476    0.0    0.0    0.0   
109    0.0  0.111111  0.070588    0.0    1.0  0.000000    0.0    1.0    1.0   
110    0.0  0.888889  0.000000    0.0    0.0  0.583333    0.0    0.0    0.0   
111    0.0  0.222222  0.000000    0.0    0.0  0.077381    0.0    1.0    0.0   
112    0.1  1.000000  0.205882    0.0    1.0  0.000000    0.0    1.0    1.0   
113    0.1  0.666667  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
114    0.0  0.333333  0.000000    0.0    0.0  0.208333    0.0    0.0    0.0   
115    0.0  0.111111  0.488235    0.0    1.0  0.000000    0.0    1.0    1.0   
116    0.1  0.444444  0.000000    0.0    0.0  0.398810    0.0    0.0    0.0   
117    0.1  0.111111  0.000000    0.0    0.0  0.535714    0.0    0.0    0.0   
118    0.0  0.888889  0.000000    0.0    0.0  0.130952    0.0    0.0    0.0   
119    0.0  0.111111  0.000000    0.0    0.0  0.571429    0.0    0.0    0.0   
120    0.1  0.111111  0.000000    0.0    0.0  0.505952    0.0    0.0    0.0   
121    0.0  0.888889  0.852941    0.0    0.0  0.000000    0.0    1.0    1.0   
122    0.0  0.111111  0.000000    0.0    0.0  0.994048    0.0    0.0    0.0   
123    0.0  0.222222  0.141176    0.0    1.0  0.000000    0.0    1.0    1.0   
124    0.0  0.222222  0.000000    0.0    0.0  0.767857    0.0    0.0    0.0   
125    0.0  0.222222  0.364706    0.0    0.0  0.000000    0.0    1.0    1.0   
126    0.0  0.222222  0.305882    0.0    1.0  0.000000    0.0    1.0    1.0   
127    0.1  0.111111  0.000000    0.0    0.0  0.250000    0.0    0.0    0.0   
128    0.0  0.666667  0.023529    0.0    0.0  0.000000    0.0    1.0    1.0   

     X_255  ...    X_2862    X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ...  0.332155  0.540541  0.652651   0.725  0.086957  0.576271   
91     0.0  ...  0.325088  0.540541  0.622972   0.700  0.652174  0.525424   
92     0.0  ...  0.761484  0.729730  0.693294   0.725  0.782609  0.881356   
93     0.0  ...  0.393993  0.540541  0.702821   0.700  0.739130  0.271186   
94     0.0  ...  0.623675  0.810811  0.848709   0.725  0.304348  0.559322   
95     0.0  ...  0.807420  0.783784  0.725634   0.725  0.478261  0.525424   
96     0.0  ...  0.416961  0.810811  0.944166   0.950  0.652174  0.542373   
97     0.0  ...  0.492933  0.270270  0.367818   0.475  0.869565  0.305085   
98     0.0  ...  0.690813  0.540541  0.667377   0.725  0.739130  0.118644   
99     0.0  ...  0.392226  0.540541  0.607884   0.475  0.652174  0.474576 

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.1  0.444444  0.000000    0.0    0.0  0.226190    0.0    0.0    0.0   
91     0.0  0.888889  0.000000    0.0    0.0  0.166667    0.0    0.0    0.0   
92     0.1  0.000000  0.000000    0.0    0.0  0.750000    0.0    0.0    0.0   
93     0.0  0.888889  0.388235    0.0    0.0  0.000000    0.0    1.0    1.0   
94     0.0  0.444444  0.147059    0.0    1.0  0.000000    0.0    1.0    1.0   
95     0.0  0.222222  0.000000    0.0    0.0  0.726190    0.0    0.0    0.0   
96     0.0  0.222222  0.382353    0.0    1.0  0.000000    0.0    1.0    1.0   
97     0.0  0.000000  0.847059    0.0    1.0  0.000000    0.0    1.0    1.0   
98     0.0  0.666667  0.117647    0.0    1.0  0.000000    0.0    1.0    1.0   
99     0.0  0.666667  0.629412    0.0    0.0  0.000000    0.0    1.0    1.0   
100    0.0  0.666667  0.888235    0.0    1.0  0.000000    0.0    1.0    1.0   
101    0.1  0.444444  0.929412    0.0    0.0  0.000000    0.0    1.0    1.0   
102    0.0  0.666667  0.811765    0.0    0.0  0.000000    0.0    1.0    1.0   
103    0.0  0.222222  0.452941    0.0    1.0  0.000000    0.0    1.0    1.0   
104    0.1  0.444444  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
105    0.0  0.222222  0.041176    0.0    1.0  0.000000    0.0    1.0    1.0   
106    0.0  0.333333  0.835294    0.0    0.0  0.000000    0.0    1.0    1.0   
107    0.1  0.444444  0.476471    0.0    1.0  0.000000    0.0    1.0    1.0   
108    0.0  0.000000  0.000000    0.0    0.0  0.065476    0.0    0.0    0.0   
109    0.0  0.111111  0.070588    0.0    1.0  0.000000    0.0    1.0    1.0   
110    0.0  0.888889  0.000000    0.0    0.0  0.583333    0.0    0.0    0.0   
111    0.0  0.222222  0.000000    0.0    0.0  0.077381    0.0    1.0    0.0   
112    0.1  1.000000  0.205882    0.0    1.0  0.000000    0.0    1.0    1.0   
113    0.1  0.666667  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
114    0.0  0.333333  0.000000    0.0    0.0  0.208333    0.0    0.0    0.0   
115    0.0  0.111111  0.488235    0.0    1.0  0.000000    0.0    1.0    1.0   
116    0.1  0.444444  0.000000    0.0    0.0  0.398810    0.0    0.0    0.0   
117    0.1  0.111111  0.000000    0.0    0.0  0.535714    0.0    0.0    0.0   
118    0.0  0.888889  0.000000    0.0    0.0  0.130952    0.0    0.0    0.0   
119    0.0  0.111111  0.000000    0.0    0.0  0.571429    0.0    0.0    0.0   
120    0.1  0.111111  0.000000    0.0    0.0  0.505952    0.0    0.0    0.0   
121    0.0  0.888889  0.852941    0.0    0.0  0.000000    0.0    1.0    1.0   
122    0.0  0.111111  0.000000    0.0    0.0  0.994048    0.0    0.0    0.0   
123    0.0  0.222222  0.141176    0.0    1.0  0.000000    0.0    1.0    1.0   
124    0.0  0.222222  0.000000    0.0    0.0  0.767857    0.0    0.0    0.0   
125    0.0  0.222222  0.364706    0.0    0.0  0.000000    0.0    1.0    1.0   
126    0.0  0.222222  0.305882    0.0    1.0  0.000000    0.0    1.0    1.0   
127    0.1  0.111111  0.000000    0.0    0.0  0.250000    0.0    0.0    0.0   
128    0.0  0.666667  0.023529    0.0    0.0  0.000000    0.0    1.0    1.0   

     X_255  ...    X_2862    X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ...  0.332155  0.540541  0.652651   0.725  0.086957  0.576271   
91     0.0  ...  0.325088  0.540541  0.622972   0.700  0.652174  0.525424   
92     0.0  ...  0.761484  0.729730  0.693294   0.725  0.782609  0.881356   
93     0.0  ...  0.393993  0.540541  0.702821   0.700  0.739130  0.271186   
94     0.0  ...  0.623675  0.810811  0.848709   0.725  0.304348  0.559322   
95     0.0  ...  0.807420  0.783784  0.725634   0.725  0.478261  0.525424   
96     0.0  ...  0.416961  0.810811  0.944166   0.950  0.652174  0.542373   
97     0.0  ...  0.492933  0.270270  0.367818   0.475  0.869565  0.305085   
98     0.0  ...  0.690813  0.540541  0.667377   0.725  0.739130  0.118644   
99     0.0  ...  0.392226  0.540541  0.607884   0.475  0.652174  0.474576 

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.1  0.444444  0.000000    0.0    0.0  0.226190    0.0    0.0    0.0   
91     0.0  0.888889  0.000000    0.0    0.0  0.166667    0.0    0.0    0.0   
92     0.1  0.000000  0.000000    0.0    0.0  0.750000    0.0    0.0    0.0   
93     0.0  0.888889  0.388235    0.0    0.0  0.000000    0.0    1.0    1.0   
94     0.0  0.444444  0.147059    0.0    1.0  0.000000    0.0    1.0    1.0   
95     0.0  0.222222  0.000000    0.0    0.0  0.726190    0.0    0.0    0.0   
96     0.0  0.222222  0.382353    0.0    1.0  0.000000    0.0    1.0    1.0   
97     0.0  0.000000  0.847059    0.0    1.0  0.000000    0.0    1.0    1.0   
98     0.0  0.666667  0.117647    0.0    1.0  0.000000    0.0    1.0    1.0   
99     0.0  0.666667  0.629412    0.0    0.0  0.000000    0.0    1.0    1.0   
100    0.0  0.666667  0.888235    0.0    1.0  0.000000    0.0    1.0    1.0   
101    0.1  0.444444  0.929412    0.0    0.0  0.000000    0.0    1.0    1.0   
102    0.0  0.666667  0.811765    0.0    0.0  0.000000    0.0    1.0    1.0   
103    0.0  0.222222  0.452941    0.0    1.0  0.000000    0.0    1.0    1.0   
104    0.1  0.444444  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
105    0.0  0.222222  0.041176    0.0    1.0  0.000000    0.0    1.0    1.0   
106    0.0  0.333333  0.835294    0.0    0.0  0.000000    0.0    1.0    1.0   
107    0.1  0.444444  0.476471    0.0    1.0  0.000000    0.0    1.0    1.0   
108    0.0  0.000000  0.000000    0.0    0.0  0.065476    0.0    0.0    0.0   
109    0.0  0.111111  0.070588    0.0    1.0  0.000000    0.0    1.0    1.0   
110    0.0  0.888889  0.000000    0.0    0.0  0.583333    0.0    0.0    0.0   
111    0.0  0.222222  0.000000    0.0    0.0  0.077381    0.0    1.0    0.0   
112    0.1  1.000000  0.205882    0.0    1.0  0.000000    0.0    1.0    1.0   
113    0.1  0.666667  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
114    0.0  0.333333  0.000000    0.0    0.0  0.208333    0.0    0.0    0.0   
115    0.0  0.111111  0.488235    0.0    1.0  0.000000    0.0    1.0    1.0   
116    0.1  0.444444  0.000000    0.0    0.0  0.398810    0.0    0.0    0.0   
117    0.1  0.111111  0.000000    0.0    0.0  0.535714    0.0    0.0    0.0   
118    0.0  0.888889  0.000000    0.0    0.0  0.130952    0.0    0.0    0.0   
119    0.0  0.111111  0.000000    0.0    0.0  0.571429    0.0    0.0    0.0   
120    0.1  0.111111  0.000000    0.0    0.0  0.505952    0.0    0.0    0.0   
121    0.0  0.888889  0.852941    0.0    0.0  0.000000    0.0    1.0    1.0   
122    0.0  0.111111  0.000000    0.0    0.0  0.994048    0.0    0.0    0.0   
123    0.0  0.222222  0.141176    0.0    1.0  0.000000    0.0    1.0    1.0   
124    0.0  0.222222  0.000000    0.0    0.0  0.767857    0.0    0.0    0.0   
125    0.0  0.222222  0.364706    0.0    0.0  0.000000    0.0    1.0    1.0   
126    0.0  0.222222  0.305882    0.0    1.0  0.000000    0.0    1.0    1.0   
127    0.1  0.111111  0.000000    0.0    0.0  0.250000    0.0    0.0    0.0   
128    0.0  0.666667  0.023529    0.0    0.0  0.000000    0.0    1.0    1.0   

     X_255  ...    X_2862    X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ...  0.332155  0.540541  0.652651   0.725  0.086957  0.576271   
91     0.0  ...  0.325088  0.540541  0.622972   0.700  0.652174  0.525424   
92     0.0  ...  0.761484  0.729730  0.693294   0.725  0.782609  0.881356   
93     0.0  ...  0.393993  0.540541  0.702821   0.700  0.739130  0.271186   
94     0.0  ...  0.623675  0.810811  0.848709   0.725  0.304348  0.559322   
95     0.0  ...  0.807420  0.783784  0.725634   0.725  0.478261  0.525424   
96     0.0  ...  0.416961  0.810811  0.944166   0.950  0.652174  0.542373   
97     0.0  ...  0.492933  0.270270  0.367818   0.475  0.869565  0.305085   
98     0.0  ...  0.690813  0.540541  0.667377   0.725  0.739130  0.118644   
99     0.0  ...  0.392226  0.540541  0.607884   0.475  0.652174  0.474576 

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.1  0.444444  0.000000    0.0    0.0  0.226190    0.0    0.0    0.0   
91     0.0  0.888889  0.000000    0.0    0.0  0.166667    0.0    0.0    0.0   
92     0.1  0.000000  0.000000    0.0    0.0  0.750000    0.0    0.0    0.0   
93     0.0  0.888889  0.388235    0.0    0.0  0.000000    0.0    1.0    1.0   
94     0.0  0.444444  0.147059    0.0    1.0  0.000000    0.0    1.0    1.0   
95     0.0  0.222222  0.000000    0.0    0.0  0.726190    0.0    0.0    0.0   
96     0.0  0.222222  0.382353    0.0    1.0  0.000000    0.0    1.0    1.0   
97     0.0  0.000000  0.847059    0.0    1.0  0.000000    0.0    1.0    1.0   
98     0.0  0.666667  0.117647    0.0    1.0  0.000000    0.0    1.0    1.0   
99     0.0  0.666667  0.629412    0.0    0.0  0.000000    0.0    1.0    1.0   
100    0.0  0.666667  0.888235    0.0    1.0  0.000000    0.0    1.0    1.0   
101    0.1  0.444444  0.929412    0.0    0.0  0.000000    0.0    1.0    1.0   
102    0.0  0.666667  0.811765    0.0    0.0  0.000000    0.0    1.0    1.0   
103    0.0  0.222222  0.452941    0.0    1.0  0.000000    0.0    1.0    1.0   
104    0.1  0.444444  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
105    0.0  0.222222  0.041176    0.0    1.0  0.000000    0.0    1.0    1.0   
106    0.0  0.333333  0.835294    0.0    0.0  0.000000    0.0    1.0    1.0   
107    0.1  0.444444  0.476471    0.0    1.0  0.000000    0.0    1.0    1.0   
108    0.0  0.000000  0.000000    0.0    0.0  0.065476    0.0    0.0    0.0   
109    0.0  0.111111  0.070588    0.0    1.0  0.000000    0.0    1.0    1.0   
110    0.0  0.888889  0.000000    0.0    0.0  0.583333    0.0    0.0    0.0   
111    0.0  0.222222  0.000000    0.0    0.0  0.077381    0.0    1.0    0.0   
112    0.1  1.000000  0.205882    0.0    1.0  0.000000    0.0    1.0    1.0   
113    0.1  0.666667  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
114    0.0  0.333333  0.000000    0.0    0.0  0.208333    0.0    0.0    0.0   
115    0.0  0.111111  0.488235    0.0    1.0  0.000000    0.0    1.0    1.0   
116    0.1  0.444444  0.000000    0.0    0.0  0.398810    0.0    0.0    0.0   
117    0.1  0.111111  0.000000    0.0    0.0  0.535714    0.0    0.0    0.0   
118    0.0  0.888889  0.000000    0.0    0.0  0.130952    0.0    0.0    0.0   
119    0.0  0.111111  0.000000    0.0    0.0  0.571429    0.0    0.0    0.0   
120    0.1  0.111111  0.000000    0.0    0.0  0.505952    0.0    0.0    0.0   
121    0.0  0.888889  0.852941    0.0    0.0  0.000000    0.0    1.0    1.0   
122    0.0  0.111111  0.000000    0.0    0.0  0.994048    0.0    0.0    0.0   
123    0.0  0.222222  0.141176    0.0    1.0  0.000000    0.0    1.0    1.0   
124    0.0  0.222222  0.000000    0.0    0.0  0.767857    0.0    0.0    0.0   
125    0.0  0.222222  0.364706    0.0    0.0  0.000000    0.0    1.0    1.0   
126    0.0  0.222222  0.305882    0.0    1.0  0.000000    0.0    1.0    1.0   
127    0.1  0.111111  0.000000    0.0    0.0  0.250000    0.0    0.0    0.0   
128    0.0  0.666667  0.023529    0.0    0.0  0.000000    0.0    1.0    1.0   

     X_255  ...    X_2862    X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ...  0.332155  0.540541  0.652651   0.725  0.086957  0.576271   
91     0.0  ...  0.325088  0.540541  0.622972   0.700  0.652174  0.525424   
92     0.0  ...  0.761484  0.729730  0.693294   0.725  0.782609  0.881356   
93     0.0  ...  0.393993  0.540541  0.702821   0.700  0.739130  0.271186   
94     0.0  ...  0.623675  0.810811  0.848709   0.725  0.304348  0.559322   
95     0.0  ...  0.807420  0.783784  0.725634   0.725  0.478261  0.525424   
96     0.0  ...  0.416961  0.810811  0.944166   0.950  0.652174  0.542373   
97     0.0  ...  0.492933  0.270270  0.367818   0.475  0.869565  0.305085   
98     0.0  ...  0.690813  0.540541  0.667377   0.725  0.739130  0.118644   
99     0.0  ...  0.392226  0.540541  0.607884   0.475  0.652174  0.474576 

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.1  0.444444  0.000000    0.0    0.0  0.226190    0.0    0.0    0.0   
91     0.0  0.888889  0.000000    0.0    0.0  0.166667    0.0    0.0    0.0   
92     0.1  0.000000  0.000000    0.0    0.0  0.750000    0.0    0.0    0.0   
93     0.0  0.888889  0.388235    0.0    0.0  0.000000    0.0    1.0    1.0   
94     0.0  0.444444  0.147059    0.0    1.0  0.000000    0.0    1.0    1.0   
95     0.0  0.222222  0.000000    0.0    0.0  0.726190    0.0    0.0    0.0   
96     0.0  0.222222  0.382353    0.0    1.0  0.000000    0.0    1.0    1.0   
97     0.0  0.000000  0.847059    0.0    1.0  0.000000    0.0    1.0    1.0   
98     0.0  0.666667  0.117647    0.0    1.0  0.000000    0.0    1.0    1.0   
99     0.0  0.666667  0.629412    0.0    0.0  0.000000    0.0    1.0    1.0   
100    0.0  0.666667  0.888235    0.0    1.0  0.000000    0.0    1.0    1.0   
101    0.1  0.444444  0.929412    0.0    0.0  0.000000    0.0    1.0    1.0   
102    0.0  0.666667  0.811765    0.0    0.0  0.000000    0.0    1.0    1.0   
103    0.0  0.222222  0.452941    0.0    1.0  0.000000    0.0    1.0    1.0   
104    0.1  0.444444  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
105    0.0  0.222222  0.041176    0.0    1.0  0.000000    0.0    1.0    1.0   
106    0.0  0.333333  0.835294    0.0    0.0  0.000000    0.0    1.0    1.0   
107    0.1  0.444444  0.476471    0.0    1.0  0.000000    0.0    1.0    1.0   
108    0.0  0.000000  0.000000    0.0    0.0  0.065476    0.0    0.0    0.0   
109    0.0  0.111111  0.070588    0.0    1.0  0.000000    0.0    1.0    1.0   
110    0.0  0.888889  0.000000    0.0    0.0  0.583333    0.0    0.0    0.0   
111    0.0  0.222222  0.000000    0.0    0.0  0.077381    0.0    1.0    0.0   
112    0.1  1.000000  0.205882    0.0    1.0  0.000000    0.0    1.0    1.0   
113    0.1  0.666667  1.000000    0.0    0.0  0.000000    0.0    1.0    1.0   
114    0.0  0.333333  0.000000    0.0    0.0  0.208333    0.0    0.0    0.0   
115    0.0  0.111111  0.488235    0.0    1.0  0.000000    0.0    1.0    1.0   
116    0.1  0.444444  0.000000    0.0    0.0  0.398810    0.0    0.0    0.0   
117    0.1  0.111111  0.000000    0.0    0.0  0.535714    0.0    0.0    0.0   
118    0.0  0.888889  0.000000    0.0    0.0  0.130952    0.0    0.0    0.0   
119    0.0  0.111111  0.000000    0.0    0.0  0.571429    0.0    0.0    0.0   
120    0.1  0.111111  0.000000    0.0    0.0  0.505952    0.0    0.0    0.0   
121    0.0  0.888889  0.852941    0.0    0.0  0.000000    0.0    1.0    1.0   
122    0.0  0.111111  0.000000    0.0    0.0  0.994048    0.0    0.0    0.0   
123    0.0  0.222222  0.141176    0.0    1.0  0.000000    0.0    1.0    1.0   
124    0.0  0.222222  0.000000    0.0    0.0  0.767857    0.0    0.0    0.0   
125    0.0  0.222222  0.364706    0.0    0.0  0.000000    0.0    1.0    1.0   
126    0.0  0.222222  0.305882    0.0    1.0  0.000000    0.0    1.0    1.0   
127    0.1  0.111111  0.000000    0.0    0.0  0.250000    0.0    0.0    0.0   
128    0.0  0.666667  0.023529    0.0    0.0  0.000000    0.0    1.0    1.0   

     X_255  ...    X_2862    X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ...  0.332155  0.540541  0.652651   0.725  0.086957  0.576271   
91     0.0  ...  0.325088  0.540541  0.622972   0.700  0.652174  0.525424   
92     0.0  ...  0.761484  0.729730  0.693294   0.725  0.782609  0.881356   
93     0.0  ...  0.393993  0.540541  0.702821   0.700  0.739130  0.271186   
94     0.0  ...  0.623675  0.810811  0.848709   0.725  0.304348  0.559322   
95     0.0  ...  0.807420  0.783784  0.725634   0.725  0.478261  0.525424   
96     0.0  ...  0.416961  0.810811  0.944166   0.950  0.652174  0.542373   
97     0.0  ...  0.492933  0.270270  0.367818   0.475  0.869565  0.305085   
98     0.0  ...  0.690813  0.540541  0.667377   0.725  0.739130  0.118644   
99     0.0  ...  0.392226  0.540541  0.607884   0.475  0.652174  0.474576 

In [75]:
T01_final_regression_model = finalize_model(T01_model_et)

In [76]:
T01_prediction = predict_model(T01_final_regression_model, data=T01_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [77]:
T01_datas = T01_prediction['prediction_label']

In [78]:
T01_datas = T01_prediction['prediction_label']
T01_datas = pd.DataFrame(T01_datas.values, columns = ['Y_Quality'])
T01_datas

Y_Quality
0     0.521249
1     0.526656
2     0.531583
3     0.530829
4     0.528270
..         ...
124   0.534716
125   0.533079
126   0.534640
127   0.560317
128   0.515214

[129 rows x 1 columns]

In [79]:
T01y_idx= T01_class.index
T01y_idx = pd.DataFrame(T01y_idx, columns = ['index'])
T01_datas = pd.concat([T01y_idx, T01_datas], axis = 1)
T01_datas = T01_datas.set_index('index')
T01_datas

Y_Quality
index           
28      0.521249
33      0.526656
39      0.531583
40      0.530829
41      0.528270
...          ...
479     0.534716
501     0.533079
523     0.534640
531     0.560317
585     0.515214

[129 rows x 1 columns]

In [80]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T01_datas, 
                   target=T01_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [81]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbc = create_model('gbc', fold = 5)
T01_total_models.append(T01_model_gbc)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [82]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbc = tune_model(T01_model_gbc, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [83]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbc, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]
T01_tuned_models

[LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
                importance_type='split', learning_rate=0.1, max_depth=-1,
                min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
                n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
                random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
                subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                        criterion='gini', max_depth=None, max_features='auto',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.0, min_samples_leaf=1,
                        min_samples_split=2, min_weight_fraction_leaf=0.0,
                        n_estimators=100, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp

In [84]:
for model in T01_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1            0.9992
91    0.517938        0                 0            0.9912
92    0.524408        0                 0            0.9912
93    0.523694        0                 0            0.9912
94    0.527486        1                 1            0.9992
95    0.524487        0                 0            0.9912
96    0.530568        1                 1            0.9992
97    0.560317        2                 2            0.9999
98    0.535394        2                 2            0.9999
99    0.549381        2                 2            0.9999
100   0.528687        1                 1            0.9992
101   0.544089        2                 2            0.9999
102   0.547492        2                 2            0.9999
103   0.529171        1                 1            0.9992
104   0.547516        2                 2            0.9999
105   0.533273        1                 1            0.9992
106   0.533122        1                 1            0.9992
107   0.528190        1                 1            0.9992
108   0.531522        1                 1            0.9992
109   0.518024        0                 0            0.9912
110   0.528270        1                 1            0.9992
111   0.536951        2                 2            0.9999
112   0.531043        1                 1            0.9992
113   0.534403        1                 1            0.9992
114   0.535589        2                 2            0.9999
115   0.538502        2                 2            0.9999
116   0.530048        1                 1            0.9992
117   0.534486        1                 1            0.9992
118   0.528087        1                 1            0.9992
119   0.526906        1                 1            0.9955
120   0.525221        1                 1            0.6632
121   0.527735        1                 1            0.9992
122   0.531583        1                 1            0.9992
123   0.530022        1                 1            0.9992
124   0.527689        1                 1            0.9992
125   0.533179        1                 1            0.9992
126   0.537116        2                 2            0.9999
127   0.523714        0                 0            0.9912
128   0.538614        2                 2            0.9999

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1              1.00
91    0.517938        0                 0              1.00
92    0.524408        0                 0              0.98
93    0.523694        0                 0              0.99
94    0.527486        1                 1              1.00
95    0.524487        0                 0              0.98
96    0.530568        1                 1              1.00
97    0.560317        2                 2              1.00
98    0.535394        2                 2              0.96
99    0.549381        2                 2              1.00
100   0.528687        1                 1              1.00
101   0.544089        2                 2              1.00
102   0.547492        2                 2              1.00
103   0.529171        1                 1              1.00
104   0.547516        2                 2              1.00
105   0.533273        1                 1              1.00
106   0.533122        1                 1              1.00
107   0.528190        1                 1              1.00
108   0.531522        1                 1              1.00
109   0.518024        0                 0              1.00
110   0.528270        1                 1              1.00
111   0.536951        2                 2              1.00
112   0.531043        1                 1              1.00
113   0.534403        1                 1              1.00
114   0.535589        2                 2              1.00
115   0.538502        2                 2              1.00
116   0.530048        1                 1              1.00
117   0.534486        1                 1              1.00
118   0.528087        1                 1              1.00
119   0.526906        1                 1              1.00
120   0.525221        1                 0              0.83
121   0.527735        1                 1              1.00
122   0.531583        1                 1              1.00
123   0.530022        1                 1              1.00
124   0.527689        1                 1              1.00
125   0.533179        1                 1              1.00
126   0.537116        2                 2              1.00
127   0.523714        0                 0              0.99
128   0.538614        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1               1.0
91    0.517938        0                 0               1.0
92    0.524408        0                 0               1.0
93    0.523694        0                 0               1.0
94    0.527486        1                 1               1.0
95    0.524487        0                 0               1.0
96    0.530568        1                 1               1.0
97    0.560317        2                 2               1.0
98    0.535394        2                 2               1.0
99    0.549381        2                 2               1.0
100   0.528687        1                 1               1.0
101   0.544089        2                 2               1.0
102   0.547492        2                 2               1.0
103   0.529171        1                 1               1.0
104   0.547516        2                 2               1.0
105   0.533273        1                 1               1.0
106   0.533122        1                 1               1.0
107   0.528190        1                 1               1.0
108   0.531522        1                 1               1.0
109   0.518024        0                 0               1.0
110   0.528270        1                 1               1.0
111   0.536951        2                 2               1.0
112   0.531043        1                 1               1.0
113   0.534403        1                 1               1.0
114   0.535589        2                 2               1.0
115   0.538502        2                 2               1.0
116   0.530048        1                 1               1.0
117   0.534486        1                 1               1.0
118   0.528087        1                 1               1.0
119   0.526906        1                 1               1.0
120   0.525221        1                 0               1.0
121   0.527735        1                 1               1.0
122   0.531583        1                 1               1.0
123   0.530022        1                 1               1.0
124   0.527689        1                 1               1.0
125   0.533179        1                 1               1.0
126   0.537116        2                 2               1.0
127   0.523714        0                 0               1.0
128   0.538614        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1               1.0
91    0.517938        0                 0               1.0
92    0.524408        0                 0               1.0
93    0.523694        0                 0               1.0
94    0.527486        1                 1               1.0
95    0.524487        0                 0               1.0
96    0.530568        1                 1               1.0
97    0.560317        2                 2               1.0
98    0.535394        2                 2               1.0
99    0.549381        2                 2               1.0
100   0.528687        1                 1               1.0
101   0.544089        2                 2               1.0
102   0.547492        2                 2               1.0
103   0.529171        1                 1               1.0
104   0.547516        2                 2               1.0
105   0.533273        1                 1               1.0
106   0.533122        1                 1               1.0
107   0.528190        1                 1               1.0
108   0.531522        1                 1               1.0
109   0.518024        0                 0               1.0
110   0.528270        1                 1               1.0
111   0.536951        2                 2               1.0
112   0.531043        1                 1               1.0
113   0.534403        1                 1               1.0
114   0.535589        2                 2               1.0
115   0.538502        2                 2               1.0
116   0.530048        1                 1               1.0
117   0.534486        1                 1               1.0
118   0.528087        1                 1               1.0
119   0.526906        1                 1               1.0
120   0.525221        1                 0               0.6
121   0.527735        1                 1               1.0
122   0.531583        1                 1               1.0
123   0.530022        1                 1               1.0
124   0.527689        1                 1               1.0
125   0.533179        1                 1               1.0
126   0.537116        2                 2               1.0
127   0.523714        0                 0               1.0
128   0.538614        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1            0.9996
91    0.517938        0                 0            0.9973
92    0.524408        0                 0            0.9967
93    0.523694        0                 0            0.9972
94    0.527486        1                 1            0.9994
95    0.524487        0                 0            0.9944
96    0.530568        1                 1            0.9996
97    0.560317        2                 2            0.9982
98    0.535394        2                 2            0.9949
99    0.549381        2                 2            0.9989
100   0.528687        1                 1            0.9994
101   0.544089        2                 2            0.9991
102   0.547492        2                 2            0.9990
103   0.529171        1                 1            0.9995
104   0.547516        2                 2            0.9990
105   0.533273        1                 1            0.9995
106   0.533122        1                 1            0.9995
107   0.528190        1                 1            0.9994
108   0.531522        1                 1            0.9996
109   0.518024        0                 0            0.9973
110   0.528270        1                 1            0.9994
111   0.536951        2                 2            0.9989
112   0.531043        1                 1            0.9996
113   0.534403        1                 1            0.9991
114   0.535589        2                 2            0.9949
115   0.538502        2                 2            0.9991
116   0.530048        1                 1            0.9996
117   0.534486        1                 1            0.9987
118   0.528087        1                 1            0.9994
119   0.526906        1                 1            0.9994
120   0.525221        1                 0            0.9791
121   0.527735        1                 1            0.9994
122   0.531583        1                 1            0.9996
123   0.530022        1                 1            0.9996
124   0.527689        1                 1            0.9994
125   0.533179        1                 1            0.9995
126   0.537116        2                 2            0.9989
127   0.523714        0                 0            0.9972
128   0.538614        2                 2            0.9991

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1            0.9953
91    0.517938        0                 0            0.9665
92    0.524408        0                 0            0.9665
93    0.523694        0                 0            0.9665
94    0.527486        1                 1            0.9849
95    0.524487        0                 0            0.9665
96    0.530568        1                 1            0.9953
97    0.560317        2                 2            0.9836
98    0.535394        2                 2            0.9836
99    0.549381        2                 2            0.9836
100   0.528687        1                 1            0.9949
101   0.544089        2                 2            0.9836
102   0.547492        2                 2            0.9836
103   0.529171        1                 1            0.9953
104   0.547516        2                 2            0.9836
105   0.533273        1                 1            0.9872
106   0.533122        1                 1            0.9879
107   0.528190        1                 1            0.9904
108   0.531522        1                 1            0.9953
109   0.518024        0                 0            0.9665
110   0.528270        1                 1            0.9904
111   0.536951        2                 2            0.9836
112   0.531043        1                 1            0.9953
113   0.534403        1                 1            0.9840
114   0.535589        2                 2            0.9836
115   0.538502        2                 2            0.9836
116   0.530048        1                 1            0.9953
117   0.534486        1                 1            0.9840
118   0.528087        1                 1            0.9904
119   0.526906        1                 1            0.9833
120   0.525221        1                 0            0.9665
121   0.527735        1                 1            0.9904
122   0.531583        1                 1            0.9953
123   0.530022        1                 1            0.9953
124   0.527689        1                 1            0.9904
125   0.533179        1                 1            0.9872
126   0.537116        2                 2            0.9836
127   0.523714        0                 0            0.9665
128   0.538614        2                 2            0.9836

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1               1.0
91    0.517938        0                 0               1.0
92    0.524408        0                 0               1.0
93    0.523694        0                 0               1.0
94    0.527486        1                 1               1.0
95    0.524487        0                 0               1.0
96    0.530568        1                 1               1.0
97    0.560317        2                 2               1.0
98    0.535394        2                 2               1.0
99    0.549381        2                 2               1.0
100   0.528687        1                 1               1.0
101   0.544089        2                 2               1.0
102   0.547492        2                 2               1.0
103   0.529171        1                 1               1.0
104   0.547516        2                 2               1.0
105   0.533273        1                 1               1.0
106   0.533122        1                 1               1.0
107   0.528190        1                 1               1.0
108   0.531522        1                 1               1.0
109   0.518024        0                 0               1.0
110   0.528270        1                 1               1.0
111   0.536951        2                 2               1.0
112   0.531043        1                 1               1.0
113   0.534403        1                 1               1.0
114   0.535589        2                 2               1.0
115   0.538502        2                 2               1.0
116   0.530048        1                 1               1.0
117   0.534486        1                 1               1.0
118   0.528087        1                 1               1.0
119   0.526906        1                 1               1.0
120   0.525221        1                 0               1.0
121   0.527735        1                 1               1.0
122   0.531583        1                 1               1.0
123   0.530022        1                 1               1.0
124   0.527689        1                 1               1.0
125   0.533179        1                 1               1.0
126   0.537116        2                 2               1.0
127   0.523714        0                 0               1.0
128   0.538614        2                 2               1.0

In [85]:
T01_final_classification_model = finalize_model(T01_model_lightgbm)

In [86]:
T01_prediction = predict_model(T01_final_classification_model, data=T01_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [87]:
T01_y_class = pd.DataFrame(T01_class, columns = ['Y_Class'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_prediction = pd.concat([T01_prediction, T01_y_class], axis = 1)
T01_prediction = T01_prediction.set_index('index')
T01_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [88]:
T01_prediction

Y_Quality  prediction_label  prediction_score
index                                               
28      0.521249                 0            0.9968
33      0.526656                 1            0.9988
39      0.531583                 1            0.9990
40      0.530829                 1            0.9990
41      0.528270                 1            0.9990
...          ...               ...               ...
479     0.534716                 1            0.9979
501     0.533079                 1            0.9990
523     0.534640                 1            0.9979
531     0.560317                 2            0.9968
585     0.515214                 0            0.9968

[129 rows x 3 columns]

# T10

In [132]:
T10_class = T10['Y_Class']
T10_target = T10['Y_Quality']
T10_data = T10.drop(['Y_Class', 'Y_Quality'], axis = 1)
T10_data

X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  X_10  ...  X_928  \
22    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...  326.0   
23    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...    0.0   
25    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...  327.0   
29    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...  327.0   
37    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...  327.0   
..    ...    ...  ...   ...   ...  ...   ...   ...   ...   ...  ...    ...   
589   1.0   94.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...  326.0   
590   1.0   89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...  327.0   
591   1.0   87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...  326.0   
593   2.0   95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...  327.0   
597  21.0   87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0   2.0  ...  326.0   

          X_929  X_930  X_931      X_932  X_933  HOUR  MINUTE  DAY_OF_WEEK  \
22   309.290909  290.0   13.7  13.443333   13.2     8      53            2   
23     0.000000    0.0    0.0   0.000000    0.0     9       1            2   
25   310.854546  298.0   13.7  13.454839   13.2     9      11            7   
29   312.109091  298.0   13.7  13.422581   13.2    23      31            7   
37   312.254546  298.0   13.7  13.456667   13.3     3      47            3   
..          ...    ...    ...        ...    ...   ...     ...          ...   
589  311.272727  298.0   13.7  13.483871   13.3    18       0            2   
590  313.400000  299.0   13.6  13.393548   13.2     1       1            3   
591  313.472727  298.0   13.6  13.400000   13.2     1       9            3   
593  313.363636  298.0   13.6  13.351613   13.2    14      30            4   
597  304.818182  289.0   13.6  13.380000   13.2    14      46            4   

     LINE_AND_CODE  
22            10.0  
23            10.0  
25            10.0  
29            10.0  
37            10.0  
..             ...  
589           11.0  
590           11.0  
591           11.0  
593           11.0  
597           17.0  

[349 rows x 669 columns]

In [90]:
T_10c = T10_data.columns
T_10scaler = MinMaxScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)
T10_data

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
0    0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
1    0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
2    0.009804  0.666667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
3    0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
4    0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
..        ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
344  0.000000  0.466667  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
345  0.000000  0.133333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
346  0.000000  0.000000  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
347  0.009804  0.533333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
348  0.196078  0.000000  0.0  0.0  0.0  0.0  0.941176  0.0  1.0   0.0  ...   

        X_928     X_929     X_930     X_931     X_932     X_933      HOUR  \
0    0.996942  0.984433  0.969900  0.992754  0.991153  0.992481  0.347826   
1    0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.391304   
2    1.000000  0.989410  0.996656  0.992754  0.992001  0.992481  0.391304   
3    1.000000  0.993403  0.996656  0.992754  0.989623  0.992481  1.000000   
4    1.000000  0.993866  0.996656  0.992754  0.992136  1.000000  0.130435   
..        ...       ...       ...       ...       ...       ...       ...   
344  0.996942  0.990741  0.996656  0.992754  0.994141  1.000000  0.782609   
345  1.000000  0.997512  1.000000  0.985507  0.987482  0.992481  0.043478   
346  0.996942  0.997743  0.996656  0.985507  0.987958  0.992481  0.043478   
347  1.000000  0.997396  0.996656  0.985507  0.984390  0.992481  0.608696   
348  0.996942  0.970197  0.966555  0.985507  0.986483  0.992481  0.608696   

       MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0    0.898305     0.166667       0.000000  
1    0.016949     0.166667       0.000000  
2    0.186441     1.000000       0.000000  
3    0.525424     1.000000       0.000000  
4    0.796610     0.333333       0.000000  
..        ...          ...            ...  
344  0.000000     0.166667       0.142857  
345  0.016949     0.333333       0.142857  
346  0.152542     0.333333       0.142857  
347  0.508475     0.500000       0.142857  
348  0.779661     0.500000       1.000000  

[349 rows x 669 columns]

In [91]:
T10_y_class = pd.DataFrame(T10_target, columns = ['Y_Quality'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_data = pd.concat([T10_data, T10_y_class], axis = 1)
T10_data = T10_data.set_index('index')
T10_data.drop(['Y_Quality'], axis = 1, inplace = True)
T10_data

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
index                                                                    ...   
22     0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
23     0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
25     0.009804  0.666667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
29     0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
37     0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
...         ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
589    0.000000  0.466667  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
590    0.000000  0.133333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
591    0.000000  0.000000  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
593    0.009804  0.533333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
597    0.196078  0.000000  0.0  0.0  0.0  0.0  0.941176  0.0  1.0   0.0  ...   

          X_928     X_929     X_930     X_931     X_932     X_933      HOUR  \
index                                                                         
22     0.996942  0.984433  0.969900  0.992754  0.991153  0.992481  0.347826   
23     0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.391304   
25     1.000000  0.989410  0.996656  0.992754  0.992001  0.992481  0.391304   
29     1.000000  0.993403  0.996656  0.992754  0.989623  0.992481  1.000000   
37     1.000000  0.993866  0.996656  0.992754  0.992136  1.000000  0.130435   
...         ...       ...       ...       ...       ...       ...       ...   
589    0.996942  0.990741  0.996656  0.992754  0.994141  1.000000  0.782609   
590    1.000000  0.997512  1.000000  0.985507  0.987482  0.992481  0.043478   
591    0.996942  0.997743  0.996656  0.985507  0.987958  0.992481  0.043478   
593    1.000000  0.997396  0.996656  0.985507  0.984390  0.992481  0.608696   
597    0.996942  0.970197  0.966555  0.985507  0.986483  0.992481  0.608696   

         MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
index                                        
22     0.898305     0.166667       0.000000  
23     0.016949     0.166667       0.000000  
25     0.186441     1.000000       0.000000  
29     0.525424     1.000000       0.000000  
37     0.796610     0.333333       0.000000  
...         ...          ...            ...  
589    0.000000     0.166667       0.142857  
590    0.016949     0.333333       0.142857  
591    0.152542     0.333333       0.142857  
593    0.508475     0.500000       0.142857  
597    0.779661     0.500000       1.000000  

[349 rows x 669 columns]

In [92]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T10_data, target = T10_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [93]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbr = create_model('gbr', fold = 5)
T10_total_models.append(T10_model_gbr)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [94]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbr = tune_model(T10_model_gbr, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [95]:
T10_tuned_models = [T10_model_rf, T10_model_gbr, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]
T10_tuned_models

[RandomForestRegressor(bootstrap=False, ccp_alpha=0.0,
                       criterion='absolute_error', max_depth=2,
                       max_features='log2', max_leaf_nodes=None,
                       max_samples=None, min_impurity_decrease=0,
                       min_samples_leaf=6, min_samples_split=9,
                       min_weight_fraction_leaf=0.0, n_estimators=160, n_jobs=-1,
                       oob_score=False, random_state=414, verbose=0,
                       warm_start=False),
 GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, criterion='friedman_mse',
                           init=None, learning_rate=0.1, loss='squared_error',
                           max_depth=3, max_features=None, max_leaf_nodes=None,
                           min_impurity_decrease=0.0, min_samples_leaf=1,
                           min_samples_split=2, min_weight_fraction_leaf=0.0,
                           n_estimators=100, n_iter_no_change=None,
                           random_s

In [96]:
for model in T10_tuned_models:
    display(predict_model(model))

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
244  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
245  0.009804  0.466667  0.0  0.0  0.0  0.0  0.529412  0.0  1.0   0.0  ...   
246  0.009804  0.933333  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
247  0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
248  0.009804  0.800000  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...   
..        ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
344  0.009804  0.800000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
345  0.009804  0.400000  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
346  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
347  0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
348  0.009804  0.533333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   

        X_930     X_931     X_932     X_933      HOUR    MINUTE  DAY_OF_WEEK  \
244  0.963211  0.985507  0.983915  0.984962  0.782609  0.423729     0.666667   
245  0.996656  0.985507  0.985579  0.992481  0.608696  0.254237     0.166667   
246  0.966555  0.992754  0.995822  1.000000  0.434783  0.881356     0.333333   
247  0.973244  0.992754  0.989623  1.000000  0.086957  0.694915     0.833333   
248  0.996656  0.985507  0.987220  0.992481  0.521739  0.542373     0.666667   
..        ...       ...       ...       ...       ...       ...          ...   
344  1.000000  0.992754  0.992001  0.992481  0.347826  0.915254     0.333333   
345  0.936455  0.992754  0.988449  0.992481  0.869565  0.864407     1.000000   
346  0.966555  0.985507  0.987220  0.992481  0.521739  0.847458     0.833333   
347  0.963211  0.985507  0.984628  0.992481  0.347826  0.457627     1.000000   
348  0.996656  0.985507  0.986293  0.992481  0.913043  0.694915     0.000000   

     LINE_AND_CODE  Y_Quality  prediction_label  
244       0.000000   0.531825          0.530258  
245       0.142857   0.530560          0.530522  
246       0.000000   0.532981          0.530441  
247       0.000000   0.530986          0.530670  
248       0.000000   0.545678          0.530800  
..             ...        ...               ...  
344       0.000000   0.526413          0.530455  
345       0.142857   0.531676          0.530213  
346       0.000000   0.529456          0.530761  
347       0.000000   0.528094          0.530142  
348       0.142857   0.531684          0.530616  

[105 rows x 671 columns]

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
244  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
245  0.009804  0.466667  0.0  0.0  0.0  0.0  0.529412  0.0  1.0   0.0  ...   
246  0.009804  0.933333  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
247  0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
248  0.009804  0.800000  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...   
..        ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
344  0.009804  0.800000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
345  0.009804  0.400000  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
346  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
347  0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
348  0.009804  0.533333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   

        X_930     X_931     X_932     X_933      HOUR    MINUTE  DAY_OF_WEEK  \
244  0.963211  0.985507  0.983915  0.984962  0.782609  0.423729     0.666667   
245  0.996656  0.985507  0.985579  0.992481  0.608696  0.254237     0.166667   
246  0.966555  0.992754  0.995822  1.000000  0.434783  0.881356     0.333333   
247  0.973244  0.992754  0.989623  1.000000  0.086957  0.694915     0.833333   
248  0.996656  0.985507  0.987220  0.992481  0.521739  0.542373     0.666667   
..        ...       ...       ...       ...       ...       ...          ...   
344  1.000000  0.992754  0.992001  0.992481  0.347826  0.915254     0.333333   
345  0.936455  0.992754  0.988449  0.992481  0.869565  0.864407     1.000000   
346  0.966555  0.985507  0.987220  0.992481  0.521739  0.847458     0.833333   
347  0.963211  0.985507  0.984628  0.992481  0.347826  0.457627     1.000000   
348  0.996656  0.985507  0.986293  0.992481  0.913043  0.694915     0.000000   

     LINE_AND_CODE  Y_Quality  prediction_label  
244       0.000000   0.531825          0.529767  
245       0.142857   0.530560          0.533748  
246       0.000000   0.532981          0.529409  
247       0.000000   0.530986          0.529814  
248       0.000000   0.545678          0.543592  
..             ...        ...               ...  
344       0.000000   0.526413          0.530341  
345       0.142857   0.531676          0.529398  
346       0.000000   0.529456          0.530344  
347       0.000000   0.528094          0.529892  
348       0.142857   0.531684          0.530338  

[105 rows x 671 columns]

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
244  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
245  0.009804  0.466667  0.0  0.0  0.0  0.0  0.529412  0.0  1.0   0.0  ...   
246  0.009804  0.933333  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
247  0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
248  0.009804  0.800000  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...   
..        ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
344  0.009804  0.800000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
345  0.009804  0.400000  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
346  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
347  0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
348  0.009804  0.533333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   

        X_930     X_931     X_932     X_933      HOUR    MINUTE  DAY_OF_WEEK  \
244  0.963211  0.985507  0.983915  0.984962  0.782609  0.423729     0.666667   
245  0.996656  0.985507  0.985579  0.992481  0.608696  0.254237     0.166667   
246  0.966555  0.992754  0.995822  1.000000  0.434783  0.881356     0.333333   
247  0.973244  0.992754  0.989623  1.000000  0.086957  0.694915     0.833333   
248  0.996656  0.985507  0.987220  0.992481  0.521739  0.542373     0.666667   
..        ...       ...       ...       ...       ...       ...          ...   
344  1.000000  0.992754  0.992001  0.992481  0.347826  0.915254     0.333333   
345  0.936455  0.992754  0.988449  0.992481  0.869565  0.864407     1.000000   
346  0.966555  0.985507  0.987220  0.992481  0.521739  0.847458     0.833333   
347  0.963211  0.985507  0.984628  0.992481  0.347826  0.457627     1.000000   
348  0.996656  0.985507  0.986293  0.992481  0.913043  0.694915     0.000000   

     LINE_AND_CODE  Y_Quality  prediction_label  
244       0.000000   0.531825          0.531514  
245       0.142857   0.530560          0.531152  
246       0.000000   0.532981          0.529418  
247       0.000000   0.530986          0.530596  
248       0.000000   0.545678          0.545946  
..             ...        ...               ...  
344       0.000000   0.526413          0.529920  
345       0.142857   0.531676          0.529352  
346       0.000000   0.529456          0.530292  
347       0.000000   0.528094          0.529778  
348       0.142857   0.531684          0.529866  

[105 rows x 671 columns]

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
244  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
245  0.009804  0.466667  0.0  0.0  0.0  0.0  0.529412  0.0  1.0   0.0  ...   
246  0.009804  0.933333  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
247  0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
248  0.009804  0.800000  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...   
..        ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
344  0.009804  0.800000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
345  0.009804  0.400000  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
346  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
347  0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
348  0.009804  0.533333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   

        X_930     X_931     X_932     X_933      HOUR    MINUTE  DAY_OF_WEEK  \
244  0.963211  0.985507  0.983915  0.984962  0.782609  0.423729     0.666667   
245  0.996656  0.985507  0.985579  0.992481  0.608696  0.254237     0.166667   
246  0.966555  0.992754  0.995822  1.000000  0.434783  0.881356     0.333333   
247  0.973244  0.992754  0.989623  1.000000  0.086957  0.694915     0.833333   
248  0.996656  0.985507  0.987220  0.992481  0.521739  0.542373     0.666667   
..        ...       ...       ...       ...       ...       ...          ...   
344  1.000000  0.992754  0.992001  0.992481  0.347826  0.915254     0.333333   
345  0.936455  0.992754  0.988449  0.992481  0.869565  0.864407     1.000000   
346  0.966555  0.985507  0.987220  0.992481  0.521739  0.847458     0.833333   
347  0.963211  0.985507  0.984628  0.992481  0.347826  0.457627     1.000000   
348  0.996656  0.985507  0.986293  0.992481  0.913043  0.694915     0.000000   

     LINE_AND_CODE  Y_Quality  prediction_label  
244       0.000000   0.531825          0.530498  
245       0.142857   0.530560          0.530523  
246       0.000000   0.532981          0.530197  
247       0.000000   0.530986          0.530731  
248       0.000000   0.545678          0.540110  
..             ...        ...               ...  
344       0.000000   0.526413          0.530259  
345       0.142857   0.531676          0.530296  
346       0.000000   0.529456          0.530668  
347       0.000000   0.528094          0.530597  
348       0.142857   0.531684          0.530543  

[105 rows x 671 columns]

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
244  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
245  0.009804  0.466667  0.0  0.0  0.0  0.0  0.529412  0.0  1.0   0.0  ...   
246  0.009804  0.933333  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
247  0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
248  0.009804  0.800000  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...   
..        ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
344  0.009804  0.800000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
345  0.009804  0.400000  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
346  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
347  0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
348  0.009804  0.533333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   

        X_930     X_931     X_932     X_933      HOUR    MINUTE  DAY_OF_WEEK  \
244  0.963211  0.985507  0.983915  0.984962  0.782609  0.423729     0.666667   
245  0.996656  0.985507  0.985579  0.992481  0.608696  0.254237     0.166667   
246  0.966555  0.992754  0.995822  1.000000  0.434783  0.881356     0.333333   
247  0.973244  0.992754  0.989623  1.000000  0.086957  0.694915     0.833333   
248  0.996656  0.985507  0.987220  0.992481  0.521739  0.542373     0.666667   
..        ...       ...       ...       ...       ...       ...          ...   
344  1.000000  0.992754  0.992001  0.992481  0.347826  0.915254     0.333333   
345  0.936455  0.992754  0.988449  0.992481  0.869565  0.864407     1.000000   
346  0.966555  0.985507  0.987220  0.992481  0.521739  0.847458     0.833333   
347  0.963211  0.985507  0.984628  0.992481  0.347826  0.457627     1.000000   
348  0.996656  0.985507  0.986293  0.992481  0.913043  0.694915     0.000000   

     LINE_AND_CODE  Y_Quality  prediction_label  
244       0.000000   0.531825          0.529079  
245       0.142857   0.530560          0.532218  
246       0.000000   0.532981          0.529757  
247       0.000000   0.530986          0.530806  
248       0.000000   0.545678          0.545331  
..             ...        ...               ...  
344       0.000000   0.526413          0.528454  
345       0.142857   0.531676          0.528886  
346       0.000000   0.529456          0.529722  
347       0.000000   0.528094          0.532293  
348       0.142857   0.531684          0.529329  

[105 rows x 671 columns]

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
244  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
245  0.009804  0.466667  0.0  0.0  0.0  0.0  0.529412  0.0  1.0   0.0  ...   
246  0.009804  0.933333  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
247  0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
248  0.009804  0.800000  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...   
..        ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
344  0.009804  0.800000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
345  0.009804  0.400000  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
346  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
347  0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
348  0.009804  0.533333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   

        X_930     X_931     X_932     X_933      HOUR    MINUTE  DAY_OF_WEEK  \
244  0.963211  0.985507  0.983915  0.984962  0.782609  0.423729     0.666667   
245  0.996656  0.985507  0.985579  0.992481  0.608696  0.254237     0.166667   
246  0.966555  0.992754  0.995822  1.000000  0.434783  0.881356     0.333333   
247  0.973244  0.992754  0.989623  1.000000  0.086957  0.694915     0.833333   
248  0.996656  0.985507  0.987220  0.992481  0.521739  0.542373     0.666667   
..        ...       ...       ...       ...       ...       ...          ...   
344  1.000000  0.992754  0.992001  0.992481  0.347826  0.915254     0.333333   
345  0.936455  0.992754  0.988449  0.992481  0.869565  0.864407     1.000000   
346  0.966555  0.985507  0.987220  0.992481  0.521739  0.847458     0.833333   
347  0.963211  0.985507  0.984628  0.992481  0.347826  0.457627     1.000000   
348  0.996656  0.985507  0.986293  0.992481  0.913043  0.694915     0.000000   

     LINE_AND_CODE  Y_Quality  prediction_label  
244       0.000000   0.531825          0.530448  
245       0.142857   0.530560          0.530547  
246       0.000000   0.532981          0.530474  
247       0.000000   0.530986          0.530506  
248       0.000000   0.545678          0.547267  
..             ...        ...               ...  
344       0.000000   0.526413          0.530511  
345       0.142857   0.531676          0.530520  
346       0.000000   0.529456          0.530518  
347       0.000000   0.528094          0.530528  
348       0.142857   0.531684          0.530470  

[105 rows x 671 columns]

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
244  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
245  0.009804  0.466667  0.0  0.0  0.0  0.0  0.529412  0.0  1.0   0.0  ...   
246  0.009804  0.933333  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
247  0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
248  0.009804  0.800000  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...   
..        ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
344  0.009804  0.800000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
345  0.009804  0.400000  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
346  0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
347  0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
348  0.009804  0.533333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   

        X_930     X_931     X_932     X_933      HOUR    MINUTE  DAY_OF_WEEK  \
244  0.963211  0.985507  0.983915  0.984962  0.782609  0.423729     0.666667   
245  0.996656  0.985507  0.985579  0.992481  0.608696  0.254237     0.166667   
246  0.966555  0.992754  0.995822  1.000000  0.434783  0.881356     0.333333   
247  0.973244  0.992754  0.989623  1.000000  0.086957  0.694915     0.833333   
248  0.996656  0.985507  0.987220  0.992481  0.521739  0.542373     0.666667   
..        ...       ...       ...       ...       ...       ...          ...   
344  1.000000  0.992754  0.992001  0.992481  0.347826  0.915254     0.333333   
345  0.936455  0.992754  0.988449  0.992481  0.869565  0.864407     1.000000   
346  0.966555  0.985507  0.987220  0.992481  0.521739  0.847458     0.833333   
347  0.963211  0.985507  0.984628  0.992481  0.347826  0.457627     1.000000   
348  0.996656  0.985507  0.986293  0.992481  0.913043  0.694915     0.000000   

     LINE_AND_CODE  Y_Quality  prediction_label  
244       0.000000   0.531825          0.530411  
245       0.142857   0.530560          0.530411  
246       0.000000   0.532981          0.530411  
247       0.000000   0.530986          0.530411  
248       0.000000   0.545678          0.530411  
..             ...        ...               ...  
344       0.000000   0.526413          0.530411  
345       0.142857   0.531676          0.530411  
346       0.000000   0.529456          0.530411  
347       0.000000   0.528094          0.530411  
348       0.142857   0.531684          0.530411  

[105 rows x 671 columns]

In [97]:
T10_final_regression_model = finalize_model(T10_model_et)

In [98]:
T10_prediction = predict_model(T10_final_regression_model, data=T10_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [99]:
T10_datas = T10_prediction['prediction_label']

In [100]:
T10_datas = T10_prediction['prediction_label']
T10_datas = pd.DataFrame(T10_datas.values, columns = ['Y_Quality'])
T10_datas

Y_Quality
0     0.517719
1     0.519090
2     0.529362
3     0.532405
4     0.533110
..         ...
344   0.529510
345   0.529948
346   0.529308
347   0.526546
348   0.533702

[349 rows x 1 columns]

In [101]:
T10y_idx= T10_class.index
T10y_idx = pd.DataFrame(T10y_idx, columns = ['index'])
T10_datas = pd.concat([T10y_idx, T10_datas], axis = 1)
T10_datas = T10_datas.set_index('index')
T10_datas

Y_Quality
index           
22      0.517719
23      0.519090
25      0.529362
29      0.532405
37      0.533110
...          ...
589     0.529510
590     0.529948
591     0.529308
593     0.526546
597     0.533702

[349 rows x 1 columns]

In [102]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T10_datas, 
                   target=T10_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [103]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbc = create_model('gbc', fold = 5)
T10_total_models.append(T10_model_gbc)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [104]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbc = tune_model(T10_model_gbc, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [105]:
T10_tuned_models = [T10_model_rf, T10_model_gbc, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]
T10_tuned_models

[RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                        criterion='gini', max_depth=None, max_features='auto',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.0, min_samples_leaf=1,
                        min_samples_split=2, min_weight_fraction_leaf=0.0,
                        n_estimators=100, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                            learning_rate=0.1, loss='deviance', max_depth=3,
                            max_features=None, max_leaf_nodes=None,
                            min_impurity_decrease=0.0, min_samples_leaf=1,
                            min_samples_split=2, min_weight_fraction_leaf=0.0,
                            n_estimators=100, n_iter_no_change=None,
                            random_state=414, su

In [106]:
for model in T10_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1               1.0
245   0.526546        1                 1               1.0
246   0.529225        1                 1               1.0
247   0.532268        1                 1               1.0
248   0.519090        0                 0               1.0
..         ...      ...               ...               ...
344   0.534122        1                 1               1.0
345   0.529948        1                 1               1.0
346   0.524862        0                 0               1.0
347   0.529017        1                 1               1.0
348   0.533338        1                 1               1.0

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1               1.0
245   0.526546        1                 1               1.0
246   0.529225        1                 1               1.0
247   0.532268        1                 1               1.0
248   0.519090        0                 0               1.0
..         ...      ...               ...               ...
344   0.534122        1                 1               1.0
345   0.529948        1                 1               1.0
346   0.524862        0                 0               1.0
347   0.529017        1                 1               1.0
348   0.533338        1                 1               1.0

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1               1.0
245   0.526546        1                 1               1.0
246   0.529225        1                 1               1.0
247   0.532268        1                 1               1.0
248   0.519090        0                 0               1.0
..         ...      ...               ...               ...
344   0.534122        1                 1               1.0
345   0.529948        1                 1               1.0
346   0.524862        0                 0               1.0
347   0.529017        1                 1               1.0
348   0.533338        1                 1               1.0

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1            0.9999
245   0.526546        1                 1            0.9998
246   0.529225        1                 1            0.9999
247   0.532268        1                 1            0.9999
248   0.519090        0                 0            0.9986
..         ...      ...               ...               ...
344   0.534122        1                 1            0.9996
345   0.529948        1                 1            0.9999
346   0.524862        0                 0            0.9931
347   0.529017        1                 1            0.9999
348   0.533338        1                 1            0.9999

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1            0.9990
245   0.526546        1                 1            0.9926
246   0.529225        1                 1            0.9991
247   0.532268        1                 1            0.9991
248   0.519090        0                 0            0.9813
..         ...      ...               ...               ...
344   0.534122        1                 1            0.9904
345   0.529948        1                 1            0.9991
346   0.524862        0                 0            0.9813
347   0.529017        1                 1            0.9991
348   0.533338        1                 1            0.9940

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1               1.0
245   0.526546        1                 1               1.0
246   0.529225        1                 1               1.0
247   0.532268        1                 1               1.0
248   0.519090        0                 0               1.0
..         ...      ...               ...               ...
344   0.534122        1                 1               1.0
345   0.529948        1                 1               1.0
346   0.524862        0                 0               1.0
347   0.529017        1                 1               1.0
348   0.533338        1                 1               1.0

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1            0.9997
245   0.526546        1                 1            0.9996
246   0.529225        1                 1            0.9997
247   0.532268        1                 1            0.9997
248   0.519090        0                 0            0.9997
..         ...      ...               ...               ...
344   0.534122        1                 1            0.9996
345   0.529948        1                 1            0.9997
346   0.524862        0                 0            0.6548
347   0.529017        1                 1            0.9997
348   0.533338        1                 1            0.9997

[105 rows x 4 columns]

In [107]:
T10_final_classification_model = finalize_model(T10_model_xgb)

In [108]:
T10_prediction = predict_model(T10_final_classification_model, data=T10_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [109]:
T10_y_class = pd.DataFrame(T10_class, columns = ['Y_Class'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_prediction = pd.concat([T10_prediction, T10_y_class], axis = 1)
T10_prediction = T10_prediction.set_index('index')
T10_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [110]:
T10_prediction

Y_Quality  prediction_label  prediction_score
index                                               
22      0.517719                 0            0.9866
23      0.519090                 0            0.9866
25      0.529362                 1            0.9994
29      0.532405                 1            0.9994
37      0.533110                 1            0.9975
...          ...               ...               ...
589     0.529510                 1            0.9994
590     0.529948                 1            0.9994
591     0.529308                 1            0.9994
593     0.526546                 1            0.9946
597     0.533702                 1            0.9956

[349 rows x 3 columns]

# Test

In [165]:
test_data = pd.read_csv("./test.csv")
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  X_2872  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...     ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2873  X_2874  X_2875  
0       NaN     NaN     NaN  
1       NaN     NaN     NaN  
2       NaN     NaN     NaN  
3       NaN     NaN     NaN  
4       NaN     NaN     NaN  
..      ...     ...     ...  
305     NaN     NaN     NaN  
306     NaN     NaN     NaN  
307     NaN     NaN     NaN  
308     NaN     NaN     NaN  
309     NaN     NaN     NaN  

[310 rows x 2879 columns]

In [166]:
test_data['YEAR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.year
test_data['MONTH'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.month
test_data['DAY'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day
test_data['HOUR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.hour
test_data['MINUTE'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.minute
test_data['DAY_OF_WEEK'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day_name()

In [167]:
test_data = test_data.drop(['MONTH', 'DAY', 'YEAR'], axis = 1)

In [168]:
test_data.drop(colls, inplace = True, axis = 1)

In [169]:
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T010305'),'LINE_AND_CODE'] = 0
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T010306'),'LINE_AND_CODE'] = 1
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T050304'),'LINE_AND_CODE'] = 2
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T050307'),'LINE_AND_CODE'] = 3
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T100304'),'LINE_AND_CODE'] = 4
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T100306'),'LINE_AND_CODE'] = 5

test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T010305'),'LINE_AND_CODE'] = 6
test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T010306'),'LINE_AND_CODE'] = 7
test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T050304'),'LINE_AND_CODE'] = 8
test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T050307'),'LINE_AND_CODE'] = 9
test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T100304'),'LINE_AND_CODE'] = 10
test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T100306'),'LINE_AND_CODE'] = 11

test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T010305'),'LINE_AND_CODE'] = 12
test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T010306'),'LINE_AND_CODE'] = 13
test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T050304'),'LINE_AND_CODE'] = 14
test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T050307'),'LINE_AND_CODE'] = 15
test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T100304'),'LINE_AND_CODE'] = 16
test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T100306'),'LINE_AND_CODE'] = 17
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     2   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     2   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     8   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN    10   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN    11   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...   ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN    11   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN    16   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN    16   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN    20   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN    21   

     MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0         1       Friday           11.0  
1         9       Friday           10.0  
2        42       Friday           10.0  
3        56       Friday            0.0  
4         4       Friday            1.0  
..      ...          ...            ...  
305      18     Saturday           11.0  
306      39     Saturday           10.0  
307      47     Saturday           11.0  
308      53     Saturday           11.0  
309       1     Saturday           11.0  

[310 rows x 2801 columns]

In [170]:
test_data.loc[test_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
test_data.loc[test_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
test_data.loc[test_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
test_data.loc[test_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
test_data.loc[test_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
test_data.loc[test_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
test_data.loc[test_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

test_data.loc[test_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
test_data.loc[test_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
test_data.loc[test_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8  ...  \
0    T100306            2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
1    T100304            2  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
2    T100304            2  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
3    T010305            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
4    T010306            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
..       ...          ...  ...   ...  ...   ...   ...  ...   ...   ...  ...   
305  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
306  T100304            2  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
307  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  ...   
308  T100306            2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
309  T100306            2  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   

     X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  MINUTE  \
0       NaN     NaN     NaN     NaN     NaN     NaN     2       1   
1       NaN     NaN     NaN     NaN     NaN     NaN     2       9   
2       NaN     NaN     NaN     NaN     NaN     NaN     8      42   
3       NaN     NaN     NaN     NaN     NaN     NaN    10      56   
4       NaN     NaN     NaN     NaN     NaN     NaN    11       4   
..      ...     ...     ...     ...     ...     ...   ...     ...   
305     NaN     NaN     NaN     NaN     NaN     NaN    11      18   
306     NaN     NaN     NaN     NaN     NaN     NaN    16      39   
307     NaN     NaN     NaN     NaN     NaN     NaN    16      47   
308     NaN     NaN     NaN     NaN     NaN     NaN    20      53   
309     NaN     NaN     NaN     NaN     NaN     NaN    21       1   

     DAY_OF_WEEK  LINE_AND_CODE  
0              5           11.0  
1              5           10.0  
2              5           10.0  
3              5            0.0  
4              5            1.0  
..           ...            ...  
305            6           11.0  
306            6           10.0  
307            6           11.0  
308            6           11.0  
309            6           11.0  

[310 rows x 2799 columns]

In [171]:
TT050304 = test_data[test_data['LINE'] == 'T050304']
TT050307 = test_data[test_data['LINE'] == 'T050307']
TT010305 = test_data[test_data['LINE'] == 'T010305']
TT010306 = test_data[test_data['LINE'] == 'T010306']
TT100304 = test_data[test_data['LINE'] == 'T100304']
TT100306 = test_data[test_data['LINE'] == 'T100306']
TT050304

LINE PRODUCT_CODE  X_1  X_2  X_3  X_4  X_5  X_6  X_7  X_8  ...  X_2866  \
7   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   57.74   
8   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   53.18   
14  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   49.77   
35  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   55.22   
41  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   49.67   
42  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   51.30   
52  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   54.06   
53  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   54.04   
54  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   55.72   
61  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...     NaN   
64  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...     NaN   
65  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   51.55   
66  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   51.37   

    X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  MINUTE  DAY_OF_WEEK  \
7    52.51   54.45   57.99   63.16     1.0    12      27            6   
8    56.02   41.79   47.94   60.72     1.0    12      35            6   
14   54.93   49.85   48.62   63.18     1.0     6      10            6   
35   58.14   48.93   56.16   64.25     1.0     3      58            7   
41   45.00   49.81   55.19   67.17     1.0    23       2            1   
42   47.66   60.00   53.75   62.58     1.0    23      10            1   
52   51.18   52.17   57.75   63.94     1.0    17      47            3   
53   51.25   54.98   57.22   63.33     1.0    17      55            3   
54   57.57   42.08   55.19   66.06     1.0    18       3            3   
61     NaN     NaN     NaN     NaN     1.0    21      24            7   
64     NaN     NaN     NaN     NaN     1.0     0      35            1   
65   55.55   39.85   47.82   61.59     1.0     3      24            1   
66   55.70   52.49   48.34   62.12     1.0     8      26            1   

    LINE_AND_CODE  
7             2.0  
8             2.0  
14            2.0  
35            2.0  
41            2.0  
42            2.0  
52            2.0  
53            2.0  
54            2.0  
61            2.0  
64            2.0  
65            2.0  
66            2.0  

[13 rows x 2799 columns]

In [172]:
TT050304.drop(['LINE'], axis = 1, inplace = True)
TT050307.drop(['LINE'], axis = 1, inplace = True)
TT010305.drop(['LINE'], axis = 1, inplace = True)
TT010306.drop(['LINE'], axis = 1, inplace = True)
TT100304.drop(['LINE'], axis = 1, inplace = True)
TT100306.drop(['LINE'], axis = 1, inplace = True)

In [173]:
TT050304.drop(T050304_col, inplace = True, axis = 1)
TT050307.drop(T050307_col, inplace = True, axis = 1)
TT010305.drop(T010305_col, inplace = True, axis = 1)
TT010306.drop(T010306_col, inplace = True, axis = 1)
TT100304.drop(T100304_col, inplace = True, axis = 1)
TT100306.drop(T100306_col, inplace = True, axis = 1)
TT050304

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
7             1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0   
8             1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0   
14            1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   
35            1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0   
41            1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0   
42            1  10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0   
52            1  12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0   
53            1  12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0   
54            1  12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0   
61            1  17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0   
64            1  18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0   
65            1  18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0   
66            1  18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0   

    X_138  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  MINUTE  \
7   354.0  ...   57.74   52.51   54.45   57.99   63.16     1.0    12      27   
8   355.0  ...   53.18   56.02   41.79   47.94   60.72     1.0    12      35   
14   60.0  ...   49.77   54.93   49.85   48.62   63.18     1.0     6      10   
35  249.0  ...   55.22   58.14   48.93   56.16   64.25     1.0     3      58   
41  293.0  ...   49.67   45.00   49.81   55.19   67.17     1.0    23       2   
42  293.0  ...   51.30   47.66   60.00   53.75   62.58     1.0    23      10   
52  330.0  ...   54.06   51.18   52.17   57.75   63.94     1.0    17      47   
53  330.0  ...   54.04   51.25   54.98   57.22   63.33     1.0    17      55   
54  330.0  ...   55.72   57.57   42.08   55.19   66.06     1.0    18       3   
61  436.0  ...     NaN     NaN     NaN     NaN     NaN     1.0    21      24   
64  437.0  ...     NaN     NaN     NaN     NaN     NaN     1.0     0      35   
65  441.0  ...   51.55   55.55   39.85   47.82   61.59     1.0     3      24   
66  446.0  ...   51.37   55.70   52.49   48.34   62.12     1.0     8      26   

    DAY_OF_WEEK  LINE_AND_CODE  
7             6            2.0  
8             6            2.0  
14            6            2.0  
35            7            2.0  
41            1            2.0  
42            1            2.0  
52            3            2.0  
53            3            2.0  
54            3            2.0  
61            7            2.0  
64            1            2.0  
65            1            2.0  
66            1            2.0  

[13 rows x 1973 columns]

In [174]:
TT05 = pd.concat([TT050304, TT050307])
TT01 = pd.concat([TT010305, TT010306])
TT10 = pd.concat([TT100304, TT100306])

In [175]:
TT05.drop(T5drop, inplace = True, axis = 1)
TT01.drop(T0drop, inplace = True, axis = 1)
TT10.drop(T1drop, inplace = True, axis = 1)

In [176]:
TT05 = TT05.fillna(0)
TT01 = TT01.fillna(0)
TT10 = TT10.fillna(0)

In [177]:
TT05

PRODUCT_CODE  X_132  X_133  X_134  X_135  X_136  X_137  X_138  X_139  \
7               1   0.19   0.20   0.19    0.2  354.0  354.0  354.0  591.5   
8               1   0.19   0.20   0.19    0.2  355.0  354.0  355.0  591.5   
14              1   0.19   0.21   0.19    0.2   60.0   60.0   60.0  558.4   
35              1   0.20   0.21   0.20    0.2  249.0  249.0  249.0  583.1   
41              1   0.20   0.21   0.20    0.2  293.0  293.0  293.0  580.9   
42              1   0.20   0.21   0.19    0.2  293.0  293.0  293.0  581.0   
52              1   0.19   0.21   0.19    0.2  330.0  330.0  330.0  582.9   
53              1   0.20   0.21   0.20    0.2  330.0  330.0  330.0  583.4   
54              1   0.19   0.21   0.19    0.2  330.0  330.0  330.0  583.0   
61              1   0.20   0.21   0.20    0.2  436.0  436.0  436.0  592.1   
64              1   0.20   0.21   0.20    0.2  437.0  437.0  437.0  593.7   
65              1   0.20   0.21   0.20    0.2  441.0  441.0  441.0  593.8   
66              1   0.20   0.21   0.20    0.2  446.0  446.0  446.0  593.2   
13              1   0.21   0.22   0.21    0.2  230.0  230.0  231.0  580.6   
36              1   0.21   0.22   0.21    0.2   99.0   99.0   99.0  581.5   
62              1   0.21   0.22   0.21    0.2   50.0   49.0   40.0  578.6   
63              1   0.21   0.22   0.21    0.2   52.0   51.0   41.0  580.5   
130             1   0.21   0.22   0.20    0.2  424.0  423.0  413.0  585.7   
131             1   0.21   0.21   0.21    0.2  424.0  423.0  414.0  584.4   
132             1   0.21   0.22   0.21    0.2  426.0  425.0  416.0  584.2   
248             1   0.21   0.22   0.21    0.2  732.0  731.0  722.0  595.5   
249             1   0.21   0.22   0.21    0.2  732.0  731.0  722.0  594.8   
250             1   0.21   0.22   0.21    0.2  733.0  732.0  722.0  594.0   
251             1   0.21   0.22   0.21    0.2  733.0  732.0  722.0  594.1   
252             1   0.21   0.22   0.21    0.2  733.0  732.0  722.0  593.9   
253             1   0.21   0.22   0.21    0.2  733.0  732.0  723.0  594.0   
254             1   0.21   0.22   0.21    0.2  737.0  736.0  727.0  594.4   
255             1   0.21   0.22   0.21    0.2  738.0  737.0  727.0  594.6   
260             1   0.21   0.22   0.20    0.2  738.0  737.0  728.0  595.7   
263             1   0.20   0.22   0.20    0.2  741.0  740.0  730.0  597.0   
280             1   0.21   0.22   0.21    0.2  789.0  788.0  779.0  602.1   
281             1   0.21   0.22   0.21    0.2  790.0  789.0  779.0  600.7   
282             1   0.21   0.22   0.21    0.2  800.0  799.0  789.0  599.7   
283             1   0.21   0.22   0.21    0.2  800.0  799.0  790.0  599.4   
284             1   0.21   0.22   0.21    0.2  806.0  805.0  796.0  599.4   
285             1   0.21   0.22   0.21    0.2  806.0  805.0  796.0  599.6   
286             1   0.21   0.22   0.21    0.2  807.0  806.0  796.0  599.6   
292             1   0.21   0.22   0.21    0.2  821.0  820.0  810.0  601.5   
293             1   0.21   0.22   0.21    0.2  821.0  820.0  811.0  601.4   

     X_140  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  MINUTE  \
7    597.7  ...   57.74   52.51   54.45   57.99   63.16     1.0    12      27   
8    597.7  ...   53.18   56.02   41.79   47.94   60.72     1.0    12      35   
14   561.9  ...   49.77   54.93   49.85   48.62   63.18     1.0     6      10   
35   587.1  ...   55.22   58.14   48.93   56.16   64.25     1.0     3      58   
41   585.1  ...   49.67   45.00   49.81   55.19   67.17     1.0    23       2   
42   585.2  ...   51.30   47.66   60.00   53.75   62.58     1.0    23      10   
52   587.9  ...   54.06   51.18   52.17   57.75   63.94     1.0    17      47   
53   588.0  ...   54.04   51.25   54.98   57.22   63.33     1.0    17      55   
54   587.8  ...   55.72   57.57   42.08   55.19   66.06     1.0    18       3   
61   597.9  ...    0.00    0.00    0.00    0.00    0.00     1.0    21      24   
64   599.4  ...    0.00    0.00  

# Test T05

In [178]:
TT05_idx = TT05['PRODUCT_CODE'].index
TT05_idx = pd.DataFrame(TT05_idx, columns = ['index'])
TT05_idx

index
0       7
1       8
2      14
3      35
4      41
5      42
6      52
7      53
8      54
9      61
10     64
11     65
12     66
13     13
14     36
15     62
16     63
17    130
18    131
19    132
20    248
21    249
22    250
23    251
24    252
25    253
26    254
27    255
28    260
29    263
30    280
31    281
32    282
33    283
34    284
35    285
36    286
37    292
38    293

In [179]:
TT05.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [180]:
T_05c = T05_data.columns
T_05scaler = MinMaxScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)
T05_data

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
0      0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.554348   
1      0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.570652   
2      0.5    0.0    0.0    0.0  0.232779  0.232779  0.228944  0.559783   
3      0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.563406   
4      0.5    0.0    0.5    0.0  0.232779  0.232779  0.228944  0.561594   
..     ...    ...    ...    ...       ...       ...       ...       ...   
115    0.5    0.0    0.5    0.0  0.058195  0.058195  0.058126  0.217391   
116    0.5    0.0    0.5    0.0  0.059382  0.059382  0.059312  0.217391   
117    0.5    0.0    0.5    0.0  0.061758  0.061758  0.061684  0.219203   
118    0.5    0.0    0.5    0.0  0.061758  0.061758  0.061684  0.222826   
119    0.5    0.0    0.5    0.0  0.065321  0.065321  0.065243  0.206522   

        X_140     X_141  ...    X_2866    X_2867    X_2868    X_2869  \
0    0.520906  0.639640  ...  0.653054  0.595543  0.538984  0.568830   
1    0.529617  0.711712  ...  0.650564  0.533790  0.703029  0.609544   
2    0.524390  0.621622  ...  0.642430  0.610108  0.776858  0.552144   
3    0.524390  0.338481  ...  0.539509  0.603262  0.634994  0.514434   
4    0.522648  0.698842  ...  0.701361  0.628750  0.920377  0.554981   
..        ...       ...  ...       ...       ...       ...       ...   
115  0.202091  0.411840  ...  0.879316  0.819400  0.879656  0.939429   
116  0.198606  0.404118  ...  0.873340  0.773376  0.948518  0.944268   
117  0.200348  0.462033  ...  0.867862  0.819109  0.901672  0.843651   
118  0.203833  0.406692  ...  0.890438  0.857850  0.825195  0.962122   
119  0.203833  0.321750  ...  0.000000  0.000000  0.000000  0.000000   

       X_2870  X_2871      HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0    0.975172     0.0  0.217391  0.237288     0.000000            0.0  
1    0.982445     0.0  0.217391  0.508475     0.000000            0.0  
2    0.965141     0.0  0.217391  0.796610     0.000000            0.0  
3    0.964639     0.0  0.260870  0.050847     0.000000            0.0  
4    0.984326     0.0  0.260870  0.322034     0.000000            0.0  
..        ...     ...       ...       ...          ...            ...  
115  0.827962     1.0  0.347826  0.305085     0.666667            1.0  
116  0.837994     1.0  0.347826  0.440678     0.666667            1.0  
117  0.784075     1.0  0.391304  0.644068     0.666667            1.0  
118  0.791724     1.0  0.608696  1.000000     0.666667            1.0  
119  0.000000     1.0  0.521739  0.627119     0.666667            1.0  

[120 rows x 1960 columns]

In [181]:
TT05c = TT05.columns
TT05scaled = T_05scaler.transform(TT05)
TT05scaled
TT05 = pd.DataFrame(TT05scaled, columns = TT05c)
TT05

X_132  X_133  X_134  X_135  X_136  X_137  X_138  X_139  X_140  X_141  ...  \
0    0.19   0.20   0.19    0.2  354.0  354.0  354.0  591.5  597.7  575.6  ...   
1    0.19   0.20   0.19    0.2  355.0  354.0  355.0  591.5  597.7  575.7  ...   
2    0.19   0.21   0.19    0.2   60.0   60.0   60.0  558.4  561.9  547.5  ...   
3    0.20   0.21   0.20    0.2  249.0  249.0  249.0  583.1  587.1  569.9  ...   
4    0.20   0.21   0.20    0.2  293.0  293.0  293.0  580.9  585.1  570.4  ...   
5    0.20   0.21   0.19    0.2  293.0  293.0  293.0  581.0  585.2  568.9  ...   
6    0.19   0.21   0.19    0.2  330.0  330.0  330.0  582.9  587.9  542.4  ...   
7    0.20   0.21   0.20    0.2  330.0  330.0  330.0  583.4  588.0  563.9  ...   
8    0.19   0.21   0.19    0.2  330.0  330.0  330.0  583.0  587.8  570.4  ...   
9    0.20   0.21   0.20    0.2  436.0  436.0  436.0  592.1  597.9  580.8  ...   
10   0.20   0.21   0.20    0.2  437.0  437.0  437.0  593.7  599.4  580.1  ...   
11   0.20   0.21   0.20    0.2  441.0  441.0  441.0  593.8  599.7  574.6  ...   
12   0.20   0.21   0.20    0.2  446.0  446.0  446.0  593.2  599.0  583.9  ...   
13   0.21   0.22   0.21    0.2  230.0  230.0  231.0  580.6  584.1  562.0  ...   
14   0.21   0.22   0.21    0.2   99.0   99.0   99.0  581.5  585.0  569.8  ...   
15   0.21   0.22   0.21    0.2   50.0   49.0   40.0  578.6  582.2  564.3  ...   
16   0.21   0.22   0.21    0.2   52.0   51.0   41.0  580.5  584.0  569.5  ...   
17   0.21   0.22   0.20    0.2  424.0  423.0  413.0  585.7  591.2  573.0  ...   
18   0.21   0.21   0.21    0.2  424.0  423.0  414.0  584.4  590.1  565.8  ...   
19   0.21   0.22   0.21    0.2  426.0  425.0  416.0  584.2  589.5  569.1  ...   
20   0.21   0.22   0.21    0.2  732.0  731.0  722.0  595.5  602.0  577.2  ...   
21   0.21   0.22   0.21    0.2  732.0  731.0  722.0  594.8  601.4  573.3  ...   
22   0.21   0.22   0.21    0.2  733.0  732.0  722.0  594.0  600.8  556.5  ...   
23   0.21   0.22   0.21    0.2  733.0  732.0  722.0  594.1  600.8  578.3  ...   
24   0.21   0.22   0.21    0.2  733.0  732.0  722.0  593.9  600.7  573.7  ...   
25   0.21   0.22   0.21    0.2  733.0  732.0  723.0  594.0  600.8  575.2  ...   
26   0.21   0.22   0.21    0.2  737.0  736.0  727.0  594.4  601.4  567.4  ...   
27   0.21   0.22   0.21    0.2  738.0  737.0  727.0  594.6  601.4  574.3  ...   
28   0.21   0.22   0.20    0.2  738.0  737.0  728.0  595.7  602.5  559.8  ...   
29   0.20   0.22   0.20    0.2  741.0  740.0  730.0  597.0  604.0  583.3  ...   
30   0.21   0.22   0.21    0.2  789.0  788.0  779.0  602.1  608.5  580.6  ...   
31   0.21   0.22   0.21    0.2  790.0  789.0  779.0  600.7  607.3  578.2  ...   
32   0.21   0.22   0.21    0.2  800.0  799.0  789.0  599.7  606.3  582.0  ...   
33   0.21   0.22   0.21    0.2  800.0  799.0  790.0  599.4  606.2  576.2  ...   
34   0.21   0.22   0.21    0.2  806.0  805.0  796.0  599.4  606.4  582.6  ...   
35   0.21   0.22   0.21    0.2  806.0  805.0  796.0  599.6  606.4  582.3  ...   
36   0.21   0.22   0.21    0.2  807.0  806.0  796.0  599.6  606.4  575.5  ...   
37   0.21   0.22   0.21    0.2  821.0  820.0  810.0  601.5  608.1  587.5  ...   
38   0.21   0.22   0.21    0.2  821.0  820.0  811.0  601.4  608.1  584.8  ...   

    X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  MINUTE  DAY_OF_WEEK  \
0    57.74   52.51   54.45   57.99   63.16     1.0  12.0    27.0          6.0   
1    53.18   56.02   41.79   47.94   60.72     1.0  12.0    35.0          6.0   
2    49.77   54.93   49.85   48.62   63.18     1.0   6.0    10.0          6.0   
3    55.22   58.14   48.93   56.16   64.25     1.0   3.0    58.0          7.0   
4    49.67   45.00   49.81   55.19   67.17     1.0  23.0     2.0          1.0   
5    51.30   47.66   60.00   53.75   62.58     1.0  23.0    10.0          1.0   
6    54.06   51.18   52.17   57.75   63.94     1.0  17.0    47.0          3.0   
7    54.04   51.25   54.98   57.22   63.33     1.0  17.0    55.0          3.0   
8    55.72   57.57   42.08   55.19

In [182]:
TT05 = pd.concat([TT05_idx, TT05], axis = 1)
TT05 = TT05.set_index('index')

# Test T01

In [183]:
TT01_idx = TT01['PRODUCT_CODE'].index
TT01_idx = pd.DataFrame(TT01_idx, columns = ['index'])
TT01_idx

index
0       3
1       6
2      10
3      11
4      38
5      40
6      71
7      86
8      88
9      89
10    116
11    117
12    141
13    142
14      4
15      5
16      9
17     12
18     37
19     39
20     72
21     79
22     87
23    109
24    114
25    115
26    128
27    129

In [184]:
TT01.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [185]:
T_01c = T01_data.columns
T_01scaler = MinMaxScaler()
T_01scaled = T_01scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)
T01_data

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
0      0.0  0.222222  0.000000    0.0    0.0  0.535714    0.0    0.0    0.0   
1      0.0  0.888889  0.000000    0.0    0.0  0.583333    0.0    0.0    0.0   
2      0.0  0.888889  0.000000    0.0    0.0  0.607143    0.0    1.0    0.0   
3      0.0  0.888889  0.000000    0.0    0.0  0.625000    0.0    0.0    0.0   
4      0.0  0.000000  0.000000    0.0    0.0  0.625000    0.0    0.0    0.0   
..     ...       ...       ...    ...    ...       ...    ...    ...    ...   
124    0.0  0.666667  0.629412    0.0    0.0  0.000000    0.0    1.0    1.0   
125    0.1  0.888889  0.729412    0.0    0.0  0.000000    0.0    1.0    1.0   
126    0.0  0.222222  0.800000    0.0    1.0  0.000000    0.0    1.0    1.0   
127    0.0  0.333333  0.835294    0.0    0.0  0.000000    0.0    1.0    1.0   
128    0.0  0.666667  0.370588    0.0    1.0  0.000000    0.0    1.0    1.0   

     X_255  ...    X_2860    X_2861    X_2862    X_2863    X_2864  X_2865  \
0      0.0  ...  0.526316  0.601597  0.503534  0.270270  0.345174   0.475   
1      0.0  ...  0.415789  0.478605  0.464664  0.270270  0.332216   0.475   
2      0.0  ...  0.563158  0.577864  0.597173  0.297297  0.287449   0.325   
3      0.0  ...  0.698246  0.679636  0.646643  0.270270  0.304180   0.475   
4      0.0  ...  0.533333  0.518925  0.545936  0.270270  0.325736   0.300   
..     ...  ...       ...       ...       ...       ...       ...     ...   
124    0.0  ...  0.549123  0.503225  0.392226  0.540541  0.607884   0.475   
125    0.0  ...  0.624561  0.742582  0.761484  0.810811  0.831899   0.775   
126    0.0  ...  0.652632  0.734162  0.719081  0.810811  0.810285   0.725   
127    0.0  ...  0.712281  0.800842  0.727915  0.810811  0.854712   0.825   
128    0.0  ...  0.705263  0.842469  0.789753  0.972973  0.988990   0.950   

         HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0    0.869565  0.440678     1.000000            0.0  
1    0.304348  0.237288     0.166667            0.0  
2    0.173913  0.762712     0.333333            0.0  
3    0.521739  0.440678     0.333333            0.0  
4    0.521739  0.576271     0.333333            0.0  
..        ...       ...          ...            ...  
124  0.652174  0.474576     0.166667            1.0  
125  0.652174  0.983051     0.666667            1.0  
126  0.434783  0.661017     1.000000            1.0  
127  0.652174  0.644068     0.000000            1.0  
128  0.478261  0.288136     0.000000            1.0  

[129 rows x 882 columns]

In [186]:
TT01c = TT01.columns
TT01scaled = T_01scaler.transform(TT01)
TT01 = pd.DataFrame(TT01scaled, columns = TT01c)
TT01

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
0     0.0  0.666667  0.000000    0.0    0.0  0.220238    0.0    0.0    0.0   
1     0.0  0.666667  0.000000    0.0    0.0  0.238095    0.0    0.0    0.0   
2     0.0  0.333333  0.000000    0.0    0.0  0.273810    0.0    0.0    0.0   
3     0.0  0.888889  0.000000    0.0    0.0  0.315476    0.0    0.0    0.0   
4     0.1  0.111111  0.000000    0.0    0.0  0.797619    0.0    0.0    0.0   
5     0.1  0.666667  0.000000    0.0    0.0  0.839286    0.0    0.0    0.0   
6     0.1  0.222222  0.000000    0.0    0.0  0.035714    0.0    0.0    0.0   
7     0.0  0.222222  0.000000    0.0    0.0  0.136905    0.0    0.0    0.0   
8     1.6  0.333333  0.000000    0.0    0.0  0.136905    0.0    0.0    0.0   
9     0.1  0.222222  0.000000    0.0    0.0  0.136905    0.0    0.0    0.0   
10    0.1  0.333333  0.000000    0.0    0.0  0.255952    0.0    0.0    0.0   
11    0.0  0.111111  0.000000    0.0    0.0  0.255952    0.0    0.0    0.0   
12    0.0  0.111111  0.000000    0.0    0.0  0.410714    0.0    0.0    0.0   
13    0.1  0.000000  0.000000    0.0    0.0  0.410714    0.0    1.0    0.0   
14    0.1  0.888889  0.523529    0.0    1.0  0.000000    0.0    1.0    1.0   
15    0.1  0.333333  0.541176    0.0    1.0  0.000000    0.0    1.0    1.0   
16    0.0  0.222222  0.576471    0.0    0.0  0.000000    0.0    1.0    1.0   
17    0.1  0.222222  0.617647    0.0    0.0  0.000000    0.0    1.0    1.0   
18    0.0  0.777778  0.082353    0.0    1.0  0.000000    0.0    1.0    1.0   
19    0.1  0.444444  0.123529    0.0    1.0  0.000000    0.0    1.0    1.0   
20    0.1  1.111111  0.517647    0.0    1.0  0.000000    0.0    1.0    1.0   
21    0.0  0.333333  0.547059    0.0    1.0  0.000000    0.0    1.0    1.0   
22    0.0  0.555556  0.652941    0.0    1.0  0.000000    0.0    1.0    1.0   
23    0.3  1.111111  0.747059    0.0    1.0  0.000000    0.0    1.0    1.0   
24    0.0  0.888889  0.764706    0.0    1.0  0.000000    0.0    1.0    1.0   
25    0.1  0.666667  0.764706    0.0    1.0  0.000000    0.0    1.0    1.0   
26    0.0  0.888889  0.841176    0.0    1.0  0.000000    0.0    1.0    1.0   
27    0.1  0.666667  0.841176    0.0    1.0  0.000000    0.0    1.0    1.0   

    X_255  ...    X_2860    X_2861    X_2862    X_2863    X_2864  X_2865  \
0     0.0  ...  0.807018  0.919536  0.915194  0.837838  0.797077   0.725   
1     0.0  ...  0.868421  0.974705  0.761484  0.756757  0.824649   0.725   
2     0.0  ...  0.817544  0.889183  0.749117  0.810811  0.794676   0.725   
3     0.0  ...  0.791228  0.841787  0.779152  0.810811  0.798278   0.700   
4     0.0  ...  0.759649  0.847189  0.849823  0.702703  0.914771   0.700   
5     0.0  ...  0.915789  1.034759  0.948763  0.810811  0.997825   0.950   
6     0.0  ...  0.884211  1.022761  0.973498  0.783784  0.815813   0.725   
7     0.0  ...  0.884211  1.017320  0.846290  0.810811  0.931264   0.975   
8     0.0  ...  1.308772  1.407075  1.312721  0.810811  0.743645   0.725   
9     0.0  ...  0.873684  1.040062  0.924028  0.783784  0.844506   0.800   
10    0.0  ...  0.866667  0.965913  0.895760  0.810811  0.879327   0.800   
11    0.0  ...  0.943860  1.000405  1.007067  0.540541  0.690938   0.700   
12    0.0  ...  0.938596  1.024073  1.031802  0.810811  0.809334   0.725   
13    0.0  ...  1.114035  1.185170  1.125442  0.810811  0.929157   0.725   
14    0.0  ...  1.021053  0.950567  0.842756  0.783784  0.766459   0.725   
15    0.0  ...  0.900000  0.937139  0.878092  0.810811  0.723335   0.700   
16    0.0  ...  0.789474  0.937598  0.927562  0.540541  0.653591   0.725   
17    0.0  ...  0.791228  0.911045  0.957597  0.810811  0.954237   0.950   
18    0.0  ...  0.794737  0.835472  0.720848  0.810811  0.834300   0.700   
19    0.0  ...  0.961404  1.060197  0.971731  1.054054  1.132125   0.950   
20    0.0  ...  0.949123  1.035939  0.832155  0.810811  0.766334   0.725   
21    0.0  ...  0.901754  0.996930  1.049470  0.783784  0.834073   0.

In [187]:
TT01 = pd.concat([TT01_idx, TT01], axis = 1)
TT01 = TT01.set_index('index')
TT01

X_246     X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
index                                                                           
3        0.0  0.666667  0.000000    0.0    0.0  0.220238    0.0    0.0    0.0   
6        0.0  0.666667  0.000000    0.0    0.0  0.238095    0.0    0.0    0.0   
10       0.0  0.333333  0.000000    0.0    0.0  0.273810    0.0    0.0    0.0   
11       0.0  0.888889  0.000000    0.0    0.0  0.315476    0.0    0.0    0.0   
38       0.1  0.111111  0.000000    0.0    0.0  0.797619    0.0    0.0    0.0   
40       0.1  0.666667  0.000000    0.0    0.0  0.839286    0.0    0.0    0.0   
71       0.1  0.222222  0.000000    0.0    0.0  0.035714    0.0    0.0    0.0   
86       0.0  0.222222  0.000000    0.0    0.0  0.136905    0.0    0.0    0.0   
88       1.6  0.333333  0.000000    0.0    0.0  0.136905    0.0    0.0    0.0   
89       0.1  0.222222  0.000000    0.0    0.0  0.136905    0.0    0.0    0.0   
116      0.1  0.333333  0.000000    0.0    0.0  0.255952    0.0    0.0    0.0   
117      0.0  0.111111  0.000000    0.0    0.0  0.255952    0.0    0.0    0.0   
141      0.0  0.111111  0.000000    0.0    0.0  0.410714    0.0    0.0    0.0   
142      0.1  0.000000  0.000000    0.0    0.0  0.410714    0.0    1.0    0.0   
4        0.1  0.888889  0.523529    0.0    1.0  0.000000    0.0    1.0    1.0   
5        0.1  0.333333  0.541176    0.0    1.0  0.000000    0.0    1.0    1.0   
9        0.0  0.222222  0.576471    0.0    0.0  0.000000    0.0    1.0    1.0   
12       0.1  0.222222  0.617647    0.0    0.0  0.000000    0.0    1.0    1.0   
37       0.0  0.777778  0.082353    0.0    1.0  0.000000    0.0    1.0    1.0   
39       0.1  0.444444  0.123529    0.0    1.0  0.000000    0.0    1.0    1.0   
72       0.1  1.111111  0.517647    0.0    1.0  0.000000    0.0    1.0    1.0   
79       0.0  0.333333  0.547059    0.0    1.0  0.000000    0.0    1.0    1.0   
87       0.0  0.555556  0.652941    0.0    1.0  0.000000    0.0    1.0    1.0   
109      0.3  1.111111  0.747059    0.0    1.0  0.000000    0.0    1.0    1.0   
114      0.0  0.888889  0.764706    0.0    1.0  0.000000    0.0    1.0    1.0   
115      0.1  0.666667  0.764706    0.0    1.0  0.000000    0.0    1.0    1.0   
128      0.0  0.888889  0.841176    0.0    1.0  0.000000    0.0    1.0    1.0   
129      0.1  0.666667  0.841176    0.0    1.0  0.000000    0.0    1.0    1.0   

       X_255  ...    X_2860    X_2861    X_2862    X_2863    X_2864  X_2865  \
index         ...                                                             
3        0.0  ...  0.807018  0.919536  0.915194  0.837838  0.797077   0.725   
6        0.0  ...  0.868421  0.974705  0.761484  0.756757  0.824649   0.725   
10       0.0  ...  0.817544  0.889183  0.749117  0.810811  0.794676   0.725   
11       0.0  ...  0.791228  0.841787  0.779152  0.810811  0.798278   0.700   
38       0.0  ...  0.759649  0.847189  0.849823  0.702703  0.914771   0.700   
40       0.0  ...  0.915789  1.034759  0.948763  0.810811  0.997825   0.950   
71       0.0  ...  0.884211  1.022761  0.973498  0.783784  0.815813   0.725   
86       0.0  ...  0.884211  1.017320  0.846290  0.810811  0.931264   0.975   
88       0.0  ...  1.308772  1.407075  1.312721  0.810811  0.743645   0.725   
89       0.0  ...  0.873684  1.040062  0.924028  0.783784  0.844506   0.800   
116      0.0  ...  0.866667  0.965913  0.895760  0.810811  0.879327   0.800   
117      0.0  ...  0.943860  1.000405  1.007067  0.540541  0.690938   0.700   
141      0.0  ...  0.938596  1.024073  1.031802  0.810811  0.809334   0.725   
142      0.0  ...  1.114035  1.185170  1.125442  0.810811  0.929157   0.725   
4        0.0  ...  1.021053  0.950567  0.842756  0.783784  0.766459   0.725   
5        0.0  ...  0.900000  0.937139  0.878092  0.810811  0.723335   0.700   
9        0.0  ...  0.789474  0.937598  0.927562  0.540541  0.653591   0.725   
12       0.0  ...  0.791228  0.911045  0.957597  0.810811  0.954237   0.950

# Test T10

In [188]:
TT10_idx = TT10['PRODUCT_CODE'].index
TT10_idx = pd.DataFrame(TT10_idx, columns = ['index'])
TT10_idx

index
0        1
1        2
2       15
3       17
4       20
..     ...
238    301
239    305
240    307
241    308
242    309

[243 rows x 1 columns]

In [189]:
TT10.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [190]:
T_10c = T10_data.columns
T_10scaler = MinMaxScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)
T10_data

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
0    0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
1    0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
2    0.009804  0.666667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
3    0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
4    0.009804  0.866667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
..        ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
344  0.000000  0.466667  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
345  0.000000  0.133333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
346  0.000000  0.000000  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
347  0.009804  0.533333  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
348  0.196078  0.000000  0.0  0.0  0.0  0.0  0.941176  0.0  1.0   0.0  ...   

        X_928     X_929     X_930     X_931     X_932     X_933      HOUR  \
0    0.996942  0.984433  0.969900  0.992754  0.991153  0.992481  0.347826   
1    0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.391304   
2    1.000000  0.989410  0.996656  0.992754  0.992001  0.992481  0.391304   
3    1.000000  0.993403  0.996656  0.992754  0.989623  0.992481  1.000000   
4    1.000000  0.993866  0.996656  0.992754  0.992136  1.000000  0.130435   
..        ...       ...       ...       ...       ...       ...       ...   
344  0.996942  0.990741  0.996656  0.992754  0.994141  1.000000  0.782609   
345  1.000000  0.997512  1.000000  0.985507  0.987482  0.992481  0.043478   
346  0.996942  0.997743  0.996656  0.985507  0.987958  0.992481  0.043478   
347  1.000000  0.997396  0.996656  0.985507  0.984390  0.992481  0.608696   
348  0.996942  0.970197  0.966555  0.985507  0.986483  0.992481  0.608696   

       MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0    0.898305     0.166667       0.000000  
1    0.016949     0.166667       0.000000  
2    0.186441     1.000000       0.000000  
3    0.525424     1.000000       0.000000  
4    0.796610     0.333333       0.000000  
..        ...          ...            ...  
344  0.000000     0.166667       0.142857  
345  0.016949     0.333333       0.142857  
346  0.152542     0.333333       0.142857  
347  0.508475     0.500000       0.142857  
348  0.779661     0.500000       1.000000  

[349 rows x 669 columns]

In [191]:
TT10c = TT10.columns
TT10scaled = T_10scaler.transform(TT10)
TT10 = pd.DataFrame(TT10scaled, columns = TT10c)
TT10

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
0    0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
1    0.009804  0.533333  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
2    0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
3    0.009804  0.533333  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
4    0.009804  0.466667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
..        ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
238  0.009804  0.466667  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
239  0.009804  0.266667  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
240  0.009804  0.266667  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
241  0.009804  0.533333  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
242  0.009804  0.000000  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   

        X_928     X_929     X_930     X_931     X_932     X_933      HOUR  \
0    1.000000  0.994965  0.996656  0.985507  0.988433  0.992481  0.086957   
1    0.996942  0.975000  0.966555  0.985507  0.985817  0.992481  0.347826   
2    0.969419  0.965856  0.966555  0.985507  0.987006  0.992481  0.217391   
3    0.996942  0.987095  0.966555  0.992754  0.988196  0.992481  1.000000   
4    0.969419  0.967130  0.966555  0.985507  0.988203  0.992481  0.043478   
..        ...       ...       ...       ...       ...       ...       ...   
238  1.000000  0.995428  0.996656  0.985507  0.986531  0.992481  0.652174   
239  0.996942  0.996470  0.983278  0.985507  0.983677  0.992481  0.478261   
240  0.987768  0.968924  0.966555  0.985507  0.985104  0.992481  0.695652   
241  0.996942  0.977199  0.969900  0.985507  0.983201  0.992481  0.869565   
242  1.000000  0.980845  0.966555  0.985507  0.983780  0.992481  0.913043   

       MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0    0.152542     0.666667       0.000000  
1    0.711864     0.666667       0.000000  
2    0.338983     0.166667       0.000000  
3    0.762712     0.500000       0.000000  
4    0.779661     0.666667       0.000000  
..        ...          ...            ...  
238  0.305085     0.666667       0.142857  
239  0.305085     0.833333       0.142857  
240  0.796610     0.833333       0.142857  
241  0.898305     0.833333       0.142857  
242  0.016949     0.833333       0.142857  

[243 rows x 669 columns]

In [192]:
TT10 = pd.concat([TT10_idx, TT10], axis = 1)
TT10 = TT10.set_index('index')
TT10

X_1       X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
index                                                                    ...   
1      0.009804  0.400000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
2      0.009804  0.533333  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
15     0.009804  1.000000  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
17     0.009804  0.533333  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
20     0.009804  0.466667  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
...         ...       ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
301    0.009804  0.466667  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
305    0.009804  0.266667  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
307    0.009804  0.266667  0.0  0.0  0.0  0.0  0.294118  0.0  1.0   0.0  ...   
308    0.009804  0.533333  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   
309    0.009804  0.000000  0.0  0.0  0.0  0.0  0.352941  0.0  1.0   0.0  ...   

          X_928     X_929     X_930     X_931     X_932     X_933      HOUR  \
index                                                                         
1      1.000000  0.994965  0.996656  0.985507  0.988433  0.992481  0.086957   
2      0.996942  0.975000  0.966555  0.985507  0.985817  0.992481  0.347826   
15     0.969419  0.965856  0.966555  0.985507  0.987006  0.992481  0.217391   
17     0.996942  0.987095  0.966555  0.992754  0.988196  0.992481  1.000000   
20     0.969419  0.967130  0.966555  0.985507  0.988203  0.992481  0.043478   
...         ...       ...       ...       ...       ...       ...       ...   
301    1.000000  0.995428  0.996656  0.985507  0.986531  0.992481  0.652174   
305    0.996942  0.996470  0.983278  0.985507  0.983677  0.992481  0.478261   
307    0.987768  0.968924  0.966555  0.985507  0.985104  0.992481  0.695652   
308    0.996942  0.977199  0.969900  0.985507  0.983201  0.992481  0.869565   
309    1.000000  0.980845  0.966555  0.985507  0.983780  0.992481  0.913043   

         MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
index                                        
1      0.152542     0.666667       0.000000  
2      0.711864     0.666667       0.000000  
15     0.338983     0.166667       0.000000  
17     0.762712     0.500000       0.000000  
20     0.779661     0.666667       0.000000  
...         ...          ...            ...  
301    0.305085     0.666667       0.142857  
305    0.305085     0.833333       0.142857  
307    0.796610     0.833333       0.142857  
308    0.898305     0.833333       0.142857  
309    0.016949     0.833333       0.142857  

[243 rows x 669 columns]

# Test Model

In [193]:
from pycaret.regression import *
TT05_prediction = predict_model(T05_final_regression_model, data=TT05)
TT01_prediction = predict_model(T01_final_regression_model, data=TT01)
TT10_prediction = predict_model(T10_final_regression_model, data=TT10)

In [194]:
TT05_y_class = pd.DataFrame(TT05, columns = ['PRODUCT_CODE'])
TT05_idx = TT05_y_class.index
TT05_y_class = TT05_y_class.reset_index()
TT05_prediction = pd.concat([TT05_prediction, TT05_y_class], axis = 1)
TT05_prediction = TT05_prediction.set_index('index')
TT05_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)
TT05_prediction

X_132  X_133  X_134  X_135  X_136  X_137  X_138       X_139  \
index                                                                
7       0.19   0.20   0.19    0.2  354.0  354.0  354.0  591.500000   
8       0.19   0.20   0.19    0.2  355.0  354.0  355.0  591.500000   
14      0.19   0.21   0.19    0.2   60.0   60.0   60.0  558.400024   
35      0.20   0.21   0.20    0.2  249.0  249.0  249.0  583.099976   
41      0.20   0.21   0.20    0.2  293.0  293.0  293.0  580.900024   
42      0.20   0.21   0.19    0.2  293.0  293.0  293.0  581.000000   
52      0.19   0.21   0.19    0.2  330.0  330.0  330.0  582.900024   
53      0.20   0.21   0.20    0.2  330.0  330.0  330.0  583.400024   
54      0.19   0.21   0.19    0.2  330.0  330.0  330.0  583.000000   
61      0.20   0.21   0.20    0.2  436.0  436.0  436.0  592.099976   
64      0.20   0.21   0.20    0.2  437.0  437.0  437.0  593.700012   
65      0.20   0.21   0.20    0.2  441.0  441.0  441.0  593.799988   
66      0.20   0.21   0.20    0.2  446.0  446.0  446.0  593.200012   
13      0.21   0.22   0.21    0.2  230.0  230.0  231.0  580.599976   
36      0.21   0.22   0.21    0.2   99.0   99.0   99.0  581.500000   
62      0.21   0.22   0.21    0.2   50.0   49.0   40.0  578.599976   
63      0.21   0.22   0.21    0.2   52.0   51.0   41.0  580.500000   
130     0.21   0.22   0.20    0.2  424.0  423.0  413.0  585.700012   
131     0.21   0.21   0.21    0.2  424.0  423.0  414.0  584.400024   
132     0.21   0.22   0.21    0.2  426.0  425.0  416.0  584.200012   
248     0.21   0.22   0.21    0.2  732.0  731.0  722.0  595.500000   
249     0.21   0.22   0.21    0.2  732.0  731.0  722.0  594.799988   
250     0.21   0.22   0.21    0.2  733.0  732.0  722.0  594.000000   
251     0.21   0.22   0.21    0.2  733.0  732.0  722.0  594.099976   
252     0.21   0.22   0.21    0.2  733.0  732.0  722.0  593.900024   
253     0.21   0.22   0.21    0.2  733.0  732.0  723.0  594.000000   
254     0.21   0.22   0.21    0.2  737.0  736.0  727.0  594.400024   
255     0.21   0.22   0.21    0.2  738.0  737.0  727.0  594.599976   
260     0.21   0.22   0.20    0.2  738.0  737.0  728.0  595.700012   
263     0.20   0.22   0.20    0.2  741.0  740.0  730.0  597.000000   
280     0.21   0.22   0.21    0.2  789.0  788.0  779.0  602.099976   
281     0.21   0.22   0.21    0.2  790.0  789.0  779.0  600.700012   
282     0.21   0.22   0.21    0.2  800.0  799.0  789.0  599.700012   
283     0.21   0.22   0.21    0.2  800.0  799.0  790.0  599.400024   
284     0.21   0.22   0.21    0.2  806.0  805.0  796.0  599.400024   
285     0.21   0.22   0.21    0.2  806.0  805.0  796.0  599.599976   
286     0.21   0.22   0.21    0.2  807.0  806.0  796.0  599.599976   
292     0.21   0.22   0.21    0.2  821.0  820.0  810.0  601.500000   
293     0.21   0.22   0.21    0.2  821.0  820.0  811.0  601.400024   

            X_140       X_141  ...     X_2867     X_2868     X_2869  \
index                          ...                                    
7      597.700012  575.599976  ...  52.509998  54.450001  57.990002   
8      597.700012  575.700012  ...  56.020000  41.790001  47.939999   
14     561.900024  547.500000  ...  54.930000  49.849998  48.619999   
35     587.099976  569.900024  ...  58.139999  48.930000  56.160000   
41     585.099976  570.400024  ...  45.000000  49.810001  55.189999   
42     585.200012  568.900024  ...  47.660000  60.000000  53.750000   
52     587.900024  542.400024  ...  51.180000  52.169998  57.750000   
53     588.000000  563.900024  ...  51.250000  54.980000  57.220001   
54     587.799988  570.400024  ...  57.570000  42.080002  55.189999   
61     597.900024  580.799988  ...   0.000000   0.000000   0.000000   
64     599.400024  580.099976  ...   0.000000   0.000000   0.000000   
65     599.700012  574.599976  ...  55.549999  39.849998  47.820000   
66     599.000000  583.900024  ...  55.700001  52.490002  48.340000   
13     584.099976  562.000000  ...  55.250000  50.139999  57.080002   


In [195]:
TT01_y_class = pd.DataFrame(TT01, columns = ['PRODUCT_CODE'])
TT01_idx = TT01_y_class.index
TT01_y_class = TT01_y_class.reset_index()
TT01_prediction = pd.concat([TT01_prediction, TT01_y_class], axis = 1)
TT01_prediction = TT01_prediction.set_index('index')
TT01_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [196]:
TT10_y_class = pd.DataFrame(TT10, columns = ['PRODUCT_CODE'])
TT10_idx = TT10_y_class.index
TT10_y_class = TT10_y_class.reset_index()
TT10_prediction = pd.concat([TT10_prediction, TT10_y_class], axis = 1)
TT10_prediction = TT10_prediction.set_index('index')
TT10_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [197]:
from pycaret.classification import *

In [198]:
TT05_datas = TT05_prediction['prediction_label']
TT05_datas = pd.DataFrame(TT05_datas.values, columns = ['Y_Quality'])
TT05_datas

Y_Quality
0    0.533285
1    0.533115
2    0.533229
3    0.534128
4    0.533936
5    0.533080
6    0.533226
7    0.533047
8    0.533859
9    0.533231
10   0.534131
11   0.533159
12   0.533443
13   0.533267
14   0.533778
15   0.533342
16   0.534234
17   0.533877
18   0.533213
19   0.533397
20   0.533125
21   0.534179
22   0.533334
23   0.533315
24   0.533282
25   0.533931
26   0.533383
27   0.533159
28   0.533272
29   0.533231
30   0.533041
31   0.533168
32   0.533286
33   0.533170
34   0.534040
35   0.533191
36   0.533235
37   0.533481
38   0.533254

In [199]:
TT05y_idx= TT05_prediction.index
TT05y_idx = pd.DataFrame(TT05y_idx, columns = ['index'])
TT05_datas = pd.concat([TT05y_idx, TT05_datas], axis = 1)
TT05_datas = TT05_datas.set_index('index')
TT05_datas

Y_Quality
index           
7       0.533285
8       0.533115
14      0.533229
35      0.534128
41      0.533936
42      0.533080
52      0.533226
53      0.533047
54      0.533859
61      0.533231
64      0.534131
65      0.533159
66      0.533443
13      0.533267
36      0.533778
62      0.533342
63      0.534234
130     0.533877
131     0.533213
132     0.533397
248     0.533125
249     0.534179
250     0.533334
251     0.533315
252     0.533282
253     0.533931
254     0.533383
255     0.533159
260     0.533272
263     0.533231
280     0.533041
281     0.533168
282     0.533286
283     0.533170
284     0.534040
285     0.533191
286     0.533235
292     0.533481
293     0.533254

In [200]:
TT01_datas = TT01_prediction['prediction_label']
TT01_datas = pd.DataFrame(TT01_datas.values, columns = ['Y_Quality'])
TT01_datas

Y_Quality
0    0.524860
1    0.529291
2    0.529065
3    0.532480
4    0.553090
5    0.531949
6    0.515626
7    0.515094
8    0.515913
9    0.524865
10   0.525199
11   0.525049
12   0.524413
13   0.525436
14   0.530238
15   0.533449
16   0.534902
17   0.536761
18   0.515608
19   0.524069
20   0.529043
21   0.531727
22   0.531300
23   0.533837
24   0.533733
25   0.533724
26   0.530506
27   0.530448

In [201]:
TT01y_idx= TT01_prediction.index
TT01y_idx = pd.DataFrame(TT01y_idx, columns = ['index'])
TT01_datas = pd.concat([TT01y_idx, TT01_datas], axis = 1)
TT01_datas = TT01_datas.set_index('index')
TT01_datas

Y_Quality
index           
3       0.524860
6       0.529291
10      0.529065
11      0.532480
38      0.553090
40      0.531949
71      0.515626
86      0.515094
88      0.515913
89      0.524865
116     0.525199
117     0.525049
141     0.524413
142     0.525436
4       0.530238
5       0.533449
9       0.534902
12      0.536761
37      0.515608
39      0.524069
72      0.529043
79      0.531727
87      0.531300
109     0.533837
114     0.533733
115     0.533724
128     0.530506
129     0.530448

In [202]:
TT10_datas = TT10_prediction['prediction_label']
TT10_datas = pd.DataFrame(TT10_datas.values, columns = ['Y_Quality'])
TT10_datas

Y_Quality
0     0.531926
1     0.531223
2     0.525385
3     0.528551
4     0.528389
..         ...
238   0.528942
239   0.528631
240   0.530156
241   0.529574
242   0.529494

[243 rows x 1 columns]

In [203]:
TT10y_idx= TT10_prediction.index
TT10y_idx = pd.DataFrame(TT10y_idx, columns = ['index'])
TT10_datas = pd.concat([TT10y_idx, TT10_datas], axis = 1)
TT10_datas = TT10_datas.set_index('index')
TT10_datas

Y_Quality
index           
1       0.531926
2       0.531223
15      0.525385
17      0.528551
20      0.528389
...          ...
301     0.528942
305     0.528631
307     0.530156
308     0.529574
309     0.529494

[243 rows x 1 columns]

In [204]:
TT05_predictions = predict_model(T05_final_classification_model, data=TT05_datas)
TT01_predictions = predict_model(T01_final_classification_model, data=TT01_datas)
TT10_predictions = predict_model(T10_final_classification_model, data=TT10_datas)

In [205]:
TT05_idxf = TT05_datas.index
TT05_p = pd.DataFrame(TT05_idxf, columns = ['index'])
TT05_predictions = pd.concat([TT05_p, TT05_predictions], axis = 1)
TT05_predictions = TT05_predictions.set_index('index')
TT05_predictions

Y_Quality  prediction_label  prediction_score
index                                               
7       0.533285                 1             0.999
8       0.533115                 1             0.999
14      0.533229                 1             0.999
35      0.534128                 1             0.999
41      0.533936                 1             0.999
42      0.533080                 1             0.999
52      0.533226                 1             0.999
53      0.533047                 1             0.999
54      0.533859                 1             0.999
61      0.533231                 1             0.999
64      0.534131                 1             0.999
65      0.533159                 1             0.999
66      0.533443                 1             0.999
13      0.533267                 1             0.999
36      0.533778                 1             0.999
62      0.533342                 1             0.999
63      0.534234                 1             0.999
130     0.533877                 1             0.999
131     0.533213                 1             0.999
132     0.533397                 1             0.999
248     0.533125                 1             0.999
249     0.534179                 1             0.999
250     0.533334                 1             0.999
251     0.533315                 1             0.999
252     0.533282                 1             0.999
253     0.533931                 1             0.999
254     0.533383                 1             0.999
255     0.533159                 1             0.999
260     0.533272                 1             0.999
263     0.533231                 1             0.999
280     0.533041                 1             0.999
281     0.533168                 1             0.999
282     0.533286                 1             0.999
283     0.533170                 1             0.999
284     0.534039                 1             0.999
285     0.533191                 1             0.999
286     0.533235                 1             0.999
292     0.533481                 1             0.999
293     0.533254                 1             0.999

In [206]:
TT01_idxf = TT01_datas.index
TT01_p = pd.DataFrame(TT01_idxf, columns = ['index'])
TT01_predictions = pd.concat([TT01_p, TT01_predictions], axis = 1)
TT01_predictions = TT01_predictions.set_index('index')
TT01_predictions

Y_Quality  prediction_label  prediction_score
index                                               
3       0.524859                 1            0.6627
6       0.529291                 1            0.9990
10      0.529065                 1            0.9990
11      0.532480                 1            0.9990
38      0.553090                 2            0.9968
40      0.531949                 1            0.9990
71      0.515626                 0            0.9968
86      0.515094                 0            0.9968
88      0.515913                 0            0.9968
89      0.524865                 1            0.6627
116     0.525199                 1            0.6627
117     0.525049                 1            0.6627
141     0.524413                 0            0.9968
142     0.525436                 1            0.6627
4       0.530238                 1            0.9990
5       0.533449                 1            0.9986
9       0.534902                 2            0.6816
12      0.536761                 2            0.9968
37      0.515608                 0            0.9968
39      0.524069                 0            0.9968
72      0.529043                 1            0.9990
79      0.531727                 1            0.9990
87      0.531300                 1            0.9990
109     0.533837                 1            0.9986
114     0.533733                 1            0.9986
115     0.533724                 1            0.9986
128     0.530506                 1            0.9990
129     0.530448                 1            0.9990

In [207]:
TT10_idxf = TT10_datas.index
TT10_p = pd.DataFrame(TT10_idxf, columns = ['index'])
TT10_predictions = pd.concat([TT10_p, TT10_predictions], axis = 1)
TT10_predictions = TT10_predictions.set_index('index')
TT10_predictions

Y_Quality  prediction_label  prediction_score
index                                               
1       0.531926                 1            0.9994
2       0.531223                 1            0.9994
15      0.525385                 1            0.9887
17      0.528551                 1            0.9994
20      0.528389                 1            0.9994
...          ...               ...               ...
301     0.528942                 1            0.9994
305     0.528631                 1            0.9994
307     0.530156                 1            0.9994
308     0.529574                 1            0.9994
309     0.529494                 1            0.9994

[243 rows x 3 columns]

In [208]:
final_test = pd.concat([TT05_predictions, TT01_predictions, TT10_predictions])
final_test

Y_Quality  prediction_label  prediction_score
index                                               
7       0.533285                 1            0.9990
8       0.533115                 1            0.9990
14      0.533229                 1            0.9990
35      0.534128                 1            0.9990
41      0.533936                 1            0.9990
...          ...               ...               ...
301     0.528942                 1            0.9994
305     0.528631                 1            0.9994
307     0.530156                 1            0.9994
308     0.529574                 1            0.9994
309     0.529494                 1            0.9994

[310 rows x 3 columns]

In [209]:
final_test = final_test.sort_index(ascending=True)
final_test['prediction_label']

index
0      1
1      1
2      1
3      1
4      1
      ..
305    1
306    1
307    1
308    1
309    1
Name: prediction_label, Length: 310, dtype: int32

In [210]:
#52
sample_submission = pd.read_csv('sample_submission.csv')
sample_submission['Y_Class'] = final_test['prediction_label']
display(sample_submission.head())
sample_submission.to_csv('line3_otherdrop_minmax_regpyc_classpyc_fill0_oth_submission.csv',index=False)

PRODUCT_ID  Y_Class
0   TEST_000        1
1   TEST_001        1
2   TEST_002        1
3   TEST_003        1
4   TEST_004        1

In [211]:
final_test['prediction_label'].value_counts()

1    277
2     22
0     11
Name: prediction_label, dtype: int64

In [212]:
np.array(final_test['prediction_label'])

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 2, 0, 1, 1, 1, 1,
       1, 1, 1, 0, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 0, 1,
       0, 1, 2, 1, 2, 2, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1,
       1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1,
       1, 1, 2, 2, 1, 2, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 2, 2, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1,
       1, 1, 1, 2, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,